# GT Educação

O GT Educação enviou uma série de formulários com indicadores desejados para o painel. A maioria desses indicadores estão disponíveis no Portal de Dados Abertos da Prefeitura de São Paulo (http://dados.prefeitura.sp.gov.br/).

Portanto, vamos carregar o módulo de downloads do portal de dados abertos.

In [1]:
import os
import pandas as pd
from xlrd import xldate
from unidecode import unidecode
from dotenv import load_dotenv
import requests, zipfile
from io import BytesIO

from core.downloads import dadosabertos as da
from core.downloads import geosampa as gs

In [2]:
load_dotenv()

True

# Extração e transformação inicial

## Número de alunos da Rede Municipal de Ensino

O primeiro indicador é o número de alunos da rede municipal, segmentado por nível educacional (Creche, Pré Escola, Ensino Fundamental I, Ensino Fundamental II, EJA I, EJA II, Ensino Médio, Ed. Prof.).

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/demanda-e-matriculas. Sabendo que o último trecho da url representa a id do conjunto de dados, vamos utilizá-la para fazer a extração dos dados do portal.

Primeiro, precisamos visualizar todos os recursos relativos a esse conjunto de dados. Nesse momento, podemos pegar todos os conjuntos em dezembro de 2024.

In [3]:
pkg_name = 'demanda-e-matriculas'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Demanda e Matrículas - Dez/2024',
  'id': '23081b4e-7866-4c3e-843b-489354c00a3e',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/45612acc-edd3-4134-ac7f-9a0026f60c97/resource/23081b4e-7866-4c3e-843b-489354c00a3e/download/publicacao-demanda-e-matriculas-dez-2024.xls'},
 {'name': 'Demanda e Matrículas - Dez/2024',
  'id': '8afd9653-8977-486e-928e-ae0dd5cff21c',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/45612acc-edd3-4134-ac7f-9a0026f60c97/resource/8afd9653-8977-486e-928e-ae0dd5cff21c/download/publicacao-demanda-e-matriculas-dez-2024.csv'},
 {'name': 'Demanda e Matrículas - Out/2024',
  'id': '08856956-7c46-4dd1-ad3b-e1b7f0d4ab25',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/45612acc-edd3-4134-ac7f-9a0026f60c97/resource/08856956-7c46-4dd1-ad3b-e1b7f0d4ab25/download/publicacao-demanda-e-matricula-out-2024.xls'},
 {'name': 'Demanda e Matrículas - Out/2024',
  'id': '7b5c0318-23ea-4cc8-9c3b-7936f00a340a',
  'url': 'https://dados.prefeitura.sp.gov.br/datas

Sabendo o id do arquivo de dezembro de 2023, vamos carregar o recurso como um dataframe.

In [4]:
resource_id = '23081b4e-7866-4c3e-843b-489354c00a3e'
mat_24 = da.load_resource(resource_id, pandas_kwargs=dict(header=[0,1]))
mat_24

Distrito Matrículas             \
                                   Unnamed: 0_level_1     Creche Pré Escola   
0                                          AGUA RASA      1264.0      724.0   
1                                  ALTO DE PINHEIROS       273.0        0.0   
2                                         ANHANGUERA      2912.0     1690.0   
3                                         ARICANDUVA      1542.0      699.0   
4                                        ARTUR ALVIM      2711.0     2138.0   
..                                                ...        ...        ...   
95                                        VILA SONIA      3609.0     1853.0   
96                                              TOTAL   345019.0   216107.0   
97                                                NaN        NaN        NaN   
98  (2) - Demanda sem opção por unidade específica...        NaN        NaN   
99     (3) - Demanda com opção por unidade específica        NaN        NaN   

                                                                   \
   Ens. Fund.I Ens. Fund.II   EJA I   EJA II Ens. Médio Ed. Prof.   
0        967.0        932.0     0.0     23.0        0.0       0.0   
1          0.0          0.0     0.0      0.0        0.0       0.0   
2       3650.0       2430.0    24.0    130.0        0.0       0.0   
3       1217.0       1085.0     0.0     58.0        0.0       0.0   
4       2355.0       2128.0     0.0     21.0        0.0       0.0   
..         ...          ...     ...      ...        ...       ...   
95      2435.0       1611.0     0.0     15.0        0.0       0.0   
96    251032.0     183303.0  3591.0  13443.0     2076.0    1213.0   
97         NaN          NaN     NaN      NaN        NaN       NaN   
98         NaN          NaN     NaN      NaN        NaN       NaN   
99         NaN          NaN     NaN      NaN        NaN       NaN   

   Matrícula em Processo  ...    Demanda                              \
                  Creche  ... Creche (3) Creche Total Pré Escola (1)   
0                    0.0  ...        0.0          0.0            0.0   
1                    0.0  ...        0.0          0.0            0.0   
2                    0.0  ...        0.0          0.0            0.0   
3                    0.0  ...        4.0          4.0            0.0   
4                    0.0  ...        6.0          6.0            0.0   
..                   ...  ...        ...          ...            ...   
95                   0.0  ...        2.0          2.0            0.0   
96                   0.0  ...      528.0        528.0            0.0   
97                   NaN  ...        NaN          NaN            NaN   
98                   NaN  ...        NaN          NaN            NaN   
99                   NaN  ...        NaN          NaN            NaN   

                                                                            \
   Pré Escola (2) Pré Escola (3) Pré Escola Total Ens. Fund.I Ens. Fund.II   
0             0.0            0.0              0.0         0.0          0.0   
1             0.0            0.0              0.0         0.0          0.0   
2             0.0            0.0              0.0         0.0          0.0   
3             0.0            0.0              0.0         0.0          0.0   
4             0.0            0.0              0.0         0.0          0.0   
..            ...            ...              ...         ...          ...   
95            0.0            0.0              0.0         0.0          0.0   
96            3.0            0.0              3.0         0.0          0.0   
97            NaN            NaN              NaN         NaN          NaN   
98            NaN            NaN              NaN         NaN          NaN   
99            NaN            NaN              NaN         NaN          NaN   

                 
   EJA I EJA II  
0    0.0    0.0  
1    0.0    0.0  
2    0.0    0.0  
3    0.0    0.0  
4    0.0    0.0  
..   ...    ...  
95   0.0    0.0  
96   

O dataframe contem dados de matrículas, matrículas em processo e demanda não atendida. Como desejamos apenas matrículas, vamos remover as outras colunas.

In [5]:
mat_24 = mat_24[['Distrito', 'Matrículas']]
mat_24

Distrito Matrículas             \
                                   Unnamed: 0_level_1     Creche Pré Escola   
0                                          AGUA RASA      1264.0      724.0   
1                                  ALTO DE PINHEIROS       273.0        0.0   
2                                         ANHANGUERA      2912.0     1690.0   
3                                         ARICANDUVA      1542.0      699.0   
4                                        ARTUR ALVIM      2711.0     2138.0   
..                                                ...        ...        ...   
95                                        VILA SONIA      3609.0     1853.0   
96                                              TOTAL   345019.0   216107.0   
97                                                NaN        NaN        NaN   
98  (2) - Demanda sem opção por unidade específica...        NaN        NaN   
99     (3) - Demanda com opção por unidade específica        NaN        NaN   

                                                                   
   Ens. Fund.I Ens. Fund.II   EJA I   EJA II Ens. Médio Ed. Prof.  
0        967.0        932.0     0.0     23.0        0.0       0.0  
1          0.0          0.0     0.0      0.0        0.0       0.0  
2       3650.0       2430.0    24.0    130.0        0.0       0.0  
3       1217.0       1085.0     0.0     58.0        0.0       0.0  
4       2355.0       2128.0     0.0     21.0        0.0       0.0  
..         ...          ...     ...      ...        ...       ...  
95      2435.0       1611.0     0.0     15.0        0.0       0.0  
96    251032.0     183303.0  3591.0  13443.0     2076.0    1213.0  
97         NaN          NaN     NaN      NaN        NaN       NaN  
98         NaN          NaN     NaN      NaN        NaN       NaN  
99         NaN          NaN     NaN      NaN        NaN       NaN  

[100 rows x 9 columns]

Agora, sabendo que temos apenas dados sobre matrículas, vamos ajustar as colunas.

In [6]:
mat_24 = (mat_24
 .droplevel(0, axis='columns')
 .rename(columns={'Unnamed: 0_level_1': 'Distrito'}))

mat_24

Distrito    Creche  Pré Escola  \
0                                          AGUA RASA     1264.0       724.0   
1                                  ALTO DE PINHEIROS      273.0         0.0   
2                                         ANHANGUERA     2912.0      1690.0   
3                                         ARICANDUVA     1542.0       699.0   
4                                        ARTUR ALVIM     2711.0      2138.0   
..                                                ...       ...         ...   
95                                        VILA SONIA     3609.0      1853.0   
96                                              TOTAL  345019.0    216107.0   
97                                                NaN       NaN         NaN   
98  (2) - Demanda sem opção por unidade específica...       NaN         NaN   
99     (3) - Demanda com opção por unidade específica       NaN         NaN   

    Ens. Fund.I  Ens. Fund.II   EJA I   EJA II  Ens. Médio  Ed. Prof.  
0         967.0         932.0     0.0     23.0         0.0        0.0  
1           0.0           0.0     0.0      0.0         0.0        0.0  
2        3650.0        2430.0    24.0    130.0         0.0        0.0  
3        1217.0        1085.0     0.0     58.0         0.0        0.0  
4        2355.0        2128.0     0.0     21.0         0.0        0.0  
..          ...           ...     ...      ...         ...        ...  
95       2435.0        1611.0     0.0     15.0         0.0        0.0  
96     251032.0      183303.0  3591.0  13443.0      2076.0     1213.0  
97          NaN           NaN     NaN      NaN         NaN        NaN  
98          NaN           NaN     NaN      NaN         NaN        NaN  
99          NaN           NaN     NaN      NaN         NaN        NaN  

[100 rows x 9 columns]

As últimas linhas do dataframe são apenas dados de totalização e notas, então vamos excluí-las também.

In [7]:
mat_24 = mat_24.loc[mat_24['Distrito'].str.lower()!='total']
mat_24 = mat_24.loc[~mat_24.iloc[:,1].isna()]
mat_24

Distrito  Creche  Pré Escola  Ens. Fund.I  Ens. Fund.II  EJA I  \
0           AGUA RASA   1264.0       724.0        967.0         932.0    0.0   
1   ALTO DE PINHEIROS    273.0         0.0          0.0           0.0    0.0   
2          ANHANGUERA   2912.0      1690.0       3650.0        2430.0   24.0   
3          ARICANDUVA   1542.0       699.0       1217.0        1085.0    0.0   
4         ARTUR ALVIM   2711.0      2138.0       2355.0        2128.0    0.0   
..                 ...     ...         ...          ...           ...    ...   
91       VILA MARIANA    781.0       531.0        280.0         222.0    0.0   
92       VILA MATILDE   1778.0       877.0       2188.0        1865.0   19.0   
93      VILA MEDEIROS   3809.0      2335.0       1814.0        1413.0   79.0   
94      VILA PRUDENTE   2445.0      1127.0       1035.0         832.0   24.0   
95         VILA SONIA   3609.0      1853.0       2435.0        1611.0    0.0   

    EJA II  Ens. Médio  Ed. Prof.  
0     23.0         0.0        0.0  
1      0.0         0.0        0.0  
2    130.0         0.0        0.0  
3     58.0         0.0        0.0  
4     21.0         0.0        0.0  
..     ...         ...        ...  
91     0.0         0.0        0.0  
92    25.0         0.0        0.0  
93   271.0         0.0        0.0  
94    70.0         0.0        0.0  
95    15.0         0.0        0.0  

[96 rows x 9 columns]

Finalmente, vamos "despivotar" a tabela, transformando o nome das colunas em uma nova coluna chamada "Nível educacional" e unificando as colunas de valor sob uma coluna chamada matrículas.

In [8]:
mat_24 = mat_24.melt(
    id_vars='Distrito',
    var_name='Nível Educacional',
    value_name='Matrículas'
)
mat_24

Distrito Nível Educacional  Matrículas
0            AGUA RASA             Creche      1264.0
1    ALTO DE PINHEIROS             Creche       273.0
2           ANHANGUERA             Creche      2912.0
3           ARICANDUVA             Creche      1542.0
4          ARTUR ALVIM             Creche      2711.0
..                  ...               ...         ...
763       VILA MARIANA          Ed. Prof.         0.0
764       VILA MATILDE          Ed. Prof.         0.0
765      VILA MEDEIROS          Ed. Prof.         0.0
766      VILA PRUDENTE          Ed. Prof.         0.0
767         VILA SONIA          Ed. Prof.         0.0

[768 rows x 3 columns]

## Número de professores da Rede Municipal de Ensino

O segundo indicador solicitado é o número de professores da Rede Municipal de Ensino, com recortes por Raça, Sexo, Nível de Ensino (Educação Infantil, Ensino Fundamental etc.), Tipo de Unidade de atuação (EMEF, EMEI etc.).

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/microdados-servidores-perfil, porém os arquivos possuem informação sobre todos os servidores da SME, o que inclui os servidores administrativos, que precisarão ser excluídos.

Primeiro, precisamos visualizar todos os recursos relativos a esse conjunto de dados. Nesse momento, podemos pegar todos os conjuntos em dezembro de 2024.

In [9]:
pkg_name = 'microdados-servidores-perfil'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Microdados - Perfil dos Servidores 2024',
  'id': 'f2d39e22-d919-4324-b92d-616adc5feb41',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/12a101f0-622b-43ad-946c-95c430ae6cab/resource/f2d39e22-d919-4324-b92d-616adc5feb41/download/perfilservidor24.csv'}]

Aparentemente, os dados de perfil dos servidores possuem periodicidade anual, já que temos apenas um arquivo disponível para 2024.

In [10]:
resource_id = resources[0]['id']
perf_24 = da.load_resource(resource_id)
perf_24

DATA_BASE_EOL  ANO_REFERENCIA  CD_CAR_SERV_SME  MES_NASC  ANO_NASC  \
0      dezembro, 2024            2024   13959569213340         5      1958   
1      dezembro, 2024            2024   13757719212040        11      1954   
2      dezembro, 2024            2024   13054398219040         5      1952   
3      dezembro, 2024            2024   13959668217340         5      1958   
4      dezembro, 2024            2024   13858808214640         4      1954   
...               ...             ...              ...       ...       ...   
90908  dezembro, 2024            2024  300726592392517         6      1987   
90909  dezembro, 2024            2024  371730092342317         2      1969   
90910  dezembro, 2024            2024  371730092342217         4      1985   
90911  dezembro, 2024            2024  309728622328717        10      1975   
90912  dezembro, 2024            2024  300723422314317         9      1967   

       IDADE CD_SEXO  CD_MUNICIPIO_NASC      DC_MUNICIPIO_NASC  \
0         66       F       9.354739e+15              SAO PAULO   
1         70       F       9.354739e+15              SAO PAULO   
2         72       F       9.354739e+15              SAO PAULO   
3         66       F       9.354739e+15              SAO PAULO   
4         70       F       3.187364e+14                  IRECE   
...      ...     ...                ...                    ...   
90908     37       F       9.354739e+15              SAO PAULO   
90909     55       F       9.343737e+15            SANTO ANDRE   
90910     39       F       9.354739e+15              SAO PAULO   
90911     49       F       9.354739e+15  SAO BERNARDO DO CAMPO   
90912     57       F       9.354739e+15              SAO PAULO   

      UF_MUNICIPIO_NASC  ...  CD_UNIDADE_FUNCAO CD_FUNCAO  DC_FUNCAO  \
0                    SP  ...                NaN       NaN        NaN   
1                    SP  ...                NaN       NaN        NaN   
2                    SP  ...                NaN       NaN        NaN   
3                    SP  ...                NaN       NaN        NaN   
4                    BA  ...                NaN       NaN        NaN   
...                 ...  ...                ...       ...        ...   
90908                SP  ...                NaN       NaN        NaN   
90909                SP  ...                NaN       NaN        NaN   
90910                SP  ...                NaN       NaN        NaN   
90911                SP  ...                NaN       NaN        NaN   
90912                SP  ...                NaN       NaN        NaN   

      DT_INICIO_FUNCAO CD_UNIDADE_SOBREPOSTO  CD_SOBREPOSTO  \
0                  NaN                   NaN            NaN   
1                  NaN                   NaN            NaN   
2                  NaN                   NaN            NaN   
3                  NaN                   NaN            NaN   
4                  NaN                   NaN            NaN   
...                ...                   ...            ...   
90908              NaN                   NaN            NaN   
90909              NaN                   NaN            NaN   
90910              NaN          1.315840e+13   9.274940e+12   
90911              NaN                   NaN            NaN   
90912              NaN                   NaN            NaN   

                         DC_SOBREPOSTO  DT_INICIO_SOBREPOSTO ACUMULO_AMBITO  \
0                                  NaN                   NaN           PMSP   
1                                  NaN                   NaN            NaN   
2                                  NaN                   NaN           PMSP   
3                                  NaN                   NaN            NaN   
4                                  NaN                   NaN            NaN   
...                                ...                   ...            ...   
90908                              NaN                   NaN           PMSP   
90909                   

Com os dados baixados, vamos selecionar as colunas para atender às segmentações propostas no formulário.

In [11]:
# Raça, Sexo, Nível de Ensino (Educação Infantil, Ensino Fundamental etc.), Tipo de Unidade de atuação (EMEF, EMEI etc.).

perf_cols = [
    'CD_SEXO',
    'CD_RACA_COR',
    'DC_RACA_COR',
    'CD_DEF',
    'DC_SIT_FUNC',
    'CD_CARGO_BASE',
    'DC_CARGO_BASE',
    'DT_INICIO_CARGO_BASE',
    'CD_CARGO_ATUAL',
    'DC_CARGO_ATUAL',
    'CD_AREA_ATUACAO_BASE',
    'DC_AREA_ATUACAO_BASE',
    'CD_UNIDADE_ATUAL',
    'TP_UNIDADE_ATUAL',
    'DC_UNIDADE_ATUAL',
]

perf_24 = perf_24.loc[:, perf_cols]
perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF  DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840      EFETIVO   
1           F   6361921931  NAO INFORMADA  12727970840  EM COMISSAO   
2           F   1311820840         BRANCA  12727970840      EFETIVO   
3           F   1311820840         BRANCA  12727970840      EFETIVO   
4           F   6361921931  NAO INFORMADA  12727970840      EFETIVO   
...       ...          ...            ...          ...          ...   
90908       F   1311820840         BRANCA  12727970840      EFETIVO   
90909       F   6361921931  NAO INFORMADA  12727970840      EFETIVO   
90910       F   6361921931  NAO INFORMADA  12727970840      EFETIVO   
90911       F  93911221827          PARDA  12727970840      EFETIVO   
90912       F   6361921931  NAO INFORMADA  12727970840      EFETIVO   

       CD_CARGO_BASE                      DC_CARGO_BASE  DT_INICIO_CARGO_BASE  \
0       9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 41660   
1       9.204600e+12     ASSISTENTE TECNICO EDUCACIONAL                 42495   
2       9.274100e+13                PROF.DE ED.INFANTIL                 39588   
3       9.264550e+12      PROF.ENS.FUND.II E MED.-ARTES                 34243   
4       9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES                 33605   
...              ...                                ...                   ...   
90908   9.274100e+13                PROF.DE ED.INFANTIL                 41716   
90909   9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 40725   
90910   9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 40728   
90911   9.274100e+13                PROF.DE ED.INFANTIL                 43382   
90912   9.274100e+13                PROF.DE ED.INFANTIL                 39625   

       CD_CARGO_ATUAL                     DC_CARGO_ATUAL  \
0        9.234430e+12           PROF.ED.INF.E ENS.FUND.I   
1        9.204600e+12     ASSISTENTE TECNICO EDUCACIONAL   
2        9.274100e+13                PROF.DE ED.INFANTIL   
3        9.264550e+12      PROF.ENS.FUND.II E MED.-ARTES   
4        9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES   
...               ...                                ...   
90908    9.274100e+13                PROF.DE ED.INFANTIL   
90909    9.234430e+12           PROF.ED.INF.E ENS.FUND.I   
90910    9.274940e+12    ASSISTENTE DE DIRETOR DE ESCOLA   
90911    9.274100e+13                PROF.DE ED.INFANTIL   
90912    9.274100e+13                PROF.DE ED.INFANTIL   

       CD_AREA_ATUACAO_BASE             DC_AREA_ATUACAO_BASE  \
0                 301521917  ENSINO FUNDAMENTAL I E INFANTIL   
1               43411221211               TECNICA PEDAGOGICA   
2                1311820840                EDUCACAO INFANTIL   
3               93911221827            ENSINO FUNDAMENTAL II   
4               93911221827            ENSINO FUNDAMENTAL II   
...                     ...                              ...   
90908            1311820840                EDUCACAO INFANTIL   
90909             301521917  ENSINO FUNDAMENTAL I E INFANTIL   
90910             301521917  ENSINO FUNDAMENTAL I E INFANTIL   
90911            1311820840                EDUCACAO INFANTIL   
90912            1311820840                EDUCACAO INFANTIL   

       CD_UNIDADE_ATUAL TP_UNIDADE_ATUAL  \
0          3.385170e+14             EMEI   
1          1.226440e+14            COORD   
2          8.271610e+15        CEI DIRET   
3          1.236240e+14      FORA DE SME   
4          1.375830e+13         CEU EMEF   
...                 ...              ...   
90908      1.315840e+13        CEU CEMEI   
90909      1.305490e+13             EMEF   
90910      1.315840e+13         CEU EMEF   
90911      8.271610e+15        CEI DIRET   
90912      8.246790e+14          CEU CEI   

                                 DC_UNIDADE_ATUAL  
0               THEREZINHA BATISTA PETTAN, PROFA.  
1      COORDENADORIA DE GESTAO DE PESSOAS - COGEP  
2    

O formulário solicita também a exclusão de professores aposentados e servidores administrativos do conjunto de dados. Apesar de existir uma coluna com um valor "aposentado", a `ACUMULO_SITUACAO_SEGUNDO_VINCULO`, essa coluna parece se referir à situação do segundo vínculo, e não do vínculo com a PMSP. Além disso, a lista de servidores aposentados da Secretaria Municipal de Educação tem mais de 94 mil registros, então esses registros provavelmente não estão nos dados de perfil dos servidores.

Para excluir os servidores administrativos, vamos primeiro avaliar quais cargos estão presentes na base.

In [12]:
df_cargos = perf_24[['CD_CARGO_BASE', 'DC_CARGO_BASE']].copy()
df_cargos = df_cargos.drop_duplicates().reset_index(drop=True)

df_cargos

CD_CARGO_BASE                      DC_CARGO_BASE
0    9.234430e+12           PROF.ED.INF.E ENS.FUND.I
1    9.204600e+12     ASSISTENTE TECNICO EDUCACIONAL
2    9.274100e+13                PROF.DE ED.INFANTIL
3    9.264550e+12      PROF.ENS.FUND.II E MED.-ARTES
4    9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES
..            ...                                ...
92   1.232303e+10               SECRETARIO MUNICIPAL
93   4.292170e+11              CHEFE DE ASSESSORIA I
94   3.244140e+13           COORDENADOR II - ENS MED
95   8.234600e+12              ASSIST.ADM. DE GESTAO
96   5.212140e+11                         ASSESSOR I

[97 rows x 2 columns]

Dado a quantidade de cargos, vamos fitrar a lista com base em uma regra geral, mantendo apenas os cargos que possual a string "PROF" em sua descrição.

In [13]:
filtro_prof = df_cargos['DC_CARGO_BASE'].str.lower().str.contains('prof.', regex=False)
df_cargos_prof = df_cargos.loc[filtro_prof]

df_cargos_prof

CD_CARGO_BASE                        DC_CARGO_BASE
0    9.234430e+12             PROF.ED.INF.E ENS.FUND.I
2    9.274100e+13                  PROF.DE ED.INFANTIL
3    9.264550e+12        PROF.ENS.FUND.II E MED.-ARTES
4    9.244720e+12    PROF.ENS.FUND.II E MED.-PORTUGUES
5    9.214970e+12   PROF.ENS.FUND.II E MED.-MATEMATICA
6    9.274960e+12     PROF.ENS.FUND.II E MED.-CIENCIAS
7    9.284110e+13       PROF.ENS.FUND.II E MED.-INGLES
9    9.214970e+12    PROF.ENS.FUND.II E MED.-GEOGRAFIA
12   9.224650e+12     PROF.ENS.FUND.II E MED.-HISTORIA
19   9.224640e+12      PROF.SUBST.DE EDUCACAO INFANTIL
20   9.294110e+13    PROF.ENS.FUND.II E MED.-ED.FISICA
21   9.234490e+12       PROF.ENS.FUND.II E MED.-FISICA
32   9.204620e+12    PROF.TITULAR DE EDUCACAO INFANTIL
41   9.254560e+12          PROF.SUBST.DE 1.GR. NIVEL I
44   9.224650e+12                 PROF.1.GRAU NIVEL II
45   9.254620e+12      PROF.ENS.FUND.II E MED.-QUIMICA
49   9.294110e+13           PROF.TITULAR DE ENS.FUND.I
56   9.224710e+12     PROF.ENS.FUND.II E MED.-BIOLOGIA
57   9.264600e+12  PROF.ENS.FUND.II E MED.-CONT.CUSTOS
63   9.274970e+12              PROF.ADJ.DE ENS.FUND. I
64   9.284110e+13   PROF.ENS.FUND.II E MED.-SOCIOLOGIA
65   9.274980e+12      PROF.ADJ.ENS.FUND.II-MATEMATICA
68   9.224670e+12       PROF.ADJ.ENS.FUND.II-GEOGRAFIA
69   9.294120e+13     PROF.ENS.FUND.II E MED.-ESPANHOL
70   9.294120e+13        PROF.ADJ.ENS.FUND.II-CIENCIAS
74   9.284110e+13    PROF.ENS.FUND.II E MED.-FILOSOFIA
82   9.274100e+13       PROF.ENS.FUND.II E MED.-LIBRAS

Por último, filtramos a base geral com base nessa lista de cargos.

In [14]:
perf_24 = (
    perf_24
    .loc[
        perf_24['DC_CARGO_BASE'].isin(df_cargos_prof['DC_CARGO_BASE'].tolist())
    ]
)

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   1311820840         BRANCA  12727970840     EFETIVO   
4           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
5           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
90908       F   1311820840         BRANCA  12727970840     EFETIVO   
90909       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
90910       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
90911       F  93911221827          PARDA  12727970840     EFETIVO   
90912       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
2       9.274100e+13                 PROF.DE ED.INFANTIL   
3       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES   
4       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES   
5       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA   
...              ...                                 ...   
90908   9.274100e+13                 PROF.DE ED.INFANTIL   
90909   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
90910   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
90911   9.274100e+13                 PROF.DE ED.INFANTIL   
90912   9.274100e+13                 PROF.DE ED.INFANTIL   

       DT_INICIO_CARGO_BASE  CD_CARGO_ATUAL  \
0                     41660    9.234430e+12   
2                     39588    9.274100e+13   
3                     34243    9.264550e+12   
4                     33605    9.244720e+12   
5                     39589    9.214970e+12   
...                     ...             ...   
90908                 41716    9.274100e+13   
90909                 40725    9.234430e+12   
90910                 40728    9.274940e+12   
90911                 43382    9.274100e+13   
90912                 39625    9.274100e+13   

                           DC_CARGO_ATUAL  CD_AREA_ATUACAO_BASE  \
0                PROF.ED.INF.E ENS.FUND.I             301521917   
2                     PROF.DE ED.INFANTIL            1311820840   
3           PROF.ENS.FUND.II E MED.-ARTES           93911221827   
4       PROF.ENS.FUND.II E MED.-PORTUGUES           93911221827   
5      PROF.ENS.FUND.II E MED.-MATEMATICA           93911221827   
...                                   ...                   ...   
90908                 PROF.DE ED.INFANTIL            1311820840   
90909            PROF.ED.INF.E ENS.FUND.I             301521917   
90910     ASSISTENTE DE DIRETOR DE ESCOLA             301521917   
90911                 PROF.DE ED.INFANTIL            1311820840   
90912                 PROF.DE ED.INFANTIL            1311820840   

                  DC_AREA_ATUACAO_BASE  CD_UNIDADE_ATUAL TP_UNIDADE_ATUAL  \
0      ENSINO FUNDAMENTAL I E INFANTIL      3.385170e+14             EMEI   
2                    EDUCACAO INFANTIL      8.271610e+15        CEI DIRET   
3                ENSINO FUNDAMENTAL II      1.236240e+14      FORA DE SME   
4                ENSINO FUNDAMENTAL II      1.375830e+13         CEU EMEF   
5                ENSINO FUNDAMENTAL II      3.335110e+14             EMEF   
...                                ...               ...              ...   
90908                EDUCACAO INFANTIL      1.315840e+13        CEU CEMEI   
90909  ENSINO FUNDAMENTAL I E INFANTIL      1.305490e+13             EMEF   
90910  ENSINO FUNDAMENTAL I E INFANTIL      1.315840e+13         CEU EMEF   
90911                EDUCACAO INFANTIL      8.271610e+15        CEI DIRET   
90912                EDUCACAO INFANTIL      8.246790e+14          CEU CEI   

                          DC_UNIDADE_ATUAL  
0        THEREZINHA BATISTA PETTAN, PROFA.  
2                           JARDIM MONJOLO  
3            C

## Número de Unidades Escolares

O terceiro indicador solicitado é o número de Unidades Escolares da Rede Municipal de Ensino, com recortes por Tipo de Escola (EMEI, EMEF etc.) e Distrito.

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/cadastro-de-escolas-municipais-conveniadas-e-privadas.

Primeiro, precisamos visualizar todos os recursos relativos a esse conjunto de dados. Nesse momento, podemos pegar todos os conjuntos em dezembro de 2024.

In [15]:
pkg_name = 'cadastro-de-escolas-municipais-conveniadas-e-privadas'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Cadastro de escolas da cidade de São Paulo 2024',
  'id': '533188c6-1949-4976-ac4e-acd313415cd1',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/8da55b0e-b385-4b54-9296-d0000014ddd5/resource/533188c6-1949-4976-ac4e-acd313415cd1/download/escolas122024.csv'}]

In [16]:
resource_id = resources[0]['id']
escolas_24 = da.load_resource(resource_id)
escolas_24

DRE  CODESC     TIPOESC                                 NOMES  \
0      G      86        EMEI            PAULO CAMILHIER FLORENCANO   
1     FO      94        EMEI                VICENTE PAULO DA SILVA   
2     MP     108        EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3     BT     191        EMEF             ALIPIO CORREA NETO, PROF.   
4     PJ     205       EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...   ..     ...         ...                                   ...   
5021  PJ  700053  CEU AT COM                     PINHEIRINHO DAGUA   
5022  PE  700054  CEU AT COM                          MONTE SERRAT   
5023  PJ  700055  CEU AT COM                      CORETO DE TAIPAS   
5024  PE  700056  CEU AT COM                        HORIZONTE AZUL   
5025  MP  700057  CEU AT COM             SAO MIGUEL - LUIZ MELODIA   

                                    DESLOC                 CEU  \
0               PAULO CAMILHIER FLORENCANO                 NaN   
1                   VICENTE PAULO DA SILVA                 NaN   
2             JOSE ERMIRIO DE MORAES, SEN.                 NaN   
3                ALIPIO CORREA NETO, PROF.                 NaN   
4     VERA LUCIA APARECIDA RIBEIRO, PROFA.                 NaN   
...                                    ...                 ...   
5021                     PINHEIRINHO DAGUA  PINHEIRINHO D'AGUA   
5022                          MONTE SERRAT        MONTE SERRAT   
5023                      CORETO DE TAIPAS    CORETO DE TAIPAS   
5024                        HORIZONTE AZUL      HORIZONTE AZUL   
5025             SAO MIGUEL - LUIZ MELODIA          SAO MIGUEL   

                  DIRETORIA                  SUBPREF  \
0                GUAIANASES               GUAIANASES   
1     FREGUESIA/BRASILANDIA  CASA VERDE/CACHOEIRINHA   
2                SAO MIGUEL               SAO MIGUEL   
3                   BUTANTA                  BUTANTA   
4                  PIRITUBA                 PIRITUBA   
...                     ...                      ...   
5021               PIRITUBA                 PIRITUBA   
5022                  PENHA                    MOOCA   
5023               PIRITUBA                 PIRITUBA   
5024                  PENHA                    PENHA   
5025             SAO MIGUEL               SAO MIGUEL   

                        ENDERECO  NUMERO  ... ATO_CRIACAO  DOM_CRIACAO  \
0      RUA FELICIANO DE MENDONCA   502.0  ...       26134   13/06/1988   
1     RUA DOUTOR FLEURY SILVEIRA   295.0  ...       26314   04/07/1988   
2         RUA SAO BRAS DO SUACUI   159.0  ...       26312   05/07/1988   
3           AVENIDA JOAO CAIAFFA   140.0  ...       26003   27/05/1988   
4           RUA BENEDITO PEREIRA   206.0  ...       26229   22/06/1988   
...                          ...     ...  ...         ...          ...   
5021         RUA CAMILLO ZANOTTI    92.0  ...       59933   01/12/2020   
5022            RUA MONTE SERRAT   230.0  ...       59931   01/12/2020   
5023     RUA JOÃO AMADO COUTINHO   240.0  ...       59932   01/12/2020   
5024       AVENIDA SYLVIO TORRES   295.0  ...       59930   01/12/2020   
5025    RUA JOSÉ FERREIRA CRESPO   495.0  ...       60010   16/12/2020   

     DT_INI_CONV DT_AUTORIZA DT_EXTINCAO             NOME_ANT REDE  LATITUDE  \
0            NaN  16/03/1991         NaN                  NaN  DIR -23553905   
1            NaN  16/03/1991         NaN                  NaN  DIR -23489728   
2            NaN  13/03/2001         NaN  VILA NITRO OPERARIA  DIR -23478312   
3            NaN  16/03/1991         NaN                  NaN  DIR -23612237   
4            NaN  16/03/1991         NaN                  NaN  DIR -23486142   
...          ...         ...         ...                  ...  ...       ...   
5021         NaN         NaN         NaN                  NaN  CON -23438098   
5022         NaN         NaN         NaN                  NaN  CON -23539898   
5023         NaN         NaN         NaN                  NaN  CON -23447574   
5024     

Os dados das escolas também serão usados com outros conjuntos de dados para regionalizá-los, então vamos manter também algumas colunas de identificação das escolas para facilitar esse uso o posterior. Vamos também filtrar apenas as escolas ativas.

In [17]:
escolas_cols = ['CODESC',
                'TIPOESC',
                'NOMES',
                'SUBPREF',
                'DISTRITO',
                'CODINEP',
                'CD_CIE',
                'NOME_ANT',
                'REDE']

escolas_24 = escolas_24.loc[:, escolas_cols]

escolas_24

CODESC     TIPOESC                                 NOMES  \
0         86        EMEI            PAULO CAMILHIER FLORENCANO   
1         94        EMEI                VICENTE PAULO DA SILVA   
2        108        EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3        191        EMEF             ALIPIO CORREA NETO, PROF.   
4        205       EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...      ...         ...                                   ...   
5021  700053  CEU AT COM                     PINHEIRINHO DAGUA   
5022  700054  CEU AT COM                          MONTE SERRAT   
5023  700055  CEU AT COM                      CORETO DE TAIPAS   
5024  700056  CEU AT COM                        HORIZONTE AZUL   
5025  700057  CEU AT COM             SAO MIGUEL - LUIZ MELODIA   

                      SUBPREF       DISTRITO     CODINEP     CD_CIE  \
0                  GUAIANASES     GUAIANASES  35098711.0  1678110.0   
1     CASA VERDE/CACHOEIRINHA          LIMAO  35098361.0  1670158.0   
2                  SAO MIGUEL  JARDIM HELENA  35098760.0  1677116.0   
3                     BUTANTA     VILA SONIA  35098462.0  1679154.0   
4                    PIRITUBA       PIRITUBA  35079029.0  1671138.0   
...                       ...            ...         ...        ...   
5021                 PIRITUBA        JARAGUA  35007555.0        NaN   
5022                    MOOCA        TATUAPE  35007556.0        NaN   
5023                 PIRITUBA        JARAGUA  35007561.0        NaN   
5024                    PENHA    ARTUR ALVIM  35007631.0        NaN   
5025               SAO MIGUEL     SAO MIGUEL  35008057.0        NaN   

                 NOME_ANT REDE  
0                     NaN  DIR  
1                     NaN  DIR  
2     VILA NITRO OPERARIA  DIR  
3                     NaN  DIR  
4                     NaN  DIR  
...                   ...  ...  
5021                  NaN  CON  
5022                  NaN  CON  
5023                  NaN  CON  
5024                  NaN  CON  
5025                  NaN  CON  

[5026 rows x 9 columns]

As unidades escolares também recebeu instruções de filtro para que os número fossem adequados ao informado no relatório de função. Devemos excluir as escolas de tipo `CEU AT COM` e `ESC.PART.`.

In [18]:
escolas_24['TIPOESC'].value_counts()

TIPOESC
CR.P.CONV     1826
ESC.PART.      795
EMEF           551
EMEI           517
CEI INDIR      399
CEI DIRET      315
MOVA           266
CEU AT COM      58
CEU             58
CEU EMEI        47
CEU EMEF        46
CEU CEI         45
ESP CONV        26
CEMEI           21
CIEJA           16
CEU CEMEI       12
EMEFM            8
EMEBS            6
E TEC            4
CECI             3
CCI/CIPS         3
CMCT             2
EMEI P FOM       1
EMEF P FOM       1
Name: count, dtype: int64

In [19]:
escolas_24 = escolas_24[~escolas_24['TIPOESC'].isin(['CEU AT COM', 'ESC.PART.'])]

escolas_24

CODESC   TIPOESC                                              NOMES  \
0         86      EMEI                         PAULO CAMILHIER FLORENCANO   
1         94      EMEI                             VICENTE PAULO DA SILVA   
2        108      EMEF                       JOSE ERMIRIO DE MORAES, SEN.   
3        191      EMEF                          ALIPIO CORREA NETO, PROF.   
4        205     EMEBS               VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...      ...       ...                                                ...   
4962  600047  ESP CONV  ASSOCIACAO CASA DOS DEFICIENTES DE ERMELINO MA...   
4963  600050  ESP CONV  AACD - ASS DE ASS A CRIANCA DEFICIENTE - UNID ...   
4964  600051  ESP CONV                    APAE - NUCLEO CAPELA DO SOCORRO   
4965  600052  ESP CONV                          APAE - NUCLEO CAMPO LIMPO   
4966  600056  ESP CONV                             APAE - NUCLEO PIRITUBA   

                      SUBPREF       DISTRITO     CODINEP     CD_CIE  \
0                  GUAIANASES     GUAIANASES  35098711.0  1678110.0   
1     CASA VERDE/CACHOEIRINHA          LIMAO  35098361.0  1670158.0   
2                  SAO MIGUEL  JARDIM HELENA  35098760.0  1677116.0   
3                     BUTANTA     VILA SONIA  35098462.0  1679154.0   
4                    PIRITUBA       PIRITUBA  35079029.0  1671138.0   
...                       ...            ...         ...        ...   
4962               SAO MIGUEL     SAO MIGUEL         NaN        NaN   
4963                    MOOCA          MOOCA         NaN        NaN   
4964        CAPELA DO SOCORRO   CIDADE DUTRA         NaN        NaN   
4965              CAMPO LIMPO    CAMPO LIMPO         NaN        NaN   
4966                     LAPA           LAPA         NaN        NaN   

                                           NOME_ANT REDE  
0                                               NaN  DIR  
1                                               NaN  DIR  
2                               VILA NITRO OPERARIA  DIR  
3                                               NaN  DIR  
4                                               NaN  DIR  
...                                             ...  ...  
4962  ASSOCIACAO CASA DOS DEFICIENTES DE ERMELINO M  CON  
4963  AACD - ASS DE ASS A CRIANCA DEFICIENTE - UNID  CON  
4964                                           APAE  CON  
4965                                           APAE  CON  
4966                                            NaN  CON  

[4173 rows x 9 columns]

## Perfil dos alunos

O quinto indicador solicitado é o número de alunos da Rede Municipal de Ensino, com recortes por Raça, Sexo, existência de Necessidades Especiais, Distrito, Rede de Ensino (Administração Direta ou Rede Conveniada/Parceira).

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/perfil-dos-educandos-cor-raca-idade-sexo-necessidades-educacionais-especiais.

Primeiro, precisamos visualizar todos os recursos relativos a esse conjunto de dados. Nesse momento, podemos pegar todos os conjuntos em dezembro de 2024.

In [20]:
pkg_name = 'perfil-dos-educandos-cor-raca-idade-sexo-necessidades-educacionais-especiais'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Perfil dos educandos - Dez/2024',
  'id': '5ef5187b-9d3d-4c68-8da2-de441f7bff30',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/b9c5faef-1a61-4814-b89e-bd7a73154ebc/resource/5ef5187b-9d3d-4c68-8da2-de441f7bff30/download/perfil_dos_educandos_122024.csv'}]

Aparentemente, os dados de perfil dos educandos possuem periodicidade anual, já que temos apenas um arquivo disponível para 2023.

In [21]:
resource_id = resources[0]['id']
alunos_24 = da.load_resource(resource_id)
alunos_24

DRE  CODESC     TIPOESC                                    NOMESC  \
0       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
1       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
2       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
3       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
4       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
...     ..     ...         ...                                       ...   
467257  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467258  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467259  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467260  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467261  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   

          DISTRITO  SETOR   ANO REDE   MODAL DESCSERIE PERIODO  TURNO  \
0       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
1       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
2       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
3       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
4       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      3   
...            ...    ...   ...  ...     ...       ...     ...    ...   
467257    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467258    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467259    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467260    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467261    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   

            DESCTURNO SEXO  IDADE                          NEE  \
0       Intermediário    F      6                      AUTISMO   
1       Intermediário    F      7                      AUTISMO   
2       Intermediário    M     10                          NaN   
3       Intermediário    M     11                          NaN   
4               Tarde    F      8                          NaN   
...               ...  ...    ...                          ...   
467257     Vespertino    M     13                          NaN   
467258     Vespertino    M     13                          NaN   
467259     Vespertino    M     14                          NaN   
467260     Vespertino    M     14  BAIXA VISAO/VISAO SUBNORMAL   
467261     Vespertino    M     15                          NaN   

                   RACA  Qtde    DATABASE  
0                 PARDA     1  31/12/2024  
1                 PARDA     1  31/12/2024  
2                 PARDA     1  31/12/2024  
3                BRANCA     1  31/12/2024  
4                 PARDA     1  31/12/2024  
...                 ...   ...         ...  
467257            PRETA     2  31/12/2024  
467258  RECUSOU INFORMA     4  31/12/2024  
467259            PARDA     5  31/12/2024  
467260  RECUSOU INFORMA     2  31/12/2024  
467261            PARDA     2  31/12/2024  

[467262 rows x 19 columns]

In [22]:
total_alunos_24_pre_filtros = alunos_24['Qtde'].sum()
total_alunos_24_pre_filtros

np.int64(1596412)

### Ajustando alunos de `EDPROF`

Para manter a quantidade de matrículas compatível com o relatório de função, vamos manter apenas algumas modalidades de ensino, de modo que não sejam consideradas matrículas de atividades em contraturno e similares. Além disso, a soma de alunos de `EDPROF` é diferente do último valor informado pela SME em auditoria. O valor informado pela SME foi de 1.879 matrículas, porém o total com base nos dados de `Perfil dos alunos` é 4.722. Vamos tentar entender de onde vem essa distorção.

In [23]:
(
    alunos_24
    .loc[alunos_24['MODAL'] == 'EDPROF', ['TIPOESC', 'Qtde']]
    .groupby('TIPOESC')
    .sum().reset_index()
)

TIPOESC  Qtde
0  CEU AT COM    63
1        CMCT  2780
2       E TEC  1445
3       EMEBS    46
4       EMEFM   388

In [24]:
1445+46+388

1879

Vemos que a soma dos alunos de `E TEC` + `EMEBS` + `EMEFM` coincide exatamente com o número de matrículas informado pela SME. Após apresentar a situação para o Coordenador do GT Educação, decidiu-se por excluir os registros de `EDPROF` de `CEU AT COM` e `CMCT`.

In [25]:
filtro_alunos_24 = (
    (alunos_24['MODAL'] != 'EDPROF') |
    (~alunos_24['TIPOESC'].isin(['CEU AT COM', 'CMCT']))
)

In [26]:
alunos_24 = alunos_24.loc[filtro_alunos_24]
alunos_24

DRE  CODESC     TIPOESC                                    NOMESC  \
0       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
1       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
2       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
3       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
4       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
...     ..     ...         ...                                       ...   
467257  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467258  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467259  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467260  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467261  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   

          DISTRITO  SETOR   ANO REDE   MODAL DESCSERIE PERIODO  TURNO  \
0       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
1       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
2       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
3       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
4       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      3   
...            ...    ...   ...  ...     ...       ...     ...    ...   
467257    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467258    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467259    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467260    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467261    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   

            DESCTURNO SEXO  IDADE                          NEE  \
0       Intermediário    F      6                      AUTISMO   
1       Intermediário    F      7                      AUTISMO   
2       Intermediário    M     10                          NaN   
3       Intermediário    M     11                          NaN   
4               Tarde    F      8                          NaN   
...               ...  ...    ...                          ...   
467257     Vespertino    M     13                          NaN   
467258     Vespertino    M     13                          NaN   
467259     Vespertino    M     14                          NaN   
467260     Vespertino    M     14  BAIXA VISAO/VISAO SUBNORMAL   
467261     Vespertino    M     15                          NaN   

                   RACA  Qtde    DATABASE  
0                 PARDA     1  31/12/2024  
1                 PARDA     1  31/12/2024  
2                 PARDA     1  31/12/2024  
3                BRANCA     1  31/12/2024  
4                 PARDA     1  31/12/2024  
...                 ...   ...         ...  
467257            PRETA     2  31/12/2024  
467258  RECUSOU INFORMA     4  31/12/2024  
467259            PARDA     5  31/12/2024  
467260  RECUSOU INFORMA     2  31/12/2024  
467261            PARDA     2  31/12/2024  

[465839 rows x 19 columns]

Finalmente, vamos conferir se o filtro funcionou corretamente.

In [27]:
(
    alunos_24
    .loc[alunos_24['MODAL'] == 'EDPROF', ['TIPOESC', 'Qtde']]
    .groupby('TIPOESC')
    .sum().reset_index()
)

TIPOESC  Qtde
0   E TEC  1445
1   EMEBS    46
2   EMEFM   388

In [28]:
total_alunos_24_pos_filtros = alunos_24['Qtde'].sum()
total_alunos_24_pos_filtros

np.int64(1593569)

In [29]:
total_alunos_24_pre_filtros - total_alunos_24_pos_filtros

np.int64(2843)

Vemos que todos os alunos de `EDPROF` que deviam estar presentes estão e a diferença antes e depois dos filtros é exatamente a quantidade de alunos de `CEU AT COM` e `CMCT`, então o filtro funcionou corretamente.

### Ajustando alunos de `ESPEC`

A soma de alunos de `ESPEC` também é diferente do último valor informado pela SME em auditoria. O valor informado pela SME foi de 693 matrículas, porém o total com base nos dados de `Perfil dos alunos` é 766. Vamos tentar entender de onde vem essa distorção.

In [30]:
(
    alunos_24
    .loc[alunos_24['MODAL'] == 'ESPEC', ['TIPOESC', 'Qtde']]
    .groupby('TIPOESC')
    .sum().reset_index()
)

TIPOESC  Qtde
0  CEU EMEF    58
1  CEU EMEI    15
2     EMEBS   693

Vemos que a soma dos alunos de `EMEBS` coincide exatamente com o número de matrículas informado pela SME. Após apresentar a situação para o Coordenador do GT Educação, decidiu-se por excluir os registros de `CEU EMEF` e `CEU EMEI`.

In [31]:
total_alunos_24_pre_filtros = alunos_24['Qtde'].sum()
total_alunos_24_pre_filtros

np.int64(1593569)

In [32]:
filtro_alunos_24 = (
    (alunos_24['MODAL'] != 'ESPEC') |
    (~alunos_24['TIPOESC'].isin(['CEU EMEF', 'CEU EMEI']))
)

In [33]:
alunos_24 = alunos_24.loc[filtro_alunos_24]
alunos_24

DRE  CODESC     TIPOESC                                    NOMESC  \
0       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
1       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
2       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
3       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
4       BT     191        EMEF                 ALIPIO CORREA NETO, PROF.   
...     ..     ...         ...                                       ...   
467257  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467258  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467259  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467260  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   
467261  SM  700044  CEU AT COM  ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.   

          DISTRITO  SETOR   ANO REDE   MODAL DESCSERIE PERIODO  TURNO  \
0       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
1       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
2       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
3       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      2   
4       VILA SONIA   9404  2024  DIR  ATCOMP    ATCOMP  Diurno      3   
...            ...    ...   ...  ...     ...       ...     ...    ...   
467257    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467258    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467259    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467260    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   
467261    IGUATEMI   3304  2024  DIR    CELP      CELP  Diurno      4   

            DESCTURNO SEXO  IDADE                          NEE  \
0       Intermediário    F      6                      AUTISMO   
1       Intermediário    F      7                      AUTISMO   
2       Intermediário    M     10                          NaN   
3       Intermediário    M     11                          NaN   
4               Tarde    F      8                          NaN   
...               ...  ...    ...                          ...   
467257     Vespertino    M     13                          NaN   
467258     Vespertino    M     13                          NaN   
467259     Vespertino    M     14                          NaN   
467260     Vespertino    M     14  BAIXA VISAO/VISAO SUBNORMAL   
467261     Vespertino    M     15                          NaN   

                   RACA  Qtde    DATABASE  
0                 PARDA     1  31/12/2024  
1                 PARDA     1  31/12/2024  
2                 PARDA     1  31/12/2024  
3                BRANCA     1  31/12/2024  
4                 PARDA     1  31/12/2024  
...                 ...   ...         ...  
467257            PRETA     2  31/12/2024  
467258  RECUSOU INFORMA     4  31/12/2024  
467259            PARDA     5  31/12/2024  
467260  RECUSOU INFORMA     2  31/12/2024  
467261            PARDA     2  31/12/2024  

[465779 rows x 19 columns]

Finalmente, vamos conferir se o filtro funcionou corretamente.

In [34]:
(
    alunos_24
    .loc[alunos_24['MODAL'] == 'ESPEC', ['TIPOESC', 'Qtde']]
    .groupby('TIPOESC')
    .sum().reset_index()
)

TIPOESC  Qtde
0   EMEBS   693

In [35]:
total_alunos_24_pos_filtros = alunos_24['Qtde'].sum()
total_alunos_24_pos_filtros

np.int64(1593496)

In [36]:
total_alunos_24_pre_filtros - total_alunos_24_pos_filtros

np.int64(73)

Vemos que todos os alunos de `ESPEC` que deviam estar presentes estão e a diferença antes e depois dos filtros é exatamente a quantidade de alunos de `CEU EMEF` e `CEU EMEI`, então o filtro funcionou corretamente.

In [37]:
alunos_24['MODAL'].unique()

array(['ATCOMP', 'FUND', 'PAEE COLAB', 'PAP', 'PAP COLAB', 'PRE', 'SAAI',
       'EJA', 'REC', 'CRECHE', 'MOVA', 'CELP', 'CONVEE', 'ESPEC',
       'EDPROF', 'MEDIO'], dtype=object)

In [38]:
modalidades = ['CRECHE', 'ESPEC', 'PRE',
               'CONVEE','EDPROF', 'EJA', 'FUND', 'MEDIO', 'MOVA']

alunos_24 = alunos_24[alunos_24['MODAL'].isin(modalidades)]
alunos_24

DRE  CODESC   TIPOESC                     NOMESC    DISTRITO  SETOR  \
54      BT     191      EMEF  ALIPIO CORREA NETO, PROF.  VILA SONIA   9404   
55      BT     191      EMEF  ALIPIO CORREA NETO, PROF.  VILA SONIA   9404   
56      BT     191      EMEF  ALIPIO CORREA NETO, PROF.  VILA SONIA   9404   
57      BT     191      EMEF  ALIPIO CORREA NETO, PROF.  VILA SONIA   9404   
58      BT     191      EMEF  ALIPIO CORREA NETO, PROF.  VILA SONIA   9404   
...     ..     ...       ...                        ...         ...    ...   
462528  SM  600035  ESP CONV        INSTITUTO MATER DEI  SAO MATEUS   7309   
462529  SM  600035  ESP CONV        INSTITUTO MATER DEI  SAO MATEUS   7309   
462530  SM  600035  ESP CONV        INSTITUTO MATER DEI  SAO MATEUS   7309   
462531  SM  600035  ESP CONV        INSTITUTO MATER DEI  SAO MATEUS   7309   
462532  SM  600035  ESP CONV        INSTITUTO MATER DEI  SAO MATEUS   7309   

         ANO REDE   MODAL     DESCSERIE PERIODO  TURNO DESCTURNO SEXO  IDADE  \
54      2024  DIR    FUND  C.I 1.ANO F9  Diurno      6  Integral    F      6   
55      2024  DIR    FUND  C.I 1.ANO F9  Diurno      6  Integral    F      7   
56      2024  DIR    FUND  C.I 1.ANO F9  Diurno      6  Integral    F      7   
57      2024  DIR    FUND  C.I 1.ANO F9  Diurno      6  Integral    F      7   
58      2024  DIR    FUND  C.I 1.ANO F9  Diurno      6  Integral    F      7   
...      ...  ...     ...           ...     ...    ...       ...  ...    ...   
462528  2024  CON  CONVEE        CONVEE  Diurno      3     Tarde    M     27   
462529  2024  CON  CONVEE        CONVEE  Diurno      3     Tarde    M     28   
462530  2024  CON  CONVEE        CONVEE  Diurno      3     Tarde    M     29   
462531  2024  CON  CONVEE        CONVEE  Diurno      3     Tarde    M     30   
462532  2024  CON  CONVEE        CONVEE  Diurno      3     Tarde    M     32   

                            NEE    RACA  Qtde    DATABASE  
54                          NaN   PARDA     3  31/12/2024  
55                          NaN  BRANCA     3  31/12/2024  
56                          NaN   PARDA     8  31/12/2024  
57                          NaN   PRETA     2  31/12/2024  
58      DEFICIENCIA INTELECTUAL  BRANCA     1  31/12/2024  
...                         ...     ...   ...         ...  
462528  DEFICIENCIA INTELECTUAL   PARDA     1  31/12/2024  
462529  DEFICIENCIA INTELECTUAL  BRANCA     2  31/12/2024  
462530  DEFICIENCIA INTELECTUAL   PARDA     1  31/12/2024  
462531  DEFICIENCIA INTELECTUAL  BRANCA     1  31/12/2024  
462532  DEFICIENCIA INTELECTUAL   PARDA     1  31/12/2024  

[266347 rows x 19 columns]

In [39]:
alunos_cols = ['DISTRITO',
               'REDE',
               'MODAL',
               'SEXO',
               'NEE',
               'RACA',
               'Qtde']

alunos_24 = alunos_24[alunos_cols]

alunos_24

DISTRITO REDE   MODAL SEXO                      NEE    RACA  Qtde
54      VILA SONIA  DIR    FUND    F                      NaN   PARDA     3
55      VILA SONIA  DIR    FUND    F                      NaN  BRANCA     3
56      VILA SONIA  DIR    FUND    F                      NaN   PARDA     8
57      VILA SONIA  DIR    FUND    F                      NaN   PRETA     2
58      VILA SONIA  DIR    FUND    F  DEFICIENCIA INTELECTUAL  BRANCA     1
...            ...  ...     ...  ...                      ...     ...   ...
462528  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1
462529  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     2
462530  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1
462531  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     1
462532  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1

[266347 rows x 7 columns]

In [40]:
alunos_24['Qtde'].sum()

np.int64(1027308)

O total de alunos está exatamente igual ao total esperado, que é de 1.027.308.

## Número de alunos estrangeiros

O sétimo indicador é o número de alunos estrangeiros da rede municipal, segmentado por País de Procedência, Distrito, Tipo de Rede (Direta ou Conveniada/Parceira), Etapa (Creche, fundamental, EJA etc.).

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/educandos-estrangeiros-por-nacionalidade. Sabendo que o último trecho da url representa a id do conjunto de dados, vamos utilizá-la para fazer a extração dos dados do portal. Nesse momento, podemos pegar todos os conjuntos em dezembro de 2024.

Primeiro, precisamos visualizar todos os recursos relativos a esse conjunto de dados.

In [41]:
pkg_name = 'educandos-estrangeiros-por-nacionalidade'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Educandos estrangeiros por nacionalidade e DRE',
  'id': '75357667-9bf6-463b-9ecc-609dfecafb25',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/f66a2317-0b67-4e14-b6c5-1a7340d6e30f/resource/75357667-9bf6-463b-9ecc-609dfecafb25/download/estudantes_estrangeiros_dez24.xlsx'},
 {'name': 'Educandos estrangeiros por nacionalidade e DRE',
  'id': 'bae3bf9f-43e6-4616-827e-d50ff5f19552',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/f66a2317-0b67-4e14-b6c5-1a7340d6e30f/resource/bae3bf9f-43e6-4616-827e-d50ff5f19552/download/estudantes_estrangeiros_dez2024.csv'},
 {'name': 'Educandos estrangeiros por nacionalidade e DRE',
  'id': '22f9daba-fb61-439b-984b-ab5d99733ad2',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/f66a2317-0b67-4e14-b6c5-1a7340d6e30f/resource/22f9daba-fb61-439b-984b-ab5d99733ad2/download/estudantes_estrangeiros_dez24.ods'},
 {'name': 'Educandos estrangeiros por nacionalidade e DRE',
  'id': '1920e20b-181f-43bf-b390-d45fbaa272d4',
  'url': 'https://d

In [42]:
resource_id = resources[0]['id']
alunos_est_2024 = da.load_resource(resource_id)
alunos_est_2024

DRE           DISTRITO  COD_PAIS                        NOME_PAIS  \
0     BT  ALTO DE PINHEIROS        42                            CHINA   
1     BT  ALTO DE PINHEIROS       226                       SERRA LEOA   
2     BT            BUTANTA        26                         COLÔMBIA   
3     BT            BUTANTA        31                          BÉLGICA   
4     BT            BUTANTA        36  ESTADOS UNIDOS DA AMÉRICA (EUA)   
...   ..                ...       ...                              ...   
3854  SM          SAPOPEMBA       185                            CONGO   
3855  SM          SAPOPEMBA       213                          NIGÉRIA   
3856  SM          SAPOPEMBA       277                            SÍRIA   
3857  SM          SAPOPEMBA       281                          TURQUIA   
3858  SM          SAPOPEMBA       281                          TURQUIA   

       ETAPA          SERIE  QTDE REDE   DATABASE  
0     CRECHE   MINI GRUPO I     1  CON 2024-12-31  
1     CRECHE     BERCARIO I     1  CON 2024-12-31  
2       FUND  C.II 4.ANO F9     1  DIR 2024-12-31  
3       FUND   C.I 3.ANO F9     1  DIR 2024-12-31  
4     CRECHE    BERCARIO II     2  CON 2024-12-31  
...      ...            ...   ...  ...        ...  
3854    FUND  C.II 6.ANO F9     1  DIR 2024-12-31  
3855    FUND  C.II 4.ANO F9     1  DIR 2024-12-31  
3856     EJA       MI CIEJA     1  DIR 2024-12-31  
3857  CRECHE    BERCARIO II     1  CON 2024-12-31  
3858  CRECHE    MINI G UNIF     1  CON 2024-12-31  

[3859 rows x 9 columns]

In [43]:
# Recortes: País de Procedência, Distrito, Tipo de Rede (Direta ou Conveniada/Parceira), Etapa (Creche, fundamental, EJA etc.)
alunos_est_cols = ['DISTRITO',
                   'COD_PAIS',
                   'NOME_PAIS',
                   'ETAPA',
                   'REDE',
                   'QTDE']

alunos_est_2024 = alunos_est_2024[alunos_est_cols]

alunos_est_2024

DISTRITO  COD_PAIS                        NOME_PAIS   ETAPA  \
0     ALTO DE PINHEIROS        42                            CHINA  CRECHE   
1     ALTO DE PINHEIROS       226                       SERRA LEOA  CRECHE   
2               BUTANTA        26                         COLÔMBIA    FUND   
3               BUTANTA        31                          BÉLGICA    FUND   
4               BUTANTA        36  ESTADOS UNIDOS DA AMÉRICA (EUA)  CRECHE   
...                 ...       ...                              ...     ...   
3854          SAPOPEMBA       185                            CONGO    FUND   
3855          SAPOPEMBA       213                          NIGÉRIA    FUND   
3856          SAPOPEMBA       277                            SÍRIA     EJA   
3857          SAPOPEMBA       281                          TURQUIA  CRECHE   
3858          SAPOPEMBA       281                          TURQUIA  CRECHE   

     REDE  QTDE  
0     CON     1  
1     CON     1  
2     DIR     1  
3     DIR     1  
4     CON     2  
...   ...   ...  
3854  DIR     1  
3855  DIR     1  
3856  DIR     1  
3857  CON     1  
3858  CON     1  

[3859 rows x 6 columns]

## Número de alunos beneficiários do Bolsa Família

O oitavo indicador é o número de alunos beneficiários do Bolsa Família da rede municipal, segmentado por Distrito e nível de ensino.

O conjunto de dados que contém esse indicador está disponível em http://dados.prefeitura.sp.gov.br/dataset/beneficiarios-programa-bolsa-familia-creches-municipais-e-conveniadas. Sabendo que o último trecho da url representa a id do conjunto de dados, vamos utilizá-la para fazer a extração dos dados do portal.

As notas (que podem ser vistas na saída abaixo) desse conjunto de dados incluem a informação de que a estrutura do conjunto mudou a partir de 2024 e, por isso, foi criado um novo conjunto de dados com a estrutura mais recente, disponível em http://dados.prefeitura.sp.gov.br/dataset/beneficiarios-do-programa-bolsa-familia-por-etapa-de-ensino-da-rede-municipal-de-educacao. Vamos utilizar essa versão mais recente e os dados de julho de 2024, assim como o número de alunos estrangeiros.

In [44]:
pkg_name = 'beneficiarios-programa-bolsa-familia-creches-municipais-e-conveniadas'
pkg = da.package_show(pkg_name)
print(pkg['notes'])

***Atualizado em: 23/09/2023***

Esta base de dados traz a série histórica de 10 anos com a quantidade de crianças beneficiárias pelo Programa Bolsa Família e matriculadas em creches municipais ou conveniadas entre os anos de 2013 e 2023.

As informações foram compiladas pela Secretaria Municipal de Educação, a partir de cruzamento do Sistema EOL com dados da Secretaria Municipal de Assistência Social utilizando a chave NIS do Aluno ou Nome do Aluno, mãe e nascimento, o que pode ocasionar variações de números por divergências cadastrais.

Nota técnica: A partir do mês de dezembro de 2021, o Programa Bolsa Família foi substituído pela Programa Auxílio Brasil, conforme Lei Federal nº 14.284/2021. Dessa forma, o conjunto de dados referente ao ano de 2022 encontra-se denominado como "Beneficiários do Programa Auxílio Brasil (Creche)". No entanto, em 19 junho de 2023, o Programa Auxílio Brasil volta a se chamar Programa Bolsa Família, conforme Lei Federal nº 14.601/2023 e por esse motivo a 

In [45]:
pkg_name = 'beneficiarios-do-programa-bolsa-familia-por-etapa-de-ensino-da-rede-municipal-de-educacao'
resources = da.package_resources(pkg_name, '24')
resources

[{'name': 'Dicionário de Variáveis Programa Bolsa Família por Etapa',
  'id': 'c36429c0-b9da-478d-b32e-c9ffd31adfce',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/2e1a7fe7-284f-445a-8566-031f689f1b54/resource/c36429c0-b9da-478d-b32e-c9ffd31adfce/download/dicionarariovariaveis_novabolsafamilia_jul2024.csv'},
 {'name': 'Dicionário de Variáveis Programa Bolsa Família por Etapa',
  'id': 'f1cf5dd5-c248-4c34-b1b0-dfb3d6f7ec1c',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/2e1a7fe7-284f-445a-8566-031f689f1b54/resource/f1cf5dd5-c248-4c34-b1b0-dfb3d6f7ec1c/download/dicionarariovariaveis_novabolsafamilia_jul2024.xlsx'},
 {'name': 'Programa Bolsa Família por Etapa - Jul24',
  'id': '8999e4a8-9cbc-4fd6-b7ce-cef505e55f34',
  'url': 'https://dados.prefeitura.sp.gov.br/dataset/2e1a7fe7-284f-445a-8566-031f689f1b54/resource/8999e4a8-9cbc-4fd6-b7ce-cef505e55f34/download/novabolsafamilia_julho2024.csv'},
 {'name': 'Programa Bolsa Família por Etapa - Jul24',
  'id': '29f089e7-2de2-4295-9d

A última data disponível permanece sendo a de julho de 2024, então vamos utilizar essa data para extrair os dados.

In [46]:
resource_id = resources[2]['id']
alunos_bf_2024 = da.load_resource(resource_id)
alunos_bf_2024

CODEOL       TIPO                               UNIDADE  \
0         86       EMEI            PAULO CAMILHIER FLORENCANO   
1         94       EMEI                VICENTE PAULO DA SILVA   
2        108       EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3        191       EMEF             ALIPIO CORREA NETO, PROF.   
4        205      EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...      ...        ...                                   ...   
3758  400902  CEI INDIR                            ISMAEL IVO   
3759  400903  CEI INDIR                    JOSE DIAS SOBRINHO   
3760  400904  CEI INDIR                         RUBEM FONSECA   
3761  400906  CEI INDIR                   ZIRALDO ALVES PINTO   
3762  400908  CEI INDIR           RUTH VIDAL DA SILVA MARTINS   

                  DIRETORIA         DISTRITO  CRECHE  PRE ESCOLA  \
0                GUAIANASES       GUAIANASES       0         140   
1     FREGUESIA/BRASILANDIA            LIMAO       0         145   
2                SAO MIGUEL    JARDIM HELENA       0           0   
3                   BUTANTA       VILA SONIA       0           0   
4                  PIRITUBA         PIRITUBA       0           0   
...                     ...              ...     ...         ...   
3758               IPIRANGA        SAO LUCAS      21           0   
3759        JACANA/TREMEMBE         TREMEMBE      81          40   
3760                  PENHA       PONTE RASA      19          16   
3761  FREGUESIA/BRASILANDIA      BRASILANDIA      15          31   
3762               PIRITUBA  VILA LEOPOLDINA      19           0   

      ENSINO FUNDAMENTAL  EDUCAÇÃO PROFISSIONAL  ENSINO MEDIO  \
0                      0                      0             0   
1                      0                      0             0   
2                    324                      0             0   
3                    193                      0             0   
4                      0                      0             0   
...                  ...                    ...           ...   
3758                   0                      0             0   
3759                   0                      0             0   
3760                   0                      0             0   
3761                   0                      0             0   
3762                   0                      0             0   

      EDUCAÇÃO ESPECIAL  TOTAL MATRICULAS    DATABASE  
0                     0               140  31/07/2024  
1                     0               145  31/07/2024  
2                     0               324  31/07/2024  
3                     0               193  31/07/2024  
4                     8                 8  31/07/2024  
...                 ...               ...         ...  
3758                  0                21  31/07/2024  
3759                  0               121  31/07/2024  
3760                  0                35  31/07/2024  
3761                  0                46  31/07/2024  
3762                  0                19  31/07/2024  

[3763 rows x 13 columns]

In [47]:
# Recortes: Alunos Beneficiários do Bolsa-Família por distrito, por nível de Ensino
alunos_bf_cols = ['CODEOL',
                   'TIPO',
                   'UNIDADE',
                   'DIRETORIA',
                   'DISTRITO',
                   'CRECHE',
                   'PRE ESCOLA',
                   'ENSINO FUNDAMENTAL',
                   'EDUCAÇÃO PROFISSIONAL',
                   'ENSINO MEDIO',
                   'EDUCAÇÃO ESPECIAL']

alunos_bf_2024 = alunos_bf_2024[alunos_bf_cols]

alunos_bf_2024

CODEOL       TIPO                               UNIDADE  \
0         86       EMEI            PAULO CAMILHIER FLORENCANO   
1         94       EMEI                VICENTE PAULO DA SILVA   
2        108       EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3        191       EMEF             ALIPIO CORREA NETO, PROF.   
4        205      EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...      ...        ...                                   ...   
3758  400902  CEI INDIR                            ISMAEL IVO   
3759  400903  CEI INDIR                    JOSE DIAS SOBRINHO   
3760  400904  CEI INDIR                         RUBEM FONSECA   
3761  400906  CEI INDIR                   ZIRALDO ALVES PINTO   
3762  400908  CEI INDIR           RUTH VIDAL DA SILVA MARTINS   

                  DIRETORIA         DISTRITO  CRECHE  PRE ESCOLA  \
0                GUAIANASES       GUAIANASES       0         140   
1     FREGUESIA/BRASILANDIA            LIMAO       0         145   
2                SAO MIGUEL    JARDIM HELENA       0           0   
3                   BUTANTA       VILA SONIA       0           0   
4                  PIRITUBA         PIRITUBA       0           0   
...                     ...              ...     ...         ...   
3758               IPIRANGA        SAO LUCAS      21           0   
3759        JACANA/TREMEMBE         TREMEMBE      81          40   
3760                  PENHA       PONTE RASA      19          16   
3761  FREGUESIA/BRASILANDIA      BRASILANDIA      15          31   
3762               PIRITUBA  VILA LEOPOLDINA      19           0   

      ENSINO FUNDAMENTAL  EDUCAÇÃO PROFISSIONAL  ENSINO MEDIO  \
0                      0                      0             0   
1                      0                      0             0   
2                    324                      0             0   
3                    193                      0             0   
4                      0                      0             0   
...                  ...                    ...           ...   
3758                   0                      0             0   
3759                   0                      0             0   
3760                   0                      0             0   
3761                   0                      0             0   
3762                   0                      0             0   

      EDUCAÇÃO ESPECIAL  
0                     0  
1                     0  
2                     0  
3                     0  
4                     8  
...                 ...  
3758                  0  
3759                  0  
3760                  0  
3761                  0  
3762                  0  

[3763 rows x 11 columns]

In [48]:
alunos_bf_id_vars = alunos_bf_cols[0:5]

alunos_bf_2024 = alunos_bf_2024.melt(id_vars=alunos_bf_id_vars,
                    var_name='NIVEL',
                    value_name='QTDE')

alunos_bf_2024

CODEOL       TIPO                               UNIDADE  \
0          86       EMEI            PAULO CAMILHIER FLORENCANO   
1          94       EMEI                VICENTE PAULO DA SILVA   
2         108       EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3         191       EMEF             ALIPIO CORREA NETO, PROF.   
4         205      EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...       ...        ...                                   ...   
22573  400902  CEI INDIR                            ISMAEL IVO   
22574  400903  CEI INDIR                    JOSE DIAS SOBRINHO   
22575  400904  CEI INDIR                         RUBEM FONSECA   
22576  400906  CEI INDIR                   ZIRALDO ALVES PINTO   
22577  400908  CEI INDIR           RUTH VIDAL DA SILVA MARTINS   

                   DIRETORIA         DISTRITO              NIVEL  QTDE  
0                 GUAIANASES       GUAIANASES             CRECHE     0  
1      FREGUESIA/BRASILANDIA            LIMAO             CRECHE     0  
2                 SAO MIGUEL    JARDIM HELENA             CRECHE     0  
3                    BUTANTA       VILA SONIA             CRECHE     0  
4                   PIRITUBA         PIRITUBA             CRECHE     0  
...                      ...              ...                ...   ...  
22573               IPIRANGA        SAO LUCAS  EDUCAÇÃO ESPECIAL     0  
22574        JACANA/TREMEMBE         TREMEMBE  EDUCAÇÃO ESPECIAL     0  
22575                  PENHA       PONTE RASA  EDUCAÇÃO ESPECIAL     0  
22576  FREGUESIA/BRASILANDIA      BRASILANDIA  EDUCAÇÃO ESPECIAL     0  
22577               PIRITUBA  VILA LEOPOLDINA  EDUCAÇÃO ESPECIAL     0  

[22578 rows x 7 columns]

## Distritos e Subprefeituras

Para agregarmos os dados em Subprefeituras, precisamos de uma lista de distritos e subprefeituras. A lista de distritos e subprefeituras pode ser obtida no GeoSampa, que é o portal de dados geográficos da Prefeitura de São Paulo.

In [49]:
gs.get_capabilities('distrito')

[{'name': 'geoportal:central_triagem_cooperativa',
  'title': 'Cooperativas Habilitadas',
  'abstract': 'Atualmente 93 distritos são contemplados pela Coleta de Materiais Recicláveis realizada pelas Centrais e pelas Concessionárias, ficando a sua coordenação sob a responsabilidade da Secretaria Municipal de Serviços, por intermédio da Autoridade Municipal de Limpeza Urbana – AMLURB, estabelecendo normas e procedimentos para sua implementação, gerenciamento, fiscalização e controle. Das 22 organizações que mantêm uma relação formal com a Prefeitura de São Paulo, 21 cooperativas ou associações que desenvolvem atividades de coleta, triagem e comercialização de RSD Secos, e uma desenvolve atividades de recuperação de resíduos eletroeletrônicos (REE).'},
 {'name': 'geoportal:distrito_municipal',
  'title': 'Distrito',
  'abstract': 'Os distritos foram criados mediante a Lei nº 11.220/1992. Seus limites foram estabelecidos a partir de estudos elaborados por diversos órgãos do Executivo munic

In [50]:
df_dist = gs.get_features('geoportal:distrito_municipal')
df_dist

id  cd_identificador_distrito  \
0   distrito_municipal.8583394                    8583394   
1   distrito_municipal.8583395                    8583395   
2   distrito_municipal.8583396                    8583396   
3   distrito_municipal.8583397                    8583397   
4   distrito_municipal.8583398                    8583398   
..                         ...                        ...   
91  distrito_municipal.8583485                    8583485   
92  distrito_municipal.8583486                    8583486   
93  distrito_municipal.8583487                    8583487   
94  distrito_municipal.8583488                    8583488   
95  distrito_municipal.8583489                    8583489   

    cd_identificador_subprefeitura cd_distrito_municipal  \
0                                5                    51   
1                               20                    52   
2                               12                    32   
3                               25                    53   
4                               10                    54   
..                             ...                   ...   
91                              27                    47   
92                              28                    96   
93                               8                    48   
94                               9                    49   
95                               4                    50   

   nm_distrito_municipal sg_distrito_municipal tx_escala sg_fonte_original  \
0               MANDAQUI                   MAN    1:5000            GEOGSG   
1               MARSILAC                   MAR    1:5000            GEOGSG   
2                  MOEMA                   MOE    1:5000            GEOGSG   
3                  MOOCA                   MOO    1:5000            GEOGSG   
4                MORUMBI                   MOR    1:5000            GEOGSG   
..                   ...                   ...       ...               ...   
91        JOSE BONIFACIO                   JBO    1:5000            GEOGSG   
92               LAJEADO                   LAJ    1:5000            GEOGSG   
93                  LAPA                   LAP    1:5000            GEOGSG   
94             LIBERDADE                   LIB    1:5000            GEOGSG   
95                 LIMAO                   LIM    1:5000            GEOGSG   

   dt_criacao                   dt_atualizacao cd_usuario_atualizacao  \
0  2004-01-01 2025-07-05 03:54:17.086000+00:00                   None   
1  2004-01-01 2025-07-05 03:54:17.153000+00:00                   None   
2  2004-01-01 2025-07-05 03:54:16.869000+00:00                   None   
3  2004-01-01 2025-07-05 03:54:16.901000+00:00                   None   
4  2004-01-01 2025-07-05 03:54:16.788000+00:00                   None   
..        ...                              ...                    ...   
91 2004-01-01 2025-07-05 03:54:16.952000+00:00                   None   
92 2004-01-01 2025-07-05 03:54:16.935000+00:00                   None   
93 2004-01-01 2025-07-05 03:54:17.002000+00:00                   None   
94 2004-01-01 2025-07-05 03:54:16.758000+00:00                   None   
95 2004-01-01 2025-07-05 03:54:17.069000+00:00                   None   

    cd_tipo_discrepancia  qt_area_quilometro  qt_area_metro  \
0              199299399              13.249   1.324946e+07   
1              199299399             208.165   2.081650e+08   
2              199299399               9.080   9.079516e+06   
3              199299399               7.949   7.948972e+06   
4              199299399              11.489   1.148932e+07   
..                   ...                 ...            ...   
91             199299399              14.570   1.456975e+07   
92             199299399               8.827   8.826983e+06   
93             199299399              10.283   1.028273e+07   
94             199299399               3.651   3.651130e+06   
95             199299399               6.457   6.456916e+06   

   

In [51]:
gs.get_capabilities('subprefeitura')

[{'name': 'geoportal:GEOSAMPA_v_praca_largo',
  'title': 'Cadastro de Praças e Largos',
  'abstract': 'Localização das praças e largos no território do município de São Paulo, com base nas informações repassadas por subprefeituras, SF e SEGES/CGPATRI.'},
 {'name': 'geoportal:perimetro_zoneamento_revogado_lei13885',
  'title': 'Perímetro Zona de Uso - Revogado - Lei 13.885/04',
  'abstract': 'A Lei de Zoneamento estabelece normas complementares ao Plano Diretor Estratégico, institui os Planos Regionais Estratégicos das Subprefeituras, dispõe sobre o parcelamento, disciplina e ordena o Uso e Ocupação do Solo do Município de São Paulo. Os perímetros de zona de uso foram vetorizados perante o estabelecido na Lei nº 13.885/2004, tendo como base cartográfica o Mapa Digital da Cidade (MDC).'},
 {'name': 'geoportal:sede_subprefeitura',
  'title': 'Subprefeituras',
  'abstract': 'Localização das sedes físicas das Subprefeituras da Cidade de São Paulo.'},
 {'name': 'geoportal:subprefeitura',
  '

In [52]:
df_subs = gs.get_features('geoportal:subprefeitura')
df_subs

id  cd_identificador_subprefeitura cd_subprefeitura  \
0    subprefeitura.1                               1               02   
1    subprefeitura.2                               2               03   
2    subprefeitura.3                               3               04   
3    subprefeitura.4                               4               05   
4    subprefeitura.5                               5               06   
5    subprefeitura.6                               6               07   
6    subprefeitura.7                               7               21   
7    subprefeitura.8                               8               22   
8    subprefeitura.9                               9               23   
9   subprefeitura.10                              10               24   
10  subprefeitura.11                              11               27   
11  subprefeitura.12                              12               28   
12  subprefeitura.13                              13               08   
13  subprefeitura.14                              14               09   
14  subprefeitura.15                              15               25   
15  subprefeitura.16                              16               26   
16  subprefeitura.17                              17               30   
17  subprefeitura.18                              18               29   
18  subprefeitura.19                              19               13   
19  subprefeitura.20                              20               12   
20  subprefeitura.21                              21               10   
21  subprefeitura.22                              22               11   
22  subprefeitura.23                              23               17   
23  subprefeitura.24                              24               18   
24  subprefeitura.25                              25               19   
25  subprefeitura.26                              26               16   
26  subprefeitura.27                              27               20   
27  subprefeitura.28                              28               15   
28  subprefeitura.29                              29               14   
29  subprefeitura.30                              30               31   
30  subprefeitura.31                              31               01   
31  subprefeitura.32                              32               32   

             nm_subprefeitura tx_escala sg_fonte_original dt_criacao  \
0            PIRITUBA-JARAGUA    1:5000            GEOGSG 2023-11-30   
1       FREGUESIA-BRASILANDIA    1:5000            GEOGSG 2023-11-30   
2     CASA VERDE-CACHOEIRINHA    1:5000            GEOGSG 2023-11-30   
3            SANTANA-TUCURUVI    1:5000            GEOGSG 2023-11-30   
4             JACANA-TREMEMBE    1:5000            GEOGSG 2023-11-30   
5   VILA MARIA-VILA GUILHERME    1:5000            GEOGSG 2023-11-30   
6                       PENHA    1:5000            GEOGSG 2023-11-30   
7          ERMELINO MATARAZZO    1:5000            GEOGSG 2023-11-30   
8                  SAO MIGUEL    1:5000            GEOGSG 2023-11-30   
9              ITAIM PAULISTA    1:5000            GEOGSG 2023-11-30   
10                   ITAQUERA    1:5000            GEOGSG 2023-11-30   
11                 GUAIANASES    1:5000            GEOGSG 2023-11-30   
12                       LAPA    1:5000            GEOGSG 2023-11-30   
13                         SE    1:5000            GEOGSG 2023-11-30   
14                      MOOCA    1:5000            GEOGSG 2023-11-30   
15  ARICANDUVA-FORMOSA-CARRAO    1:5000            GEOGSG 2023-11-30   
16                 SAO MATEUS    1:5000            GEOGSG 2023-11-30   
17              VILA PRUDENTE    1:5000            GEOGSG 2023-11-30   
18                   IPIRANGA    1:5000            GEOGSG 2023-11-30   
19               VILA MARIANA    1:5000            GEOGSG 2023-11-30   
20                    BUTANTA    1:5000            GEOGSG 2023-11-30   
21                  PINH

## CSV de Subprefeituras do Qlik

In [53]:
url_subs = os.environ.get('CSV_SUBPREFEITURAS_QLIK')
df_subs_qlik = pd.read_csv(url_subs)
df_subs_qlik

sub.CODIGO                   sub.NOME  \
0            1                      PERUS   
1            2           PIRITUBA-JARAGUA   
2            3      FREGUESIA-BRASILANDIA   
3            4    CASA VERDE-CACHOEIRINHA   
4            5           SANTANA-TUCURUVI   
5            6            JACANA-TREMEMBE   
6            7  VILA MARIA-VILA GUILHERME   
7            8                       LAPA   
8            9                         SE   
9           10                    BUTANTA   
10          11                  PINHEIROS   
11          12               VILA MARIANA   
12          13                   IPIRANGA   
13          14                SANTO AMARO   
14          15                  JABAQUARA   
15          16              CIDADE ADEMAR   
16          17                CAMPO LIMPO   
17          18                M BOI MIRIM   
18          19          CAPELA DO SOCORRO   
19          20                PARELHEIROS   
20          21                      PENHA   
21          22         ERMELINO MATARAZZO   
22          23                 SAO MIGUEL   
23          24             ITAIM PAULISTA   
24          25                      MOOCA   
25          26  ARICANDUVA-FORMOSA-CARRAO   
26          27                   ITAQUERA   
27          28                 GUAIANASES   
28          29              VILA PRUDENTE   
29          30                 SAO MATEUS   
30          31          CIDADE TIRADENTES   
31          32                  SAPOPEMBA   

                                         sub.POLIGONO  total_de_pessoas  
0   [[[[-46.7082012617476,-23.4165818252815],[-46....            163076  
1   [[[[-46.7753669019781,-23.4628032705496],[-46....            480225  
2   [[[[-46.6910223492151,-23.5088410763715],[-46....            380513  
3   [[[[-46.673577305455,-23.479858692024],[-46.67...            306275  
4   [[[[-46.6251942372966,-23.5193645522374],[-46....            318913  
5   [[[[-46.6138088697146,-23.4620183373337],[-46....            283892  
6   [[[[-46.5985584306269,-23.4916579527685],[-46....            276069  
7   [[[[-46.7475634318888,-23.5587659797062],[-46....            338347  
8   [[[[-46.6634017492882,-23.5366395157441],[-46....            423536  
9   [[[[-46.7579053376809,-23.5510466758162],[-46....            468522  
10  [[[[-46.6873257325884,-23.6261005948649],[-46....            285815  
11  [[[[-46.6466231102846,-23.6318751226343],[-46....            337654  
12  [[[[-46.6144174088106,-23.5817429681912],[-46....            480878  
13  [[[[-46.6871184024493,-23.6262042574839],[-46....            272308  
14  [[[[-46.6514911841313,-23.639281619134],[-46.6...            214982  
15  [[[[-46.6436598239316,-23.6711448733991],[-46....            412804  
16  [[[[-46.7488186849265,-23.6170307889433],[-46....            675598  
17  [[[[-46.7978153624677,-23.6966712465463],[-46....            570809  
18  [[[[-46.7239680778519,-23.7003633100076],[-46....            605383  
19  [[[[-46.7670823703732,-23.7542674823043],[-46....            165138  
20  [[[[-46.5001019550132,-23.4772971422316],[-46....            472757  
21  [[[[-46.4777764784187,-23.5079412725303],[-46....            202214  
22  [[[[-46.4450300522138,-23.5259251812641],[-46....            344609  
23  [[[[-46.4064461192725,-23.5289195706913],[-46....            345968  
24  [[[[-46.6248908345177,-23.5343267292496],[-46....            377163  
25  [[[[-46.5540056763679,-23.5550942316414],[-46....            266157  
26  [[[[-46.4322812602783,-23.5263593067658],[-46....            550540  
27  [[[[-46.4234585487012,-23.5393558027579],[-46....            273707  
28  [[[[-46.5794802013929,-23.6045586898005],[-46....            243728  
29  [[[[-46.4838565669135,-23.6236721840668],[-46....            453527  
30  [[[[-46.3975119128078,-23.6154254384527],[-46....            194177  
31  [[[[-46.5228118371426,-23.6138210842128],[-46....            266715

In [54]:
df_subs_qlik = df_subs_qlik[['sub.CODIGO', 'sub.NOME']]
df_subs_qlik

sub.CODIGO                   sub.NOME
0            1                      PERUS
1            2           PIRITUBA-JARAGUA
2            3      FREGUESIA-BRASILANDIA
3            4    CASA VERDE-CACHOEIRINHA
4            5           SANTANA-TUCURUVI
5            6            JACANA-TREMEMBE
6            7  VILA MARIA-VILA GUILHERME
7            8                       LAPA
8            9                         SE
9           10                    BUTANTA
10          11                  PINHEIROS
11          12               VILA MARIANA
12          13                   IPIRANGA
13          14                SANTO AMARO
14          15                  JABAQUARA
15          16              CIDADE ADEMAR
16          17                CAMPO LIMPO
17          18                M BOI MIRIM
18          19          CAPELA DO SOCORRO
19          20                PARELHEIROS
20          21                      PENHA
21          22         ERMELINO MATARAZZO
22          23                 SAO MIGUEL
23          24             ITAIM PAULISTA
24          25                      MOOCA
25          26  ARICANDUVA-FORMOSA-CARRAO
26          27                   ITAQUERA
27          28                 GUAIANASES
28          29              VILA PRUDENTE
29          30                 SAO MATEUS
30          31          CIDADE TIRADENTES
31          32                  SAPOPEMBA

## Orçamento previsto/liquidado na função Educação

Vamos começar coletando os dados orçamentários do site de execução orçamentária da Secretaria da Fazenda.

In [55]:
url_orcamento = 'https://orcamento.sf.prefeitura.sp.gov.br/orcamento/uploads/2024/basedadosexecucao_1224.csv'
df_orcamento = pd.read_csv(url_orcamento,
                           sep=';',
                           decimal=',',
                           encoding='latin1',
                           dtype=str)
df_orcamento

DataInicial   DataFinal Cd_AnoExecucao Cd_Exercicio Cd_Dotacao_Id  \
0     01/01/2024  31/12/2024           2024         2024        169108   
1     01/01/2024  31/12/2024           2024         2024        173723   
2     01/01/2024  31/12/2024           2024         2024        171046   
3     01/01/2024  31/12/2024           2024         2024        173862   
4     01/01/2024  31/12/2024           2024         2024        180471   
...          ...         ...            ...          ...           ...   
9339  01/01/2024  31/12/2024           2024         2024        164854   
9340  01/01/2024  31/12/2024           2024         2024        182836   
9341  01/01/2024  31/12/2024           2024         2024        173543   
9342  01/01/2024  31/12/2024           2024         2024        164855   
9343  01/01/2024  31/12/2024           2024         2024        173540   

     Administracao Cd_Orgao Sigla_Orgao  \
0           Direta       07         FMD   
1           Direta       07         FMD   
2           Direta       07         FMD   
3           Direta       07         FMD   
4           Direta       07         FMD   
...            ...      ...         ...   
9339   Legislativo       77      FTCMSP   
9340   Legislativo       77      FTCMSP   
9341   Legislativo       77      FTCMSP   
9342   Legislativo       77      FTCMSP   
9343   Legislativo       77      FTCMSP   

                                              Ds_Orgao Cd_Unidade  ...  \
0            Fundo Municipal de Desenvolvimento Social         10  ...   
1            Fundo Municipal de Desenvolvimento Social         10  ...   
2            Fundo Municipal de Desenvolvimento Social         10  ...   
3            Fundo Municipal de Desenvolvimento Social         10  ...   
4            Fundo Municipal de Desenvolvimento Social         10  ...   
...                                                ...        ...  ...   
9339  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9340  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9341  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9342  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9343  Fundo Especial de Despesas do Tribunal de Contas         10  ...   

     Vl_Congelado Vl_Descongelado Vl_CongeladoLiquido   Disponivel  \
0               0               0                   0         1000   
1               0               0                   0    1317978,6   
2               0               0                   0    3131324,4   
3               0               0                   0  37258939,15   
4               0               0                   0      2000000   
...           ...             ...                 ...          ...   
9339            0               0                   0        24000   
9340            0               0                   0        20000   
9341            0               0                   0       400000   
9342            0               0                   0         6252   
9343            0               0                   0            0   

     Vl_ReservadoLiquido Vl_EmpenhadoLiquido Vl_Liquidado      Vl_Pago  \
0                      0                   0            0            0   
1                1314177             1314177      1314177      1314177   
2              3131324,4           3131324,4    2940879,9   2791266,85   
3            37222552,12         37222552,12  30999672,71  30291725,36   
4                2000000             2000000      2000000      2000000   
...                  ...                 ...          ...          ...   
9339                   0                   0            0            0   
9340                1856                1856         1856         1856   
9341           201545,67           201545,67    201545,67    201545,67   
9342                   0                   0            0            0   
9343                   0                   0           

In [56]:
for col in [col for col in df_orcamento.columns if 'Vl' in col]:
    df_orcamento[col] = df_orcamento[col].str.replace(',', '.').astype(float)
df_orcamento['DataExtracao'] = pd.to_datetime(df_orcamento['DataExtracao'], format='%d/%m/%Y')
df_orcamento

DataInicial   DataFinal Cd_AnoExecucao Cd_Exercicio Cd_Dotacao_Id  \
0     01/01/2024  31/12/2024           2024         2024        169108   
1     01/01/2024  31/12/2024           2024         2024        173723   
2     01/01/2024  31/12/2024           2024         2024        171046   
3     01/01/2024  31/12/2024           2024         2024        173862   
4     01/01/2024  31/12/2024           2024         2024        180471   
...          ...         ...            ...          ...           ...   
9339  01/01/2024  31/12/2024           2024         2024        164854   
9340  01/01/2024  31/12/2024           2024         2024        182836   
9341  01/01/2024  31/12/2024           2024         2024        173543   
9342  01/01/2024  31/12/2024           2024         2024        164855   
9343  01/01/2024  31/12/2024           2024         2024        173540   

     Administracao Cd_Orgao Sigla_Orgao  \
0           Direta       07         FMD   
1           Direta       07         FMD   
2           Direta       07         FMD   
3           Direta       07         FMD   
4           Direta       07         FMD   
...            ...      ...         ...   
9339   Legislativo       77      FTCMSP   
9340   Legislativo       77      FTCMSP   
9341   Legislativo       77      FTCMSP   
9342   Legislativo       77      FTCMSP   
9343   Legislativo       77      FTCMSP   

                                              Ds_Orgao Cd_Unidade  ...  \
0            Fundo Municipal de Desenvolvimento Social         10  ...   
1            Fundo Municipal de Desenvolvimento Social         10  ...   
2            Fundo Municipal de Desenvolvimento Social         10  ...   
3            Fundo Municipal de Desenvolvimento Social         10  ...   
4            Fundo Municipal de Desenvolvimento Social         10  ...   
...                                                ...        ...  ...   
9339  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9340  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9341  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9342  Fundo Especial de Despesas do Tribunal de Contas         10  ...   
9343  Fundo Especial de Despesas do Tribunal de Contas         10  ...   

     Vl_Congelado Vl_Descongelado Vl_CongeladoLiquido   Disponivel  \
0             0.0             0.0                 0.0         1000   
1             0.0             0.0                 0.0    1317978,6   
2             0.0             0.0                 0.0    3131324,4   
3             0.0             0.0                 0.0  37258939,15   
4             0.0             0.0                 0.0      2000000   
...           ...             ...                 ...          ...   
9339          0.0             0.0                 0.0        24000   
9340          0.0             0.0                 0.0        20000   
9341          0.0             0.0                 0.0       400000   
9342          0.0             0.0                 0.0         6252   
9343          0.0             0.0                 0.0            0   

     Vl_ReservadoLiquido Vl_EmpenhadoLiquido Vl_Liquidado      Vl_Pago  \
0                   0.00                0.00         0.00         0.00   
1             1314177.00          1314177.00   1314177.00   1314177.00   
2             3131324.40          3131324.40   2940879.90   2791266.85   
3            37222552.12         37222552.12  30999672.71  30291725.36   
4             2000000.00          2000000.00   2000000.00   2000000.00   
...                  ...                 ...          ...          ...   
9339                0.00                0.00         0.00         0.00   
9340             1856.00             1856.00      1856.00      1856.00   
9341           201545.67           201545.67    201545.67    201545.67   
9342                0.00                0.00         0.00         0.00   
9343                0.00                0.00         0.

In [57]:
df_orcamento = df_orcamento.loc[df_orcamento['Cd_Funcao']=='12']
df_orcamento

DataInicial   DataFinal Cd_AnoExecucao Cd_Exercicio Cd_Dotacao_Id  \
589   01/01/2024  31/12/2024           2024         2024        174256   
590   01/01/2024  31/12/2024           2024         2024        174471   
591   01/01/2024  31/12/2024           2024         2024        174505   
592   01/01/2024  31/12/2024           2024         2024        174450   
593   01/01/2024  31/12/2024           2024         2024        166524   
...          ...         ...            ...          ...           ...   
8946  01/01/2024  31/12/2024           2024         2024        181463   
8947  01/01/2024  31/12/2024           2024         2024        164952   
8948  01/01/2024  31/12/2024           2024         2024        180889   
8949  01/01/2024  31/12/2024           2024         2024        173088   
8950  01/01/2024  31/12/2024           2024         2024        180892   

     Administracao Cd_Orgao Sigla_Orgao  \
589         Direta       16         SME   
590         Direta       16         SME   
591         Direta       16         SME   
592         Direta       16         SME   
593         Direta       16         SME   
...            ...      ...         ...   
8946      Indireta       80       FPETC   
8947      Indireta       80       FPETC   
8948      Indireta       80       FPETC   
8949      Indireta       80       FPETC   
8950      Indireta       80       FPETC   

                                               Ds_Orgao Cd_Unidade  ...  \
589                    Secretaria Municipal de Educação         10  ...   
590                    Secretaria Municipal de Educação         10  ...   
591                    Secretaria Municipal de Educação         10  ...   
592                    Secretaria Municipal de Educação         10  ...   
593                    Secretaria Municipal de Educação         10  ...   
...                                                 ...        ...  ...   
8946  Fundação Paulistana de Educação Tecnologia e C...         10  ...   
8947  Fundação Paulistana de Educação Tecnologia e C...         10  ...   
8948  Fundação Paulistana de Educação Tecnologia e C...         10  ...   
8949  Fundação Paulistana de Educação Tecnologia e C...         10  ...   
8950  Fundação Paulistana de Educação Tecnologia e C...         10  ...   

     Vl_Congelado Vl_Descongelado Vl_CongeladoLiquido Disponivel  \
589           0.0            0.00                0.00          0   
590           0.0            0.00                0.00     100000   
591           0.0            0.00                0.00   39535,03   
592           0.0            0.00                0.00          0   
593        1000.0         1000.00                0.00          0   
...           ...             ...                 ...        ...   
8946          0.0            0.00                0.00    1497,82   
8947      10000.0        10000.00                0.00          0   
8948          0.0            0.00                0.00          0   
8949      30000.0        30000.00                0.00          0   
8950    8009864.5      7935537.17            74327.33  6007635,5   

     Vl_ReservadoLiquido Vl_EmpenhadoLiquido Vl_Liquidado     Vl_Pago  \
589                 0.00                0.00         0.00        0.00   
590            100000.00           100000.00    100000.00   100000.00   
591             39535.03            39535.03       657.91      657.91   
592                 0.00                0.00         0.00        0.00   
593                 0.00                0.00         0.00        0.00   
...                  ...                 ...          ...         ...   
8946             1497.82             1497.82      1497.82     1497.82   
8947                0.00                0.00         0.00        0.00   
8948                0.00                0.00         0.00        0.00   
8949                0.00                0.00         0.00        0.00   
8950          6007635.50          6007635.50   5763100.00  5763100.00   

    

## Orçamento regionalizado na função Educação

O orçamento é regionalizado apenas na liquidação, então não é possível obter o orçamento previsto por subprefeitura, mas é possível obter o orçamento liquidado.

In [58]:
url_orcamento_r = 'https://orcamento.sf.prefeitura.sp.gov.br/orcamento/uploads/2024/basedadosDA_1224.csv'
df_orcamento_r = pd.read_csv(url_orcamento_r,
                           sep=';',
                           decimal=',',
                           encoding='latin1',
                           dtype=str)
df_orcamento_r

COD_EMPRESA_PMSP COD_EMPENHO ANO_EMPENHO CÓDIGO_NLP ANO_LIQUIDAÇÃO  \
0                    01           1        2024       5695           2025   
1                    01           1        2024       5878           2025   
2                    01           1        2024       7627           2025   
3                    01           1        2024      43181           2025   
4                    01           1        2024      43192           2025   
...                 ...         ...         ...        ...            ...   
531053               91         148        2024        110           2025   
531054               91         149        2024         85           2025   
531055               91         150        2024        111           2025   
531056               91         151        2024         80           2025   
531057               91         152        2024         36           2025   

                    DATA_LIQUIDAÇÃO CÓDIGO_ÓRGÃO SIGLA_ÓRGÃO  \
0       2025-01-16 00:00:00.0000000           16         SME   
1       2025-01-16 00:00:00.0000000           16         SME   
2       2025-01-20 00:00:00.0000000           16         SME   
3       2025-02-21 00:00:00.0000000           16         SME   
4       2025-02-21 00:00:00.0000000           16         SME   
...                             ...          ...         ...   
531053  2025-02-25 00:00:00.0000000           91         FMH   
531054  2025-02-21 00:00:00.0000000           91         FMH   
531055  2025-02-25 00:00:00.0000000           91         FMH   
531056  2025-02-20 00:00:00.0000000           91         FMH   
531057  2025-02-10 00:00:00.0000000           91         FMH   

                         DESCRIÇÃO_ÓRGÃO CÓDIGO_UNIDADE  ...  \
0       Secretaria Municipal de Educação             10  ...   
1       Secretaria Municipal de Educação             10  ...   
2       Secretaria Municipal de Educação             10  ...   
3       Secretaria Municipal de Educação             10  ...   
4       Secretaria Municipal de Educação             10  ...   
...                                  ...            ...  ...   
531053      Fundo Municipal de Habitação             10  ...   
531054      Fundo Municipal de Habitação             10  ...   
531055      Fundo Municipal de Habitação             10  ...   
531056      Fundo Municipal de Habitação             10  ...   
531057      Fundo Municipal de Habitação             10  ...   

                            DESCRIÇÃO_FONTE CÓDIGO_EXERCÍCIO_FONTE  \
0       Recursos não vinculados de Impostos                      1   
1       Recursos não vinculados de Impostos                      1   
2       Recursos não vinculados de Impostos                      1   
3       Recursos não vinculados de Impostos                      1   
4       Recursos não vinculados de Impostos                      1   
...                                     ...                    ...   
531053         Fundo Municipal de Habitação                      1   
531054         Fundo Municipal de Habitação                      1   
531055         Fundo Municipal de Habitação                      1   
531056         Fundo Municipal de Habitação                      1   
531057         Fundo Municipal de Habitação                      1   

       CÓDIGO_DESTINAÇÃO_RECURSO CÓDIGO_VÍNCULO_PMSP  \
0                            500                9001   
1                            500                9001   
2                            500                9001   
3                            500                9001   
4                            500                9001   
...                          ...                 ...   
531053                       759                8011   
531054                       759                8011   
531055                       759                8011   
531056                       759                8011   
531057                       759                8011   

       CÓDIGO_TIPO_CRÉDITO_ORÇ

In [59]:
df_orcamento_r['VALOR_DETALHAMENTO_AÇÃO'] = df_orcamento_r['VALOR_DETALHAMENTO_AÇÃO'].str.replace(',', '.').astype(float)
# df_orcamento_r['DATA_EXTRAÇÃO'] = pd.to_datetime(df_orcamento_r['DATA_EXTRAÇÃO'], format='%d/%m/%Y')
df_orcamento_r

COD_EMPRESA_PMSP COD_EMPENHO ANO_EMPENHO CÓDIGO_NLP ANO_LIQUIDAÇÃO  \
0                    01           1        2024       5695           2025   
1                    01           1        2024       5878           2025   
2                    01           1        2024       7627           2025   
3                    01           1        2024      43181           2025   
4                    01           1        2024      43192           2025   
...                 ...         ...         ...        ...            ...   
531053               91         148        2024        110           2025   
531054               91         149        2024         85           2025   
531055               91         150        2024        111           2025   
531056               91         151        2024         80           2025   
531057               91         152        2024         36           2025   

                    DATA_LIQUIDAÇÃO CÓDIGO_ÓRGÃO SIGLA_ÓRGÃO  \
0       2025-01-16 00:00:00.0000000           16         SME   
1       2025-01-16 00:00:00.0000000           16         SME   
2       2025-01-20 00:00:00.0000000           16         SME   
3       2025-02-21 00:00:00.0000000           16         SME   
4       2025-02-21 00:00:00.0000000           16         SME   
...                             ...          ...         ...   
531053  2025-02-25 00:00:00.0000000           91         FMH   
531054  2025-02-21 00:00:00.0000000           91         FMH   
531055  2025-02-25 00:00:00.0000000           91         FMH   
531056  2025-02-20 00:00:00.0000000           91         FMH   
531057  2025-02-10 00:00:00.0000000           91         FMH   

                         DESCRIÇÃO_ÓRGÃO CÓDIGO_UNIDADE  ...  \
0       Secretaria Municipal de Educação             10  ...   
1       Secretaria Municipal de Educação             10  ...   
2       Secretaria Municipal de Educação             10  ...   
3       Secretaria Municipal de Educação             10  ...   
4       Secretaria Municipal de Educação             10  ...   
...                                  ...            ...  ...   
531053      Fundo Municipal de Habitação             10  ...   
531054      Fundo Municipal de Habitação             10  ...   
531055      Fundo Municipal de Habitação             10  ...   
531056      Fundo Municipal de Habitação             10  ...   
531057      Fundo Municipal de Habitação             10  ...   

                            DESCRIÇÃO_FONTE CÓDIGO_EXERCÍCIO_FONTE  \
0       Recursos não vinculados de Impostos                      1   
1       Recursos não vinculados de Impostos                      1   
2       Recursos não vinculados de Impostos                      1   
3       Recursos não vinculados de Impostos                      1   
4       Recursos não vinculados de Impostos                      1   
...                                     ...                    ...   
531053         Fundo Municipal de Habitação                      1   
531054         Fundo Municipal de Habitação                      1   
531055         Fundo Municipal de Habitação                      1   
531056         Fundo Municipal de Habitação                      1   
531057         Fundo Municipal de Habitação                      1   

       CÓDIGO_DESTINAÇÃO_RECURSO CÓDIGO_VÍNCULO_PMSP  \
0                            500                9001   
1                            500                9001   
2                            500                9001   
3                            500                9001   
4                            500                9001   
...                          ...                 ...   
531053                       759                8011   
531054                       759                8011   
531055                       759                8011   
531056                       759                8011   
531057                       759                8011   

       CÓDIGO_TIPO_CRÉDITO_ORÇ

In [60]:
df_orcamento_r = df_orcamento_r.loc[df_orcamento_r['CÓDIGO_FUNÇÃO']=='12']
df_orcamento_r = df_orcamento_r.loc[df_orcamento_r['ANO_LIQUIDAÇÃO']=='2024']
df_orcamento_r

COD_EMPRESA_PMSP COD_EMPENHO ANO_EMPENHO CÓDIGO_NLP ANO_LIQUIDAÇÃO  \
11                   01           1        2024      72189           2024   
12                   01           1        2024      72326           2024   
13                   01           1        2024      99706           2024   
14                   01           1        2024      99864           2024   
15                   01           1        2024     131213           2024   
...                 ...         ...         ...        ...            ...   
493950               16         298        2024       2175           2024   
493951               16         299        2024       2160           2024   
493952               16         299        2024       2173           2024   
493953               16         299        2024       2176           2024   
493955               16         304        2024       2290           2024   

                    DATA_LIQUIDAÇÃO CÓDIGO_ÓRGÃO SIGLA_ÓRGÃO  \
11      2024-03-18 00:00:00.0000000           16         SME   
12      2024-03-18 00:00:00.0000000           16         SME   
13      2024-04-15 00:00:00.0000000           16         SME   
14      2024-04-15 00:00:00.0000000           16         SME   
15      2024-05-17 00:00:00.0000000           16         SME   
...                             ...          ...         ...   
493950  2024-12-10 00:00:00.0000000           80       FPETC   
493951  2024-12-10 00:00:00.0000000           80       FPETC   
493952  2024-12-10 00:00:00.0000000           80       FPETC   
493953  2024-12-10 00:00:00.0000000           80       FPETC   
493955  2024-12-26 00:00:00.0000000           80       FPETC   

                                          DESCRIÇÃO_ÓRGÃO CÓDIGO_UNIDADE  ...  \
11                       Secretaria Municipal de Educação             10  ...   
12                       Secretaria Municipal de Educação             10  ...   
13                       Secretaria Municipal de Educação             10  ...   
14                       Secretaria Municipal de Educação             10  ...   
15                       Secretaria Municipal de Educação             10  ...   
...                                                   ...            ...  ...   
493950  Fundação Paulistana de Educação Tecnologia e C...             10  ...   
493951  Fundação Paulistana de Educação Tecnologia e C...             10  ...   
493952  Fundação Paulistana de Educação Tecnologia e C...             10  ...   
493953  Fundação Paulistana de Educação Tecnologia e C...             10  ...   
493955  Fundação Paulistana de Educação Tecnologia e C...             10  ...   

                            DESCRIÇÃO_FONTE CÓDIGO_EXERCÍCIO_FONTE  \
11      Recursos não vinculados de Impostos                      1   
12      Recursos não vinculados de Impostos                      1   
13      Recursos não vinculados de Impostos                      1   
14      Recursos não vinculados de Impostos                      1   
15      Recursos não vinculados de Impostos                      1   
...                                     ...                    ...   
493950  Recursos não vinculados de Impostos                      1   
493951  Recursos não vinculados de Impostos                      1   
493952  Recursos não vinculados de Impostos                      1   
493953  Recursos não vinculados de Impostos                      1   
493955  Recursos não vinculados de Impostos                      1   

       CÓDIGO_DESTINAÇÃO_RECURSO CÓDIGO_VÍNCULO_PMSP  \
11                           500                9001   
12                           500                9001   
13                           500                9001   
14                           500                9001   
15                           500                9001   
...                          ...                 ...   
493950                       500                9001   
493951                       500                900

Vamos conferir qual o percentual do orçamento está presente na tabela de detalhamento e regionalizado a nível de subprefeitura.

In [61]:
df_orcamento_r['VALOR_DETALHAMENTO_AÇÃO'].sum()/df_orcamento['Vl_Liquidado'].sum()

np.float64(0.5387537644095716)

53,9% de detalhamento não é um percentual tão bom, mas vamos checar a regionalização.

In [62]:
(
    df_orcamento_r
    .assign(regionalizado=df_orcamento_r['SUBPREFEITURA'].str.contains('Supra')==False)
    .groupby('regionalizado')
    ['VALOR_DETALHAMENTO_AÇÃO'].sum()/df_orcamento['Vl_Liquidado'].sum()
)

regionalizado
False    0.263278
True     0.275476
Name: VALOR_DETALHAMENTO_AÇÃO, dtype: float64

O percentual de regionalização é de 27,5%, o que é bem baixo. Apesar de não parecer tão satisfatório, não perdemos nada ao mantê-los, então vamos manter as informações de regionalização também.

## IDEB do município

Durante a evolução do projeto, também foi sugerida a inclusão do IDEB do município como indicador educacional ao dashboard de visão geral. Os dados são divulgados de maneira agregada para o município separados por anos iniciais, anos finais e ensino médio. Vamos obtê-los diretamente do site do INEP.

In [63]:
def get_ideb(ciclo: str) -> pd.DataFrame:
    """
    Baixa e processa dados do IDEB para o município de São Paulo.
    
    Parâmetros:
    -----------
    ciclo : str
        O ciclo educacional desejado. Deve ser um dos valores:
        - 'anos_iniciais': Anos iniciais do ensino fundamental
        - 'anos_finais': Anos finais do ensino fundamental  
        - 'ensino_medio': Ensino médio
    
    Retorna:
    --------
    pd.DataFrame
        DataFrame com os dados do IDEB filtrados para o município de São Paulo
        (código 3550308).
    
    Levanta:
    --------
    ValueError
        Se o parâmetro 'ciclo' não for um dos valores válidos.
    
    Exemplo:
    --------
    >>> df_ideb = get_ideb('anos_iniciais')
    >>> print(df_ideb.head())
    """
    if ciclo not in ['anos_iniciais', 'anos_finais', 'ensino_medio']:
        raise ValueError("Ciclo deve ser 'anos_iniciais', 'anos_finais' ou 'ensino_medio'")
    
    url = f'https://download.inep.gov.br/ideb/resultados/divulgacao_{ciclo}_municipios_2023.zip'
    r = requests.get(url)
    z = zipfile.ZipFile(BytesIO(r.content))
    file_path = f'divulgacao_{ciclo}_municipios_2023/divulgacao_{ciclo}_municipios_2023.xlsx'
    df = pd.read_excel(z.open(file_path), skiprows=9)

    df = df[df['CO_MUNICIPIO'] == 3550308]
    return df

In [65]:
df_ideb_iniciais = get_ideb('anos_iniciais')
df_ideb_iniciais

SG_UF  CO_MUNICIPIO NO_MUNICIPIO       REDE VL_APROVACAO_2005_SI_4  \
9940    SP     3550308.0    São Paulo    Federal                      -   
9941    SP     3550308.0    São Paulo   Estadual                   95.1   
9942    SP     3550308.0    São Paulo  Municipal                   94.7   
9943    SP     3550308.0    São Paulo    Pública                   94.9   

     VL_APROVACAO_2005_SI VL_APROVACAO_2005_1 VL_APROVACAO_2005_2  \
9940                    -                   -                   -   
9941                    -                95.2                97.1   
9942                    -                96.5                98.1   
9943                    -                95.8                97.5   

     VL_APROVACAO_2005_3 VL_APROVACAO_2005_4  ... VL_OBSERVADO_2021  \
9940                   -                   -  ...                 -   
9941                97.2                  91  ...                 6   
9942                98.3                87.6  ...               5.7   
9943                97.7                89.3  ...               5.9   

     VL_OBSERVADO_2023 VL_PROJECAO_2007 VL_PROJECAO_2009 VL_PROJECAO_2011  \
9940               6.5                -                -              5.7   
9941               6.1              4.7                5              5.4   
9942               5.6              4.1              4.5              4.9   
9943               5.9              4.4              4.7              5.1   

     VL_PROJECAO_2013 VL_PROJECAO_2015 VL_PROJECAO_2017 VL_PROJECAO_2019  \
9940                6              6.2              6.5              6.7   
9941              5.7              5.9              6.2              6.4   
9942              5.2              5.4              5.7                6   
9943              5.4              5.7              5.9              6.2   

     VL_PROJECAO_2021  
9940              6.9  
9941              6.6  
9942              6.2  
9943              6.4  

[4 rows x 122 columns]

In [66]:
df_ideb_finais = get_ideb('anos_finais')
df_ideb_finais

SG_UF  CO_MUNICIPIO NO_MUNICIPIO       REDE VL_APROVACAO_2005_SI_4  \
10053    SP     3550308.0    São Paulo   Estadual                   85.5   
10054    SP     3550308.0    São Paulo  Municipal                   93.6   
10055    SP     3550308.0    São Paulo    Pública                   88.8   

      VL_APROVACAO_2005_1 VL_APROVACAO_2005_2 VL_APROVACAO_2005_3  \
10053                88.9                88.6                87.4   
10054                96.5                95.7                  95   
10055                92.2                91.6                90.5   

      VL_APROVACAO_2005_4 VL_INDICADOR_REND_2005  ... VL_OBSERVADO_2021  \
10053                76.9               0.851411  ...               5.1   
10054                  86               0.930964  ...               5.1   
10055                80.3               0.883665  ...               5.1   

      VL_OBSERVADO_2023 VL_PROJECAO_2007 VL_PROJECAO_2009 VL_PROJECAO_2011  \
10053               4.9              3.8                4              4.3   
10054               4.8              4.1              4.3              4.6   
10055               4.8                4              4.1              4.4   

      VL_PROJECAO_2013 VL_PROJECAO_2015 VL_PROJECAO_2017 VL_PROJECAO_2019  \
10053              4.7                5              5.3              5.5   
10054                5              5.3              5.6              5.8   
10055              4.8              5.2              5.4              5.6   

      VL_PROJECAO_2021  
10053              5.8  
10054                6  
10055              5.9  

[3 rows x 112 columns]

In [67]:
df_ideb_medio = get_ideb('ensino_medio')
df_ideb_medio

SG_UF  CO_MUNICIPIO NO_MUNICIPIO       REDE VL_APROVACAO_2017_SI_4  \
8058    SP     3550308.0    São Paulo   Estadual                   81.6   
8059    SP     3550308.0    São Paulo    Federal                   88.4   
8060    SP     3550308.0    São Paulo  Municipal                   85.3   
8061    SP     3550308.0    São Paulo    Pública                   81.7   

     VL_APROVACAO_2017_1 VL_APROVACAO_2017_2 VL_APROVACAO_2017_3  \
8058                74.2                82.2                90.5   
8059                85.2                86.8                96.8   
8060                79.3                84.8                92.1   
8061                74.3                82.3                90.5   

     VL_APROVACAO_2017_4 VL_INDICADOR_REND_2017  ... VL_NOTA_MEDIA_2021  \
8058                   -               0.817611  ...           4.713662   
8059                   -               0.893165  ...           6.597057   
8060                93.3               0.869969  ...           4.711535   
8061                93.3               0.844283  ...           4.727806   

     VL_NOTA_MATEMATICA_2023 VL_NOTA_PORTUGUES_2023 VL_NOTA_MEDIA_2023  \
8058                  265.35                 277.16           4.565442   
8059                  327.41                 330.84           6.240664   
8060                  266.21                  273.1           4.516742   
8061                  265.86                 277.57           4.578743   

     VL_OBSERVADO_2017 VL_OBSERVADO_2019 VL_OBSERVADO_2021 VL_OBSERVADO_2023  \
8058               3.5               3.9               4.3               4.1   
8059               6.3               6.7                 6                 6   
8060               3.5               3.7               4.5               4.3   
8061               3.6               4.1               4.4               4.2   

     VL_PROJECAO_2019 VL_PROJECAO_2021  
8058              3.7              3.9  
8059              6.5              6.7  
8060              3.7                4  
8061              3.8                4  

[4 rows x 46 columns]

# Transformação e mesclagem de dados

Para facilitar o trabalho dos dados no Qlik Sense, vamos avaliar como é a melhor forma de retrabalhar os dados de acordo com o paradigma fato-dimensão.

## Nível Escolar

A primeira dimensão que parece fazer sentido é o Nível escolar. Vamos avaliar como aparece em cada tabela.

In [68]:
mat_24['Nível Educacional'].value_counts()

Nível Educacional
Creche          96
Pré Escola      96
Ens. Fund.I     96
Ens. Fund.II    96
EJA I           96
EJA II          96
Ens. Médio      96
Ed. Prof.       96
Name: count, dtype: int64

In [69]:
perf_24[['CD_AREA_ATUACAO_BASE', 'DC_AREA_ATUACAO_BASE']].value_counts()

CD_AREA_ATUACAO_BASE  DC_AREA_ATUACAO_BASE           
301521917             ENSINO FUNDAMENTAL I E INFANTIL    33516
93911221827           ENSINO FUNDAMENTAL II              23228
1311820840            EDUCACAO INFANTIL                  15512
83811221917           ENSINO MEDIO                          76
73711221947           EDUCACAO ESPECIAL                     11
Name: count, dtype: int64

In [70]:
alunos_24['MODAL'].value_counts()

MODAL
CRECHE    102313
FUND      101168
PRE        36396
EJA        15042
MOVA        8215
CONVEE      1141
EDPROF       884
MEDIO        667
ESPEC        521
Name: count, dtype: int64

In [71]:
alunos_est_2024['ETAPA'].value_counts()

ETAPA
FUND      1736
CRECHE    1184
PRE        616
EJA        259
MOVA        32
MEDIO       19
EDPROF       6
ESPEC        6
CONVEE       1
Name: count, dtype: int64

In [72]:
alunos_bf_2024['NIVEL'].value_counts()

NIVEL
CRECHE                   3763
PRE ESCOLA               3763
ENSINO FUNDAMENTAL       3763
EDUCAÇÃO PROFISSIONAL    3763
ENSINO MEDIO             3763
EDUCAÇÃO ESPECIAL        3763
Name: count, dtype: int64

Existe uma tabela de correspondência relacionada a essas categorias fornecida no último relatório de Gestão da Função Educação. A tabela é a seguinte:

| Nível Educacional | Tipo de escola |
| --- | --- |
| Educação Infantil | Creches |
| Educação Infantil | Pré-escola |
| Ensino Fundamental | EMEF |
| Ensino Médio | EMEFM |
| Educação de Jovens e Adultos | EJA/CIEJA |
| Educação de Jovens e Adultos | MOVA (Parceria) |
| Educação de Jovens e Adultos | Educação Profissional |
| Educação Especial | EMEBS |
| Educação Especial | Educação Especial (Parceira) |


Essa tabela permite a padronização de quase todas as tabelas, exceto a de perfil dos professores. Para as outras, vamos utilizar a tabela como base para a criação de um dicionário que será utilizado como *mapper* em cada uma das tabelas.

In [73]:
mat_23_nivel = {
    'Creche': 'Educação Infantil',
    'Pré Escola': 'Educação Infantil',
    'Ens. Fund.I': 'Ensino Fundamental',
    'Ens. Fund.II': 'Ensino Fundamental',
    'EJA I': 'Educação de Jovens e Adultos',
    'EJA II': 'Educação de Jovens e Adultos',
    'Ens. Médio': 'Ensino Médio',
    'Ed. Prof.': 'Educação de Jovens e Adultos'
}

mat_24['Nível padronizado'] = mat_24['Nível Educacional'].map(mat_23_nivel)
mat_24['Nível padronizado'].value_counts()

Nível padronizado
Educação de Jovens e Adultos    288
Educação Infantil               192
Ensino Fundamental              192
Ensino Médio                     96
Name: count, dtype: int64

In [74]:
alunos_23_nivel = {
    'CRECHE': 'Educação Infantil',
    'PRE': 'Educação Infantil',
    'FUND': 'Ensino Fundamental',
    'EJA': 'Educação de Jovens e Adultos',
    'MOVA': 'Educação de Jovens e Adultos',
    'MEDIO': 'Ensino Médio',
    'EDPROF': 'Educação de Jovens e Adultos',
    'ESPEC': 'Educação Especial',
    'CONVEE': 'Educação Especial',
    'ATCOMP': '?',
    'REC': '?',
    'SAAI': '?'
}

alunos_24['Nível padronizado'] = alunos_24['MODAL'].map(alunos_23_nivel)
alunos_24['Nível padronizado'].value_counts()

/tmp/ipykernel_2586/4086248992.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  alunos_24['Nível padronizado'] = alunos_24['MODAL'].map(alunos_23_nivel)


Nível padronizado
Educação Infantil               138709
Ensino Fundamental              101168
Educação de Jovens e Adultos     24141
Educação Especial                 1662
Ensino Médio                       667
Name: count, dtype: int64

In [75]:
alunos_est_2024_nivel = {
    'CRECHE': 'Educação Infantil',
    'PRE': 'Educação Infantil',
    'FUND': 'Ensino Fundamental',
    'EJA': 'Educação de Jovens e Adultos',
    'MOVA': 'Educação de Jovens e Adultos',
    'MEDIO': 'Ensino Médio',
    'EDPROF': 'Educação de Jovens e Adultos',
    'ESPEC': 'Educação Especial',
    'CONVEE': 'Educação Especial'
}

alunos_est_2024['Nível padronizado'] = alunos_est_2024['ETAPA'].map(alunos_est_2024_nivel)
alunos_est_2024['Nível padronizado'].value_counts()

/tmp/ipykernel_2586/2594895673.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  alunos_est_2024['Nível padronizado'] = alunos_est_2024['ETAPA'].map(alunos_est_2024_nivel)


Nível padronizado
Educação Infantil               1800
Ensino Fundamental              1736
Educação de Jovens e Adultos     297
Ensino Médio                      19
Educação Especial                  7
Name: count, dtype: int64

In [76]:
alunos_bf_2024_nivel = {
    'CRECHE': 'Educação Infantil',
    'PRE ESCOLA': 'Educação Infantil',
    'ENSINO FUNDAMENTAL': 'Ensino Fundamental',
    'ENSINO MEDIO': 'Ensino Médio',
    'EDUCAÇÃO PROFISSIONAL': 'Educação de Jovens e Adultos',
    'EDUCAÇÃO ESPECIAL': 'Educação Especial'
}

alunos_bf_2024['Nível padronizado'] = alunos_bf_2024['NIVEL'].map(alunos_bf_2024_nivel)
alunos_bf_2024['Nível padronizado'].value_counts()

Nível padronizado
Educação Infantil               7526
Ensino Fundamental              3763
Educação de Jovens e Adultos    3763
Ensino Médio                    3763
Educação Especial               3763
Name: count, dtype: int64

## Padronização dos nomes de Distritos

Os dados de matrículas, escolas, educandos, educandos estrangeiros e educandos beneficiários do Bolsa Família possuem uma coluna chamada "Distrito" que contém o nome do distrito onde a escola está localizada.

Já os dados de servidores não possuem dados de distrito, mas possuem o nome da escola, que pode ser utilizada para buscar o distrito correspondente. Antes de unir as tabelas para fazer isso, vamos padronizar os nomes dos distritos de acordo com os dados do geosampa.

### Número de Unidades Escolares

In [77]:
(
    escolas_24
    .loc[~escolas_24['DISTRITO'].isin(df_dist['nm_distrito_municipal'])]
    ['DISTRITO']
    .unique().tolist()
)

[]

### Perfil dos alunos

In [78]:
(
    alunos_24
    .loc[~alunos_24['DISTRITO'].isin(df_dist['nm_distrito_municipal'])]
    ['DISTRITO']
    .unique().tolist()
)

[]

### Número de alunos estrangeiros

In [79]:
(
    alunos_est_2024
    .loc[~alunos_est_2024['DISTRITO'].isin(df_dist['nm_distrito_municipal'])]
    ['DISTRITO']
    .unique().tolist()
)

[]

### Número de alunos beneficiários do Bolsa Família

In [80]:
(
    alunos_bf_2024
    .loc[~alunos_bf_2024['DISTRITO'].isin(df_dist['nm_distrito_municipal'])]
    ['DISTRITO']
    .unique().tolist()
)

[]

Nenhum dos conjuntos de dados possui distritos que não estejam na lista do GeoSampa.

Agora, vamos unir os dados de servidores com os dados de escolas para adicionar a coluna de distrito aos dados de servidores.

### Número de professores da Rede Municipal de Ensino

Primeiro, vamos criar uma coluna com o tipo de escola e o nome da escola nos dois dataframes, para que possamos unir os dados de servidores com os dados de escolas.

In [81]:
escolas_24['NOMES_COMPLETO'] = (
    escolas_24['TIPOESC'].str.strip().str.upper()
    + ' ' + escolas_24['NOMES'].str.strip().str.upper()
)
escolas_24['NOMES_COMPLETO']

/tmp/ipykernel_2586/3063976760.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  escolas_24['NOMES_COMPLETO'] = (


0                         EMEI PAULO CAMILHIER FLORENCANO
1                             EMEI VICENTE PAULO DA SILVA
2                       EMEF JOSE ERMIRIO DE MORAES, SEN.
3                          EMEF ALIPIO CORREA NETO, PROF.
4              EMEBS VERA LUCIA APARECIDA RIBEIRO, PROFA.
                              ...                        
4962    ESP CONV ASSOCIACAO CASA DOS DEFICIENTES DE ER...
4963    ESP CONV AACD - ASS DE ASS A CRIANCA DEFICIENT...
4964             ESP CONV APAE - NUCLEO CAPELA DO SOCORRO
4965                   ESP CONV APAE - NUCLEO CAMPO LIMPO
4966                      ESP CONV APAE - NUCLEO PIRITUBA
Name: NOMES_COMPLETO, Length: 4173, dtype: object

In [82]:
perf_24['DC_UNIDADE_ATUAL_COMPLETA'] = (
    perf_24['TP_UNIDADE_ATUAL'].str.strip().str.upper()
    + ' ' + perf_24['DC_UNIDADE_ATUAL'].str.strip().str.upper()
)
perf_24['DC_UNIDADE_ATUAL_COMPLETA']

/tmp/ipykernel_2586/3256895158.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  perf_24['DC_UNIDADE_ATUAL_COMPLETA'] = (


0             EMEI THEREZINHA BATISTA PETTAN, PROFA.
2                           CEI DIRET JARDIM MONJOLO
3          FORA DE SME CAMARA MUNICIPAL DE SAO PAULO
4                                  CEU EMEF JAMBEIRO
5           EMEF MARTIN FRANCISCO RIBEIRO DE ANDRADA
                            ...                     
90908                       CEU CEMEI FREGUESIA DO O
90909                           EMEF FAZENDA DA JUTA
90910                           CEU EMEF ALTO ALEGRE
90911                     CEI DIRET GENOVEVA DASCOLI
90912    CEU CEI ANA LUCIA DE HOLANDA GAMBOA, PROFA.
Name: DC_UNIDADE_ATUAL_COMPLETA, Length: 72343, dtype: object

In [83]:
perf_24 = (
    perf_24
    .merge(escolas_24[['NOMES_COMPLETO', 'DISTRITO']],
           left_on=['DC_UNIDADE_ATUAL_COMPLETA'],
           right_on=['NOMES_COMPLETO'],
           how='left')
)

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
1       9.274100e+13                 PROF.DE ED.INFANTIL   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA   
...              ...                                 ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
72341   9.274100e+13                 PROF.DE ED.INFANTIL   
72342   9.274100e+13                 PROF.DE ED.INFANTIL   

       DT_INICIO_CARGO_BASE  CD_CARGO_ATUAL  \
0                     41660    9.234430e+12   
1                     39588    9.274100e+13   
2                     34243    9.264550e+12   
3                     33605    9.244720e+12   
4                     39589    9.214970e+12   
...                     ...             ...   
72338                 41716    9.274100e+13   
72339                 40725    9.234430e+12   
72340                 40728    9.274940e+12   
72341                 43382    9.274100e+13   
72342                 39625    9.274100e+13   

                           DC_CARGO_ATUAL  CD_AREA_ATUACAO_BASE  \
0                PROF.ED.INF.E ENS.FUND.I             301521917   
1                     PROF.DE ED.INFANTIL            1311820840   
2           PROF.ENS.FUND.II E MED.-ARTES           93911221827   
3       PROF.ENS.FUND.II E MED.-PORTUGUES           93911221827   
4      PROF.ENS.FUND.II E MED.-MATEMATICA           93911221827   
...                                   ...                   ...   
72338                 PROF.DE ED.INFANTIL            1311820840   
72339            PROF.ED.INF.E ENS.FUND.I             301521917   
72340     ASSISTENTE DE DIRETOR DE ESCOLA             301521917   
72341                 PROF.DE ED.INFANTIL            1311820840   
72342                 PROF.DE ED.INFANTIL            1311820840   

                  DC_AREA_ATUACAO_BASE  CD_UNIDADE_ATUAL TP_UNIDADE_ATUAL  \
0      ENSINO FUNDAMENTAL I E INFANTIL      3.385170e+14             EMEI   
1                    EDUCACAO INFANTIL      8.271610e+15        CEI DIRET   
2                ENSINO FUNDAMENTAL II      1.236240e+14      FORA DE SME   
3                ENSINO FUNDAMENTAL II      1.375830e+13         CEU EMEF   
4                ENSINO FUNDAMENTAL II      3.335110e+14             EMEF   
...                                ...               ...              ...   
72338                EDUCACAO INFANTIL      1.315840e+13        CEU CEMEI   
72339  ENSINO FUNDAMENTAL I E INFANTIL      1.305490e+13             EMEF   
72340  ENSINO FUNDAMENTAL I E INFANTIL      1.315840e+13         CEU EMEF   
72341                EDUCACAO INFANTIL      8.271610e+15        CEI DIRET   
72342                EDUCACAO INFANTIL      8.246790e+14          CEU CEI   

                          DC_UNIDADE_ATUAL  \
0        THEREZINHA BATISTA PETTAN, PROFA.   
1                           JARDIM MONJOLO   
2          

Vamos avaliar se todas as unidades escolares foram encontradas no dataframe de unidades.

In [84]:
(
    perf_24
    .query('DISTRITO.isnull()')
)

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
2           F   1311820840         BRANCA  12727970840     EFETIVO   
9           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
11          M   6361921931  NAO INFORMADA  12727970840     EFETIVO   
36          M   6361921931  NAO INFORMADA  12727970840     EFETIVO   
41          F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72213       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72214       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72281       F  83811221917        AMARELA  12727970840     EFETIVO   
72316       M  93911221827          PARDA  12727970840     EFETIVO   
72325       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                      DC_CARGO_BASE  DT_INICIO_CARGO_BASE  \
2       9.264550e+12      PROF.ENS.FUND.II E MED.-ARTES                 34243   
9       9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES                 34589   
11      9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES                 39106   
36      9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 31450   
41      9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 26764   
...              ...                                ...                   ...   
72213   9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 40710   
72214   9.274100e+13                PROF.DE ED.INFANTIL                 41180   
72281   9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 40722   
72316   9.274960e+12   PROF.ENS.FUND.II E MED.-CIENCIAS                 43270   
72325   9.234430e+12           PROF.ED.INF.E ENS.FUND.I                 40725   

       CD_CARGO_ATUAL                     DC_CARGO_ATUAL  \
2        9.264550e+12      PROF.ENS.FUND.II E MED.-ARTES   
9        9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES   
11       9.244720e+12  PROF.ENS.FUND.II E MED.-PORTUGUES   
36       2.245870e+11   ASSISTENTE TECNICO DE EDUCACAO I   
41       2.245870e+11   ASSISTENTE TECNICO DE EDUCACAO I   
...               ...                                ...   
72213    9.234430e+12           PROF.ED.INF.E ENS.FUND.I   
72214    9.274100e+13                PROF.DE ED.INFANTIL   
72281    9.234430e+12           PROF.ED.INF.E ENS.FUND.I   
72316    9.274960e+12   PROF.ENS.FUND.II E MED.-CIENCIAS   
72325    9.234430e+12           PROF.ED.INF.E ENS.FUND.I   

       CD_AREA_ATUACAO_BASE             DC_AREA_ATUACAO_BASE  \
2               93911221827            ENSINO FUNDAMENTAL II   
9               93911221827            ENSINO FUNDAMENTAL II   
11              93911221827            ENSINO FUNDAMENTAL II   
36                301521917  ENSINO FUNDAMENTAL I E INFANTIL   
41                301521917  ENSINO FUNDAMENTAL I E INFANTIL   
...                     ...                              ...   
72213             301521917  ENSINO FUNDAMENTAL I E INFANTIL   
72214            1311820840                EDUCACAO INFANTIL   
72281             301521917  ENSINO FUNDAMENTAL I E INFANTIL   
72316           93911221827            ENSINO FUNDAMENTAL II   
72325             301521917  ENSINO FUNDAMENTAL I E INFANTIL   

       CD_UNIDADE_ATUAL TP_UNIDADE_ATUAL  \
2          1.236240e+14      FORA DE SME   
9          1.226430e+14         DIR EDUC   
11         1.246530e+14      FORA DE SME   
36         1.226430e+14         DIR EDUC   
41         1.226430e+14         DIR EDUC   
...                 ...              ...   
72213      1.226430e+14         DIR EDUC   
72214      1.226430e+14         DIR EDUC   
72281      1.256340e+14         DIR EDUC   
72316      1.226440e+14            COORD   
72325      1.266330e+14         DIR EDUC   

                                        DC_UNIDADE_ATUAL  \
2                          CAMARA MUNICIPAL DE SAO PAULO   
9                DIRETORIA REGIONAL DE EDUCACAO IPIRA

In [85]:
(
    perf_24
    .query('DISTRITO.isna()')
    .shape[0]
    /perf_24.shape[0]
)

0.03533168378419474

Cerca de 3,6% dos professores não tiveram as unidades escolares encontradas. Vamos avaliar quais são essas unidades.

In [86]:
(
    perf_24
    .query('DISTRITO.isna()')
    [['TP_UNIDADE_ATUAL', 'DC_UNIDADE_ATUAL']]
    .sort_values(['TP_UNIDADE_ATUAL', 'DC_UNIDADE_ATUAL'])
    .drop_duplicates()
)

TP_UNIDADE_ATUAL                               DC_UNIDADE_ATUAL
39089     CEU AT COMPL     AGUA AZUL - PAULO RENATO COSTA SOUZA, PROF
63221     CEU AT COMPL       ALTO ALEGRE - PAULO SUYOSH MINAMI, PROF.
32216     CEU AT COMPL                                      ALVARENGA
20118     CEU AT COMPL     ARICANDUVA - IRENE GALVAO DE SOUZA, PROFA.
59749     CEU AT COMPL                             AZUL DA COR DO MAR
...                ...                                            ...
854           OUT-PMSP             ASSESSORIA PARLAMENTAR - SME-ASPAR
13844         OUT-PMSP  COMISSAO DE AVAL. DE ACUMULO DE CARGOS - CAAC
2149          OUT-PMSP                 NUCLEO ADMINISTRATIVO - SME-NA
27506         OUT-PMSP   NUCLEO DE PLANEJAMENTO CENTRAL - SME-ATP-NPC
1664               SME                 GABINETE DO SECRETARIO - SME G

[190 rows x 2 columns]

Por ora, vamos manter dessa forma e, caso seja necessário, podemos avaliar como tratar esses casos numa atualização futura.

## Adicionando as Subprefeituras

Agora, vamos adicionar a coluna de subprefeitura a todos os dataframes.

### Associando distritos e subprefeituras

In [87]:
df_dist.sort_values('cd_identificador_subprefeitura').head(2)

id  cd_identificador_distrito  \
10  distrito_municipal.8583404                    8583404   
49  distrito_municipal.8583443                    8583443   

    cd_identificador_subprefeitura cd_distrito_municipal  \
10                               1                    61   
49                               1                     3   

   nm_distrito_municipal sg_distrito_municipal tx_escala sg_fonte_original  \
10                 PERUS                   PRS    1:5000            GEOGSG   
49            ANHANGUERA                   ANH    1:5000            GEOGSG   

   dt_criacao                   dt_atualizacao cd_usuario_atualizacao  \
10 2004-01-01 2025-07-05 03:54:17.019000+00:00                   None   
49 2004-01-01 2025-07-05 03:54:17.103000+00:00                   None   

    cd_tipo_discrepancia  qt_area_quilometro  qt_area_metro  \
10             199299399              23.644    23644355.41   
49             199299399              33.245    33244961.18   

                                             geometry  
10  POLYGON ((325464.931 7409329.344, 325464.512 7...  
49  POLYGON ((317503.566 7410509.962, 317523.506 7...

In [88]:
df_subs.sort_values('cd_identificador_subprefeitura').head(2)

id  cd_identificador_subprefeitura cd_subprefeitura  \
0  subprefeitura.1                               1               02   
1  subprefeitura.2                               2               03   

        nm_subprefeitura tx_escala sg_fonte_original dt_criacao  \
0       PIRITUBA-JARAGUA    1:5000            GEOGSG 2023-11-30   
1  FREGUESIA-BRASILANDIA    1:5000            GEOGSG 2023-11-30   

   cd_tipo_discrepancia                   dt_atualizacao  \
0             100200300 2025-07-05 04:29:42.042000+00:00   
1             100200300 2025-07-05 04:29:42.050000+00:00   

  cd_usuario_atualizacao sg_subprefeitura  qt_area_quilometro  qt_area_metro  \
0                                      PJ                  55    55021021.42   
1                                      FO                  32    31980202.74   

                                            geometry  
0  POLYGON ((318663.925 7404127.712, 318663.251 7...  
1  POLYGON ((327340.628 7399133.313, 327331.514 7...

In [89]:
df_subs.sort_values('cd_subprefeitura').head(2)

id  cd_identificador_subprefeitura cd_subprefeitura  \
30  subprefeitura.31                              31               01   
0    subprefeitura.1                               1               02   

    nm_subprefeitura tx_escala sg_fonte_original dt_criacao  \
30             PERUS    1:5000            GEOGSG 2023-11-30   
0   PIRITUBA-JARAGUA    1:5000            GEOGSG 2023-11-30   

    cd_tipo_discrepancia                   dt_atualizacao  \
30             100200300 2025-07-05 04:29:41.999000+00:00   
0              100200300 2025-07-05 04:29:42.042000+00:00   

   cd_usuario_atualizacao sg_subprefeitura  qt_area_quilometro  qt_area_metro  \
30                                      PR                  57    56889310.75   
0                                       PJ                  55    55021021.42   

                                             geometry  
30  POLYGON ((325464.932 7409329.344, 325464.513 7...  
0   POLYGON ((318663.925 7404127.712, 318663.251 7...

Os dados de distritos e subprefeituras não estão completamente compatíveis, então precisamos de um tratamento adicional.

O dataframe de distritos possui uma coluna chamada `cd_identificador_subprefeitura`, mas não corresponde exatamente à coluna `cd_identificador_subprefeitura` do dataframe de subprefeituras. Ele corresponde parcialmente à coluna `cd_subprefeitura` do dataframe de subprefeituras, mas não é exatamente a mesma, porque esta última possui um zero à esquerda que não está presente no dataframe de distritos. Portanto, vamos criar uma coluna com o código de subprefeitura no dataframe de distritos, que será o código de subprefeitura com o zero à esquerda.

In [90]:
df_dist['cd_subprefeitura'] = (
    df_dist['cd_identificador_subprefeitura'].astype(str)
    .str.zfill(2)
)

df_dist.sort_values('cd_subprefeitura').head(2)

id  cd_identificador_distrito  \
49  distrito_municipal.8583443                    8583443   
10  distrito_municipal.8583404                    8583404   

    cd_identificador_subprefeitura cd_distrito_municipal  \
49                               1                     3   
10                               1                    61   

   nm_distrito_municipal sg_distrito_municipal tx_escala sg_fonte_original  \
49            ANHANGUERA                   ANH    1:5000            GEOGSG   
10                 PERUS                   PRS    1:5000            GEOGSG   

   dt_criacao                   dt_atualizacao cd_usuario_atualizacao  \
49 2004-01-01 2025-07-05 03:54:17.103000+00:00                   None   
10 2004-01-01 2025-07-05 03:54:17.019000+00:00                   None   

    cd_tipo_discrepancia  qt_area_quilometro  qt_area_metro  \
49             199299399              33.245    33244961.18   
10             199299399              23.644    23644355.41   

                                             geometry cd_subprefeitura  
49  POLYGON ((317503.566 7410509.962, 317523.506 7...               01  
10  POLYGON ((325464.931 7409329.344, 325464.512 7...               01

Agora, vamos associar os distritos e subprefeituras.

In [91]:
df_dist_sub = df_dist.merge(
    df_subs[['cd_subprefeitura', 'nm_subprefeitura']],
    on='cd_subprefeitura',
    how='left'
)
df_dist_sub.sort_values('cd_subprefeitura')

id  cd_identificador_distrito  \
49  distrito_municipal.8583443                    8583443   
10  distrito_municipal.8583404                    8583404   
87  distrito_municipal.8583481                    8583481   
21  distrito_municipal.8583415                    8583415   
12  distrito_municipal.8583406                    8583406   
..                         ...                        ...   
78  distrito_municipal.8583472                    8583472   
25  distrito_municipal.8583419                    8583419   
23  distrito_municipal.8583417                    8583417   
71  distrito_municipal.8583465                    8583465   
26  distrito_municipal.8583420                    8583420   

    cd_identificador_subprefeitura cd_distrito_municipal  \
49                               1                     3   
10                               1                    61   
87                               2                    42   
21                               2                    95   
12                               2                    63   
..                             ...                   ...   
78                              30                    33   
25                              30                    75   
23                              30                    73   
71                              31                    25   
26                              32                    76   

   nm_distrito_municipal sg_distrito_municipal tx_escala sg_fonte_original  \
49            ANHANGUERA                   ANH    1:5000            GEOGSG   
10                 PERUS                   PRS    1:5000            GEOGSG   
87               JARAGUA                   JAR    1:5000            GEOGSG   
21          SAO DOMINGOS                   SDO    1:5000            GEOGSG   
12              PIRITUBA                   PIR    1:5000            GEOGSG   
..                   ...                   ...       ...               ...   
78              IGUATEMI                   IGU    1:5000            GEOGSG   
25            SAO RAFAEL                   SRA    1:5000            GEOGSG   
23            SAO MATEUS                   SMT    1:5000            GEOGSG   
71     CIDADE TIRADENTES                   CTI    1:5000            GEOGSG   
26             SAPOPEMBA                   SAP    1:5000            GEOGSG   

   dt_criacao                   dt_atualizacao cd_usuario_atualizacao  \
49 2004-01-01 2025-07-05 03:54:17.103000+00:00                   None   
10 2004-01-01 2025-07-05 03:54:17.019000+00:00                   None   
87 2004-01-01 2025-07-05 03:54:16.797000+00:00                   None   
21 2004-01-01 2025-07-05 03:54:17.137000+00:00                   None   
12 2004-01-01 2025-07-05 03:54:16.886000+00:00                   None   
..        ...                              ...                    ...   
78 2004-01-01 2025-07-05 03:54:16.895000+00:00                   None   
25 2004-01-01 2025-07-05 03:54:16.912000+00:00                   None   
23 2004-01-01 2025-07-05 03:54:17.117000+00:00                   None   
71 2004-01-01 2025-07-05 03:54:16.745000+00:00                   None   
26 2004-01-01 2025-07-05 03:54:17.107000+00:00                   None   

    cd_tipo_discrepancia  qt_area_quilometro  qt_area_metro  \
49             199299399              33.245    33244961.18   
10             199299399              23.644    23644355.41   
87             199299399              28.111    28111480.23   
21             199299399               9.693     9693355.95   
12             199299399              17.216    17216180.68   
..                   ...                 ...            ...   
78             199299399              19.435    19434636.54   
25             199299399              13.076    13076288.46   
23             199299399              12.800    12800219.28   
71             199299399              14.939    14939046.96   
26             199299399              13.633    13632901.77   

   

Aparentemente, os dados de distritos e subprefeituras estão compatíveis, então vamos adicionar a coluna de subprefeitura aos outros dataframes.

### Número de Unidades Escolares

In [92]:
escolas_24 = escolas_24.merge(
    df_dist_sub[['nm_distrito_municipal', 'cd_subprefeitura', 'nm_subprefeitura']],
    left_on='DISTRITO',
    right_on='nm_distrito_municipal',
    how='left'
)

escolas_24

CODESC   TIPOESC                                              NOMES  \
0         86      EMEI                         PAULO CAMILHIER FLORENCANO   
1         94      EMEI                             VICENTE PAULO DA SILVA   
2        108      EMEF                       JOSE ERMIRIO DE MORAES, SEN.   
3        191      EMEF                          ALIPIO CORREA NETO, PROF.   
4        205     EMEBS               VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...      ...       ...                                                ...   
4168  600047  ESP CONV  ASSOCIACAO CASA DOS DEFICIENTES DE ERMELINO MA...   
4169  600050  ESP CONV  AACD - ASS DE ASS A CRIANCA DEFICIENTE - UNID ...   
4170  600051  ESP CONV                    APAE - NUCLEO CAPELA DO SOCORRO   
4171  600052  ESP CONV                          APAE - NUCLEO CAMPO LIMPO   
4172  600056  ESP CONV                             APAE - NUCLEO PIRITUBA   

                      SUBPREF       DISTRITO     CODINEP     CD_CIE  \
0                  GUAIANASES     GUAIANASES  35098711.0  1678110.0   
1     CASA VERDE/CACHOEIRINHA          LIMAO  35098361.0  1670158.0   
2                  SAO MIGUEL  JARDIM HELENA  35098760.0  1677116.0   
3                     BUTANTA     VILA SONIA  35098462.0  1679154.0   
4                    PIRITUBA       PIRITUBA  35079029.0  1671138.0   
...                       ...            ...         ...        ...   
4168               SAO MIGUEL     SAO MIGUEL         NaN        NaN   
4169                    MOOCA          MOOCA         NaN        NaN   
4170        CAPELA DO SOCORRO   CIDADE DUTRA         NaN        NaN   
4171              CAMPO LIMPO    CAMPO LIMPO         NaN        NaN   
4172                     LAPA           LAPA         NaN        NaN   

                                           NOME_ANT REDE  \
0                                               NaN  DIR   
1                                               NaN  DIR   
2                               VILA NITRO OPERARIA  DIR   
3                                               NaN  DIR   
4                                               NaN  DIR   
...                                             ...  ...   
4168  ASSOCIACAO CASA DOS DEFICIENTES DE ERMELINO M  CON   
4169  AACD - ASS DE ASS A CRIANCA DEFICIENTE - UNID  CON   
4170                                           APAE  CON   
4171                                           APAE  CON   
4172                                            NaN  CON   

                                         NOMES_COMPLETO nm_distrito_municipal  \
0                       EMEI PAULO CAMILHIER FLORENCANO            GUAIANASES   
1                           EMEI VICENTE PAULO DA SILVA                 LIMAO   
2                     EMEF JOSE ERMIRIO DE MORAES, SEN.         JARDIM HELENA   
3                        EMEF ALIPIO CORREA NETO, PROF.            VILA SONIA   
4            EMEBS VERA LUCIA APARECIDA RIBEIRO, PROFA.              PIRITUBA   
...                                                 ...                   ...   
4168  ESP CONV ASSOCIACAO CASA DOS DEFICIENTES DE ER...            SAO MIGUEL   
4169  ESP CONV AACD - ASS DE ASS A CRIANCA DEFICIENT...                 MOOCA   
4170           ESP CONV APAE - NUCLEO CAPELA DO SOCORRO          CIDADE DUTRA   
4171                 ESP CONV APAE - NUCLEO CAMPO LIMPO           CAMPO LIMPO   
4172                    ESP CONV APAE - NUCLEO PIRITUBA                  LAPA   

     cd_subprefeitura         nm_subprefeitura  
0                  28               GUAIANASES  
1                  04  CASA VERDE-CACHOEIRINHA  
2                  23               SAO MIGUEL  
3                  10                  BUTANTA  
4                  02         PIRITUBA-JARAGUA  
...               ...                      ...  
4168               23               SAO MIGUEL  
4169               25                    MOOCA  
4170               19        CAPELA DO SOCORRO  
4171               17              CAMPO LIM

In [93]:
escolas_24[escolas_24['nm_subprefeitura'].isna()]

Empty DataFrame
Columns: [CODESC, TIPOESC, NOMES, SUBPREF, DISTRITO, CODINEP, CD_CIE, NOME_ANT, REDE, NOMES_COMPLETO, nm_distrito_municipal, cd_subprefeitura, nm_subprefeitura]
Index: []

### Perfil dos alunos

In [94]:
alunos_24 = alunos_24.merge(
    df_dist_sub[['nm_distrito_municipal', 'cd_subprefeitura', 'nm_subprefeitura']],
    left_on='DISTRITO',
    right_on='nm_distrito_municipal',
    how='left'
)

alunos_24

DISTRITO REDE   MODAL SEXO                      NEE    RACA  Qtde  \
0       VILA SONIA  DIR    FUND    F                      NaN   PARDA     3   
1       VILA SONIA  DIR    FUND    F                      NaN  BRANCA     3   
2       VILA SONIA  DIR    FUND    F                      NaN   PARDA     8   
3       VILA SONIA  DIR    FUND    F                      NaN   PRETA     2   
4       VILA SONIA  DIR    FUND    F  DEFICIENCIA INTELECTUAL  BRANCA     1   
...            ...  ...     ...  ...                      ...     ...   ...   
266342  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   
266343  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     2   
266344  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   
266345  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     1   
266346  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   

         Nível padronizado nm_distrito_municipal cd_subprefeitura  \
0       Ensino Fundamental            VILA SONIA               10   
1       Ensino Fundamental            VILA SONIA               10   
2       Ensino Fundamental            VILA SONIA               10   
3       Ensino Fundamental            VILA SONIA               10   
4       Ensino Fundamental            VILA SONIA               10   
...                    ...                   ...              ...   
266342   Educação Especial            SAO MATEUS               30   
266343   Educação Especial            SAO MATEUS               30   
266344   Educação Especial            SAO MATEUS               30   
266345   Educação Especial            SAO MATEUS               30   
266346   Educação Especial            SAO MATEUS               30   

       nm_subprefeitura  
0               BUTANTA  
1               BUTANTA  
2               BUTANTA  
3               BUTANTA  
4               BUTANTA  
...                 ...  
266342       SAO MATEUS  
266343       SAO MATEUS  
266344       SAO MATEUS  
266345       SAO MATEUS  
266346       SAO MATEUS  

[266347 rows x 11 columns]

In [95]:
alunos_24[alunos_24['nm_subprefeitura'].isna()]

Empty DataFrame
Columns: [DISTRITO, REDE, MODAL, SEXO, NEE, RACA, Qtde, Nível padronizado, nm_distrito_municipal, cd_subprefeitura, nm_subprefeitura]
Index: []

### Número de alunos estrangeiros

In [96]:
alunos_est_2024 = alunos_est_2024.merge(
    df_dist_sub[['nm_distrito_municipal', 'cd_subprefeitura', 'nm_subprefeitura']],
    left_on='DISTRITO',
    right_on='nm_distrito_municipal',
    how='left'
)

alunos_est_2024

DISTRITO  COD_PAIS                        NOME_PAIS   ETAPA  \
0     ALTO DE PINHEIROS        42                            CHINA  CRECHE   
1     ALTO DE PINHEIROS       226                       SERRA LEOA  CRECHE   
2               BUTANTA        26                         COLÔMBIA    FUND   
3               BUTANTA        31                          BÉLGICA    FUND   
4               BUTANTA        36  ESTADOS UNIDOS DA AMÉRICA (EUA)  CRECHE   
...                 ...       ...                              ...     ...   
3854          SAPOPEMBA       185                            CONGO    FUND   
3855          SAPOPEMBA       213                          NIGÉRIA    FUND   
3856          SAPOPEMBA       277                            SÍRIA     EJA   
3857          SAPOPEMBA       281                          TURQUIA  CRECHE   
3858          SAPOPEMBA       281                          TURQUIA  CRECHE   

     REDE  QTDE             Nível padronizado nm_distrito_municipal  \
0     CON     1             Educação Infantil     ALTO DE PINHEIROS   
1     CON     1             Educação Infantil     ALTO DE PINHEIROS   
2     DIR     1            Ensino Fundamental               BUTANTA   
3     DIR     1            Ensino Fundamental               BUTANTA   
4     CON     2             Educação Infantil               BUTANTA   
...   ...   ...                           ...                   ...   
3854  DIR     1            Ensino Fundamental             SAPOPEMBA   
3855  DIR     1            Ensino Fundamental             SAPOPEMBA   
3856  DIR     1  Educação de Jovens e Adultos             SAPOPEMBA   
3857  CON     1             Educação Infantil             SAPOPEMBA   
3858  CON     1             Educação Infantil             SAPOPEMBA   

     cd_subprefeitura nm_subprefeitura  
0                  11        PINHEIROS  
1                  11        PINHEIROS  
2                  10          BUTANTA  
3                  10          BUTANTA  
4                  10          BUTANTA  
...               ...              ...  
3854               32        SAPOPEMBA  
3855               32        SAPOPEMBA  
3856               32        SAPOPEMBA  
3857               32        SAPOPEMBA  
3858               32        SAPOPEMBA  

[3859 rows x 10 columns]

In [97]:
alunos_est_2024[alunos_est_2024['nm_subprefeitura'].isna()]

Empty DataFrame
Columns: [DISTRITO, COD_PAIS, NOME_PAIS, ETAPA, REDE, QTDE, Nível padronizado, nm_distrito_municipal, cd_subprefeitura, nm_subprefeitura]
Index: []

### Número de alunos beneficiários do Bolsa Família

In [98]:
alunos_bf_2024 = alunos_bf_2024.merge(
    df_dist_sub[['nm_distrito_municipal', 'cd_subprefeitura', 'nm_subprefeitura']],
    left_on='DISTRITO',
    right_on='nm_distrito_municipal',
    how='left'
)

alunos_bf_2024

CODEOL       TIPO                               UNIDADE  \
0          86       EMEI            PAULO CAMILHIER FLORENCANO   
1          94       EMEI                VICENTE PAULO DA SILVA   
2         108       EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3         191       EMEF             ALIPIO CORREA NETO, PROF.   
4         205      EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...       ...        ...                                   ...   
22573  400902  CEI INDIR                            ISMAEL IVO   
22574  400903  CEI INDIR                    JOSE DIAS SOBRINHO   
22575  400904  CEI INDIR                         RUBEM FONSECA   
22576  400906  CEI INDIR                   ZIRALDO ALVES PINTO   
22577  400908  CEI INDIR           RUTH VIDAL DA SILVA MARTINS   

                   DIRETORIA         DISTRITO              NIVEL  QTDE  \
0                 GUAIANASES       GUAIANASES             CRECHE     0   
1      FREGUESIA/BRASILANDIA            LIMAO             CRECHE     0   
2                 SAO MIGUEL    JARDIM HELENA             CRECHE     0   
3                    BUTANTA       VILA SONIA             CRECHE     0   
4                   PIRITUBA         PIRITUBA             CRECHE     0   
...                      ...              ...                ...   ...   
22573               IPIRANGA        SAO LUCAS  EDUCAÇÃO ESPECIAL     0   
22574        JACANA/TREMEMBE         TREMEMBE  EDUCAÇÃO ESPECIAL     0   
22575                  PENHA       PONTE RASA  EDUCAÇÃO ESPECIAL     0   
22576  FREGUESIA/BRASILANDIA      BRASILANDIA  EDUCAÇÃO ESPECIAL     0   
22577               PIRITUBA  VILA LEOPOLDINA  EDUCAÇÃO ESPECIAL     0   

       Nível padronizado nm_distrito_municipal cd_subprefeitura  \
0      Educação Infantil            GUAIANASES               28   
1      Educação Infantil                 LIMAO               04   
2      Educação Infantil         JARDIM HELENA               23   
3      Educação Infantil            VILA SONIA               10   
4      Educação Infantil              PIRITUBA               02   
...                  ...                   ...              ...   
22573  Educação Especial             SAO LUCAS               29   
22574  Educação Especial              TREMEMBE               06   
22575  Educação Especial            PONTE RASA               22   
22576  Educação Especial           BRASILANDIA               03   
22577  Educação Especial       VILA LEOPOLDINA               08   

              nm_subprefeitura  
0                   GUAIANASES  
1      CASA VERDE-CACHOEIRINHA  
2                   SAO MIGUEL  
3                      BUTANTA  
4             PIRITUBA-JARAGUA  
...                        ...  
22573            VILA PRUDENTE  
22574          JACANA-TREMEMBE  
22575       ERMELINO MATARAZZO  
22576    FREGUESIA-BRASILANDIA  
22577                     LAPA  

[22578 rows x 11 columns]

In [99]:
alunos_bf_2024[alunos_bf_2024['nm_subprefeitura'].isna()]

Empty DataFrame
Columns: [CODEOL, TIPO, UNIDADE, DIRETORIA, DISTRITO, NIVEL, QTDE, Nível padronizado, nm_distrito_municipal, cd_subprefeitura, nm_subprefeitura]
Index: []

### Número de professores da Rede Municipal de Ensino

In [100]:
perf_24 = perf_24.merge(
    df_dist_sub[['nm_distrito_municipal', 'cd_subprefeitura', 'nm_subprefeitura']],
    left_on='DISTRITO',
    right_on='nm_distrito_municipal',
    how='left'
)

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
1       9.274100e+13                 PROF.DE ED.INFANTIL   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA   
...              ...                                 ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I   
72341   9.274100e+13                 PROF.DE ED.INFANTIL   
72342   9.274100e+13                 PROF.DE ED.INFANTIL   

       DT_INICIO_CARGO_BASE  CD_CARGO_ATUAL  \
0                     41660    9.234430e+12   
1                     39588    9.274100e+13   
2                     34243    9.264550e+12   
3                     33605    9.244720e+12   
4                     39589    9.214970e+12   
...                     ...             ...   
72338                 41716    9.274100e+13   
72339                 40725    9.234430e+12   
72340                 40728    9.274940e+12   
72341                 43382    9.274100e+13   
72342                 39625    9.274100e+13   

                           DC_CARGO_ATUAL  ...  \
0                PROF.ED.INF.E ENS.FUND.I  ...   
1                     PROF.DE ED.INFANTIL  ...   
2           PROF.ENS.FUND.II E MED.-ARTES  ...   
3       PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4      PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...                                   ...  ...   
72338                 PROF.DE ED.INFANTIL  ...   
72339            PROF.ED.INF.E ENS.FUND.I  ...   
72340     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341                 PROF.DE ED.INFANTIL  ...   
72342                 PROF.DE ED.INFANTIL  ...   

                  DC_AREA_ATUACAO_BASE CD_UNIDADE_ATUAL  TP_UNIDADE_ATUAL  \
0      ENSINO FUNDAMENTAL I E INFANTIL     3.385170e+14              EMEI   
1                    EDUCACAO INFANTIL     8.271610e+15         CEI DIRET   
2                ENSINO FUNDAMENTAL II     1.236240e+14       FORA DE SME   
3                ENSINO FUNDAMENTAL II     1.375830e+13          CEU EMEF   
4                ENSINO FUNDAMENTAL II     3.335110e+14              EMEF   
...                                ...              ...               ...   
72338                EDUCACAO INFANTIL     1.315840e+13         CEU CEMEI   
72339  ENSINO FUNDAMENTAL I E INFANTIL     1.305490e+13              EMEF   
72340  ENSINO FUNDAMENTAL I E INFANTIL     1.315840e+13          CEU EMEF   
72341                EDUCACAO INFANTIL     8.271610e+15         CEI DIRET   
72342                EDUCACAO INFANTIL     8.246790e+14           CEU CEI   

                          DC_UNIDADE_ATUAL  \
0        THEREZINHA BATISTA PETTAN, PROFA.   
1                           JARDIM MONJOLO   
2            CAMARA MUNICIPAL DE SAO PAULO   
3                                 JAMBEIRO   
4      MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                    ...   
72338                       FRE

In [101]:
perf_24[perf_24['nm_subprefeitura'].isna() & ~perf_24['DISTRITO'].isna()]

Empty DataFrame
Columns: [CD_SEXO, CD_RACA_COR, DC_RACA_COR, CD_DEF, DC_SIT_FUNC, CD_CARGO_BASE, DC_CARGO_BASE, DT_INICIO_CARGO_BASE, CD_CARGO_ATUAL, DC_CARGO_ATUAL, CD_AREA_ATUACAO_BASE, DC_AREA_ATUACAO_BASE, CD_UNIDADE_ATUAL, TP_UNIDADE_ATUAL, DC_UNIDADE_ATUAL, DC_UNIDADE_ATUAL_COMPLETA, NOMES_COMPLETO, DISTRITO, nm_distrito_municipal, cd_subprefeitura, nm_subprefeitura]
Index: []

[0 rows x 21 columns]

## Adicionando tempo de atuação dos educadores na SME

In [102]:
ref_date = pd.to_datetime('2023-12-31')
ref_date

Timestamp('2023-12-31 00:00:00')

No ano de 2024, a coluna de data de início de atuação dos educadores foi disponibilizada com o formato numérico usado pelo Excel, que é o número de dias desde 30/12/1899. Vamos converter essa coluna para o formato de data.

In [103]:
perf_24['DT_INICIO_CARGO_BASE'] = perf_24['DT_INICIO_CARGO_BASE'].apply(
    lambda x: pd.to_datetime(xldate.xldate_as_datetime(x, 0))
    if isinstance(x, (int, float)) else pd.NaT
)

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE DT_INICIO_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2014-01-21   
1       9.274100e+13                 PROF.DE ED.INFANTIL           2008-05-20   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES           1993-10-01   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES           1992-01-02   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA           2008-05-21   
...              ...                                 ...                  ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL           2014-03-18   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-01   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-04   
72341   9.274100e+13                 PROF.DE ED.INFANTIL           2018-10-09   
72342   9.274100e+13                 PROF.DE ED.INFANTIL           2008-06-26   

       CD_CARGO_ATUAL                      DC_CARGO_ATUAL  ...  \
0        9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
1        9.274100e+13                 PROF.DE ED.INFANTIL  ...   
2        9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES  ...   
3        9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4        9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...               ...                                 ...  ...   
72338    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72339    9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
72340    9.274940e+12     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72342    9.274100e+13                 PROF.DE ED.INFANTIL  ...   

                  DC_AREA_ATUACAO_BASE CD_UNIDADE_ATUAL  TP_UNIDADE_ATUAL  \
0      ENSINO FUNDAMENTAL I E INFANTIL     3.385170e+14              EMEI   
1                    EDUCACAO INFANTIL     8.271610e+15         CEI DIRET   
2                ENSINO FUNDAMENTAL II     1.236240e+14       FORA DE SME   
3                ENSINO FUNDAMENTAL II     1.375830e+13          CEU EMEF   
4                ENSINO FUNDAMENTAL II     3.335110e+14              EMEF   
...                                ...              ...               ...   
72338                EDUCACAO INFANTIL     1.315840e+13         CEU CEMEI   
72339  ENSINO FUNDAMENTAL I E INFANTIL     1.305490e+13              EMEF   
72340  ENSINO FUNDAMENTAL I E INFANTIL     1.315840e+13          CEU EMEF   
72341                EDUCACAO INFANTIL     8.271610e+15         CEI DIRET   
72342                EDUCACAO INFANTIL     8.246790e+14           CEU CEI   

                          DC_UNIDADE_ATUAL  \
0        THEREZINHA BATISTA PETTAN, PROFA.   
1                           JARDIM MONJOLO   
2            CAMARA MUNICIPAL DE SAO PAULO   
3                                 JAMBEIRO   
4      MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                    ...   
72338                       FREGUESIA DO O   
72339                      FAZENDA DA JUTA   
72340                          ALTO ALEGRE   
72341         

In [104]:
perf_24['TEMPO_ATUACAO_SME'] =  ref_date - perf_24['DT_INICIO_CARGO_BASE']

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE DT_INICIO_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2014-01-21   
1       9.274100e+13                 PROF.DE ED.INFANTIL           2008-05-20   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES           1993-10-01   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES           1992-01-02   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA           2008-05-21   
...              ...                                 ...                  ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL           2014-03-18   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-01   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-04   
72341   9.274100e+13                 PROF.DE ED.INFANTIL           2018-10-09   
72342   9.274100e+13                 PROF.DE ED.INFANTIL           2008-06-26   

       CD_CARGO_ATUAL                      DC_CARGO_ATUAL  ...  \
0        9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
1        9.274100e+13                 PROF.DE ED.INFANTIL  ...   
2        9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES  ...   
3        9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4        9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...               ...                                 ...  ...   
72338    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72339    9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
72340    9.274940e+12     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72342    9.274100e+13                 PROF.DE ED.INFANTIL  ...   

       CD_UNIDADE_ATUAL TP_UNIDADE_ATUAL                     DC_UNIDADE_ATUAL  \
0          3.385170e+14             EMEI    THEREZINHA BATISTA PETTAN, PROFA.   
1          8.271610e+15        CEI DIRET                       JARDIM MONJOLO   
2          1.236240e+14      FORA DE SME        CAMARA MUNICIPAL DE SAO PAULO   
3          1.375830e+13         CEU EMEF                             JAMBEIRO   
4          3.335110e+14             EMEF  MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                 ...              ...                                  ...   
72338      1.315840e+13        CEU CEMEI                       FREGUESIA DO O   
72339      1.305490e+13             EMEF                      FAZENDA DA JUTA   
72340      1.315840e+13         CEU EMEF                          ALTO ALEGRE   
72341      8.271610e+15        CEI DIRET                     GENOVEVA DASCOLI   
72342      8.246790e+14          CEU CEI  ANA LUCIA DE HOLANDA GAMBOA, PROFA.   

                         DC_UNIDADE_ATUAL_COMPLETA  \
0           EMEI THEREZINHA BATISTA PETTAN, PROFA.   
1                         CEI DIRET JARDIM MONJOLO   
2        FORA DE SME CAMARA MUNICIPAL DE SAO PAULO   
3                                CEU EMEF JAMBEIRO   
4         EMEF MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                            ...   
72338                     CEU CEMEI FREGUESIA DO

In [105]:
perf_24['DIAS_ATUACAO_SME'] =  perf_24['TEMPO_ATUACAO_SME'].dt.days

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE DT_INICIO_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2014-01-21   
1       9.274100e+13                 PROF.DE ED.INFANTIL           2008-05-20   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES           1993-10-01   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES           1992-01-02   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA           2008-05-21   
...              ...                                 ...                  ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL           2014-03-18   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-01   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-04   
72341   9.274100e+13                 PROF.DE ED.INFANTIL           2018-10-09   
72342   9.274100e+13                 PROF.DE ED.INFANTIL           2008-06-26   

       CD_CARGO_ATUAL                      DC_CARGO_ATUAL  ...  \
0        9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
1        9.274100e+13                 PROF.DE ED.INFANTIL  ...   
2        9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES  ...   
3        9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4        9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...               ...                                 ...  ...   
72338    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72339    9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
72340    9.274940e+12     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72342    9.274100e+13                 PROF.DE ED.INFANTIL  ...   

       TP_UNIDADE_ATUAL                     DC_UNIDADE_ATUAL  \
0                  EMEI    THEREZINHA BATISTA PETTAN, PROFA.   
1             CEI DIRET                       JARDIM MONJOLO   
2           FORA DE SME        CAMARA MUNICIPAL DE SAO PAULO   
3              CEU EMEF                             JAMBEIRO   
4                  EMEF  MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                 ...                                  ...   
72338         CEU CEMEI                       FREGUESIA DO O   
72339              EMEF                      FAZENDA DA JUTA   
72340          CEU EMEF                          ALTO ALEGRE   
72341         CEI DIRET                     GENOVEVA DASCOLI   
72342           CEU CEI  ANA LUCIA DE HOLANDA GAMBOA, PROFA.   

                         DC_UNIDADE_ATUAL_COMPLETA  \
0           EMEI THEREZINHA BATISTA PETTAN, PROFA.   
1                         CEI DIRET JARDIM MONJOLO   
2        FORA DE SME CAMARA MUNICIPAL DE SAO PAULO   
3                                CEU EMEF JAMBEIRO   
4         EMEF MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                            ...   
72338                     CEU CEMEI FREGUESIA DO O   
72339                         EMEF FAZENDA DA JUTA   
72340                         CEU EMEF ALTO ALEGRE   
72341                   CEI DIRET GENOVEVA DASCOLI   
72342  CEU CEI ANA LUCIA DE HOLANDA 

In [106]:
perf_24['ANOS_ATUACAO_SME'] =  perf_24['TEMPO_ATUACAO_SME'].dt.days / 365.25
perf_24['ANOS_ATUACAO_SME'] = round(perf_24['ANOS_ATUACAO_SME'], 2)

perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE DT_INICIO_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2014-01-21   
1       9.274100e+13                 PROF.DE ED.INFANTIL           2008-05-20   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES           1993-10-01   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES           1992-01-02   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA           2008-05-21   
...              ...                                 ...                  ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL           2014-03-18   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-01   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-04   
72341   9.274100e+13                 PROF.DE ED.INFANTIL           2018-10-09   
72342   9.274100e+13                 PROF.DE ED.INFANTIL           2008-06-26   

       CD_CARGO_ATUAL                      DC_CARGO_ATUAL  ...  \
0        9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
1        9.274100e+13                 PROF.DE ED.INFANTIL  ...   
2        9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES  ...   
3        9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4        9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...               ...                                 ...  ...   
72338    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72339    9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
72340    9.274940e+12     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72342    9.274100e+13                 PROF.DE ED.INFANTIL  ...   

                          DC_UNIDADE_ATUAL  \
0        THEREZINHA BATISTA PETTAN, PROFA.   
1                           JARDIM MONJOLO   
2            CAMARA MUNICIPAL DE SAO PAULO   
3                                 JAMBEIRO   
4      MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                    ...   
72338                       FREGUESIA DO O   
72339                      FAZENDA DA JUTA   
72340                          ALTO ALEGRE   
72341                     GENOVEVA DASCOLI   
72342  ANA LUCIA DE HOLANDA GAMBOA, PROFA.   

                         DC_UNIDADE_ATUAL_COMPLETA  \
0           EMEI THEREZINHA BATISTA PETTAN, PROFA.   
1                         CEI DIRET JARDIM MONJOLO   
2        FORA DE SME CAMARA MUNICIPAL DE SAO PAULO   
3                                CEU EMEF JAMBEIRO   
4         EMEF MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                            ...   
72338                     CEU CEMEI FREGUESIA DO O   
72339                         EMEF FAZENDA DA JUTA   
72340                         CEU EMEF ALTO ALEGRE   
72341                   CEI DIRET GENOVEVA DASCOLI   
72342  CEU CEI ANA LUCIA DE HOLANDA GAMBOA, PROFA.   

                                    NOMES_COMPLETO        DISTRITO  \
0           EMEI THEREZINHA BATISTA PETTAN, PROFA.         CURSINO   
1                         CEI DIRET JARDIM MONJOLO  FREGU

In [107]:
perf_24 = perf_24.drop(columns='TEMPO_ATUACAO_SME')
perf_24

CD_SEXO  CD_RACA_COR    DC_RACA_COR       CD_DEF DC_SIT_FUNC  \
0           F   1311820840         BRANCA  12727970840     EFETIVO   
1           F   1311820840         BRANCA  12727970840     EFETIVO   
2           F   1311820840         BRANCA  12727970840     EFETIVO   
3           F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
4           F   1311820840         BRANCA  12727970840     EFETIVO   
...       ...          ...            ...          ...         ...   
72338       F   1311820840         BRANCA  12727970840     EFETIVO   
72339       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72340       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   
72341       F  93911221827          PARDA  12727970840     EFETIVO   
72342       F   6361921931  NAO INFORMADA  12727970840     EFETIVO   

       CD_CARGO_BASE                       DC_CARGO_BASE DT_INICIO_CARGO_BASE  \
0       9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2014-01-21   
1       9.274100e+13                 PROF.DE ED.INFANTIL           2008-05-20   
2       9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES           1993-10-01   
3       9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES           1992-01-02   
4       9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA           2008-05-21   
...              ...                                 ...                  ...   
72338   9.274100e+13                 PROF.DE ED.INFANTIL           2014-03-18   
72339   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-01   
72340   9.234430e+12            PROF.ED.INF.E ENS.FUND.I           2011-07-04   
72341   9.274100e+13                 PROF.DE ED.INFANTIL           2018-10-09   
72342   9.274100e+13                 PROF.DE ED.INFANTIL           2008-06-26   

       CD_CARGO_ATUAL                      DC_CARGO_ATUAL  ...  \
0        9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
1        9.274100e+13                 PROF.DE ED.INFANTIL  ...   
2        9.264550e+12       PROF.ENS.FUND.II E MED.-ARTES  ...   
3        9.244720e+12   PROF.ENS.FUND.II E MED.-PORTUGUES  ...   
4        9.214970e+12  PROF.ENS.FUND.II E MED.-MATEMATICA  ...   
...               ...                                 ...  ...   
72338    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72339    9.234430e+12            PROF.ED.INF.E ENS.FUND.I  ...   
72340    9.274940e+12     ASSISTENTE DE DIRETOR DE ESCOLA  ...   
72341    9.274100e+13                 PROF.DE ED.INFANTIL  ...   
72342    9.274100e+13                 PROF.DE ED.INFANTIL  ...   

       TP_UNIDADE_ATUAL                     DC_UNIDADE_ATUAL  \
0                  EMEI    THEREZINHA BATISTA PETTAN, PROFA.   
1             CEI DIRET                       JARDIM MONJOLO   
2           FORA DE SME        CAMARA MUNICIPAL DE SAO PAULO   
3              CEU EMEF                             JAMBEIRO   
4                  EMEF  MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                 ...                                  ...   
72338         CEU CEMEI                       FREGUESIA DO O   
72339              EMEF                      FAZENDA DA JUTA   
72340          CEU EMEF                          ALTO ALEGRE   
72341         CEI DIRET                     GENOVEVA DASCOLI   
72342           CEU CEI  ANA LUCIA DE HOLANDA GAMBOA, PROFA.   

                         DC_UNIDADE_ATUAL_COMPLETA  \
0           EMEI THEREZINHA BATISTA PETTAN, PROFA.   
1                         CEI DIRET JARDIM MONJOLO   
2        FORA DE SME CAMARA MUNICIPAL DE SAO PAULO   
3                                CEU EMEF JAMBEIRO   
4         EMEF MARTIN FRANCISCO RIBEIRO DE ANDRADA   
...                                            ...   
72338                     CEU CEMEI FREGUESIA DO O   
72339                         EMEF FAZENDA DA JUTA   
72340                         CEU EMEF ALTO ALEGRE   
72341                   CEI DIRET GENOVEVA DASCOLI   
72342  CEU CEI ANA LUCIA DE HOLANDA 

## Adicionando chave composta nível padronizado e Subprefeitura

### Criando tabela de níveis padronizados e subprefeituras

In [108]:
nivel_padronizado = pd.DataFrame(
    data=['Educação Infantil',
          'Ensino Fundamental',
          'Ensino Médio',
          'Educação de Jovens e Adultos',
          'Educação Especial'],
    columns=['Nível padronizado']
)

nivel_padronizado

Nível padronizado
0             Educação Infantil
1            Ensino Fundamental
2                  Ensino Médio
3  Educação de Jovens e Adultos
4             Educação Especial

In [109]:
nivel_padronizado = (
    nivel_padronizado
    .merge(df_subs['nm_subprefeitura'], how='cross')
)

nivel_padronizado

Nível padronizado         nm_subprefeitura
0    Educação Infantil         PIRITUBA-JARAGUA
1    Educação Infantil    FREGUESIA-BRASILANDIA
2    Educação Infantil  CASA VERDE-CACHOEIRINHA
3    Educação Infantil         SANTANA-TUCURUVI
4    Educação Infantil          JACANA-TREMEMBE
..                 ...                      ...
155  Educação Especial                JABAQUARA
156  Educação Especial              SANTO AMARO
157  Educação Especial        CIDADE TIRADENTES
158  Educação Especial                    PERUS
159  Educação Especial                SAPOPEMBA

[160 rows x 2 columns]

In [110]:
nivel_padronizado['nivel_subprefeitura'] = (
    nivel_padronizado['Nível padronizado']
    + '|'
    + nivel_padronizado['nm_subprefeitura']
)

nivel_padronizado

Nível padronizado         nm_subprefeitura  \
0    Educação Infantil         PIRITUBA-JARAGUA   
1    Educação Infantil    FREGUESIA-BRASILANDIA   
2    Educação Infantil  CASA VERDE-CACHOEIRINHA   
3    Educação Infantil         SANTANA-TUCURUVI   
4    Educação Infantil          JACANA-TREMEMBE   
..                 ...                      ...   
155  Educação Especial                JABAQUARA   
156  Educação Especial              SANTO AMARO   
157  Educação Especial        CIDADE TIRADENTES   
158  Educação Especial                    PERUS   
159  Educação Especial                SAPOPEMBA   

                           nivel_subprefeitura  
0           Educação Infantil|PIRITUBA-JARAGUA  
1      Educação Infantil|FREGUESIA-BRASILANDIA  
2    Educação Infantil|CASA VERDE-CACHOEIRINHA  
3           Educação Infantil|SANTANA-TUCURUVI  
4            Educação Infantil|JACANA-TREMEMBE  
..                                         ...  
155                Educação Especial|JABAQUARA  
156              Educação Especial|SANTO AMARO  
157        Educação Especial|CIDADE TIRADENTES  
158                    Educação Especial|PERUS  
159                Educação Especial|SAPOPEMBA  

[160 rows x 3 columns]

### Adicionando a coluna de nível padronizado e subprefeitura aos outros dataframes

In [111]:
alunos_24 = alunos_24.merge(
    nivel_padronizado,
    left_on=['Nível padronizado', 'nm_subprefeitura'],
    right_on=['Nível padronizado', 'nm_subprefeitura'],
    how='left'
)

alunos_24

DISTRITO REDE   MODAL SEXO                      NEE    RACA  Qtde  \
0       VILA SONIA  DIR    FUND    F                      NaN   PARDA     3   
1       VILA SONIA  DIR    FUND    F                      NaN  BRANCA     3   
2       VILA SONIA  DIR    FUND    F                      NaN   PARDA     8   
3       VILA SONIA  DIR    FUND    F                      NaN   PRETA     2   
4       VILA SONIA  DIR    FUND    F  DEFICIENCIA INTELECTUAL  BRANCA     1   
...            ...  ...     ...  ...                      ...     ...   ...   
266342  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   
266343  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     2   
266344  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   
266345  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL  BRANCA     1   
266346  SAO MATEUS  CON  CONVEE    M  DEFICIENCIA INTELECTUAL   PARDA     1   

         Nível padronizado nm_distrito_municipal cd_subprefeitura  \
0       Ensino Fundamental            VILA SONIA               10   
1       Ensino Fundamental            VILA SONIA               10   
2       Ensino Fundamental            VILA SONIA               10   
3       Ensino Fundamental            VILA SONIA               10   
4       Ensino Fundamental            VILA SONIA               10   
...                    ...                   ...              ...   
266342   Educação Especial            SAO MATEUS               30   
266343   Educação Especial            SAO MATEUS               30   
266344   Educação Especial            SAO MATEUS               30   
266345   Educação Especial            SAO MATEUS               30   
266346   Educação Especial            SAO MATEUS               30   

       nm_subprefeitura           nivel_subprefeitura  
0               BUTANTA    Ensino Fundamental|BUTANTA  
1               BUTANTA    Ensino Fundamental|BUTANTA  
2               BUTANTA    Ensino Fundamental|BUTANTA  
3               BUTANTA    Ensino Fundamental|BUTANTA  
4               BUTANTA    Ensino Fundamental|BUTANTA  
...                 ...                           ...  
266342       SAO MATEUS  Educação Especial|SAO MATEUS  
266343       SAO MATEUS  Educação Especial|SAO MATEUS  
266344       SAO MATEUS  Educação Especial|SAO MATEUS  
266345       SAO MATEUS  Educação Especial|SAO MATEUS  
266346       SAO MATEUS  Educação Especial|SAO MATEUS  

[266347 rows x 12 columns]

In [112]:
alunos_est_2024 = alunos_est_2024.merge(
    nivel_padronizado,
    left_on=['Nível padronizado', 'nm_subprefeitura'],
    right_on=['Nível padronizado', 'nm_subprefeitura'],
    how='left'
)

alunos_est_2024

DISTRITO  COD_PAIS                        NOME_PAIS   ETAPA  \
0     ALTO DE PINHEIROS        42                            CHINA  CRECHE   
1     ALTO DE PINHEIROS       226                       SERRA LEOA  CRECHE   
2               BUTANTA        26                         COLÔMBIA    FUND   
3               BUTANTA        31                          BÉLGICA    FUND   
4               BUTANTA        36  ESTADOS UNIDOS DA AMÉRICA (EUA)  CRECHE   
...                 ...       ...                              ...     ...   
3854          SAPOPEMBA       185                            CONGO    FUND   
3855          SAPOPEMBA       213                          NIGÉRIA    FUND   
3856          SAPOPEMBA       277                            SÍRIA     EJA   
3857          SAPOPEMBA       281                          TURQUIA  CRECHE   
3858          SAPOPEMBA       281                          TURQUIA  CRECHE   

     REDE  QTDE             Nível padronizado nm_distrito_municipal  \
0     CON     1             Educação Infantil     ALTO DE PINHEIROS   
1     CON     1             Educação Infantil     ALTO DE PINHEIROS   
2     DIR     1            Ensino Fundamental               BUTANTA   
3     DIR     1            Ensino Fundamental               BUTANTA   
4     CON     2             Educação Infantil               BUTANTA   
...   ...   ...                           ...                   ...   
3854  DIR     1            Ensino Fundamental             SAPOPEMBA   
3855  DIR     1            Ensino Fundamental             SAPOPEMBA   
3856  DIR     1  Educação de Jovens e Adultos             SAPOPEMBA   
3857  CON     1             Educação Infantil             SAPOPEMBA   
3858  CON     1             Educação Infantil             SAPOPEMBA   

     cd_subprefeitura nm_subprefeitura                     nivel_subprefeitura  
0                  11        PINHEIROS             Educação Infantil|PINHEIROS  
1                  11        PINHEIROS             Educação Infantil|PINHEIROS  
2                  10          BUTANTA              Ensino Fundamental|BUTANTA  
3                  10          BUTANTA              Ensino Fundamental|BUTANTA  
4                  10          BUTANTA               Educação Infantil|BUTANTA  
...               ...              ...                                     ...  
3854               32        SAPOPEMBA            Ensino Fundamental|SAPOPEMBA  
3855               32        SAPOPEMBA            Ensino Fundamental|SAPOPEMBA  
3856               32        SAPOPEMBA  Educação de Jovens e Adultos|SAPOPEMBA  
3857               32        SAPOPEMBA             Educação Infantil|SAPOPEMBA  
3858               32        SAPOPEMBA             Educação Infantil|SAPOPEMBA  

[3859 rows x 11 columns]

In [113]:
alunos_bf_2024 = alunos_bf_2024.merge(
    nivel_padronizado,
    left_on=['Nível padronizado', 'nm_subprefeitura'],
    right_on=['Nível padronizado', 'nm_subprefeitura'],
    how='left'
)

alunos_bf_2024

CODEOL       TIPO                               UNIDADE  \
0          86       EMEI            PAULO CAMILHIER FLORENCANO   
1          94       EMEI                VICENTE PAULO DA SILVA   
2         108       EMEF          JOSE ERMIRIO DE MORAES, SEN.   
3         191       EMEF             ALIPIO CORREA NETO, PROF.   
4         205      EMEBS  VERA LUCIA APARECIDA RIBEIRO, PROFA.   
...       ...        ...                                   ...   
22573  400902  CEI INDIR                            ISMAEL IVO   
22574  400903  CEI INDIR                    JOSE DIAS SOBRINHO   
22575  400904  CEI INDIR                         RUBEM FONSECA   
22576  400906  CEI INDIR                   ZIRALDO ALVES PINTO   
22577  400908  CEI INDIR           RUTH VIDAL DA SILVA MARTINS   

                   DIRETORIA         DISTRITO              NIVEL  QTDE  \
0                 GUAIANASES       GUAIANASES             CRECHE     0   
1      FREGUESIA/BRASILANDIA            LIMAO             CRECHE     0   
2                 SAO MIGUEL    JARDIM HELENA             CRECHE     0   
3                    BUTANTA       VILA SONIA             CRECHE     0   
4                   PIRITUBA         PIRITUBA             CRECHE     0   
...                      ...              ...                ...   ...   
22573               IPIRANGA        SAO LUCAS  EDUCAÇÃO ESPECIAL     0   
22574        JACANA/TREMEMBE         TREMEMBE  EDUCAÇÃO ESPECIAL     0   
22575                  PENHA       PONTE RASA  EDUCAÇÃO ESPECIAL     0   
22576  FREGUESIA/BRASILANDIA      BRASILANDIA  EDUCAÇÃO ESPECIAL     0   
22577               PIRITUBA  VILA LEOPOLDINA  EDUCAÇÃO ESPECIAL     0   

       Nível padronizado nm_distrito_municipal cd_subprefeitura  \
0      Educação Infantil            GUAIANASES               28   
1      Educação Infantil                 LIMAO               04   
2      Educação Infantil         JARDIM HELENA               23   
3      Educação Infantil            VILA SONIA               10   
4      Educação Infantil              PIRITUBA               02   
...                  ...                   ...              ...   
22573  Educação Especial             SAO LUCAS               29   
22574  Educação Especial              TREMEMBE               06   
22575  Educação Especial            PONTE RASA               22   
22576  Educação Especial           BRASILANDIA               03   
22577  Educação Especial       VILA LEOPOLDINA               08   

              nm_subprefeitura                        nivel_subprefeitura  
0                   GUAIANASES               Educação Infantil|GUAIANASES  
1      CASA VERDE-CACHOEIRINHA  Educação Infantil|CASA VERDE-CACHOEIRINHA  
2                   SAO MIGUEL               Educação Infantil|SAO MIGUEL  
3                      BUTANTA                  Educação Infantil|BUTANTA  
4             PIRITUBA-JARAGUA         Educação Infantil|PIRITUBA-JARAGUA  
...                        ...                                        ...  
22573            VILA PRUDENTE            Educação Especial|VILA PRUDENTE  
22574          JACANA-TREMEMBE          Educação Especial|JACANA-TREMEMBE  
22575       ERMELINO MATARAZZO       Educação Especial|ERMELINO MATARAZZO  
22576    FREGUESIA-BRASILANDIA    Educação Especial|FREGUESIA-BRASILANDIA  
22577                     LAPA                     Educação Especial|LAPA  

[22578 rows x 12 columns]

## Orçamento da função Educação

Para o orçamento, além de padronizar os nomes de subprefeituras e tipos de dados das métricas, precisaremos também adaptar os dados para compatibilizar o orçamento regionalizado e não realizado. Para isso, vamos fazer o seguinte:

1. Classificar o orçamento detalhado por nível de regionalização nas seguintes categorias: subprefeitura, região e não regionalizável;
1. Agrupar o restante do orçamento não detalhado e manter apenas o orçamento inicial, atualizado e liquidado;
1. Subtrair o total do orçamento detalhado do orçamento não detalhado e classificar o nível de regionalização como não regionalizado;
1. Unir os dois dataframes de orçamento de acordo com as dimensões mantidas.

### Orçamento regionalizado

In [114]:
df_orcamento_r.head(1)

COD_EMPRESA_PMSP COD_EMPENHO ANO_EMPENHO CÓDIGO_NLP ANO_LIQUIDAÇÃO  \
11               01           1        2024      72189           2024   

                DATA_LIQUIDAÇÃO CÓDIGO_ÓRGÃO SIGLA_ÓRGÃO  \
11  2024-03-18 00:00:00.0000000           16         SME   

                     DESCRIÇÃO_ÓRGÃO CÓDIGO_UNIDADE  ...  \
11  Secretaria Municipal de Educação             10  ...   

                        DESCRIÇÃO_FONTE CÓDIGO_EXERCÍCIO_FONTE  \
11  Recursos não vinculados de Impostos                      1   

   CÓDIGO_DESTINAÇÃO_RECURSO CÓDIGO_VÍNCULO_PMSP  \
11                       500                9001   

   CÓDIGO_TIPO_CRÉDITO_ORÇAMENTÁRIO          REGIÃO        SUBPREFEITURA  \
11                                0  Supra-Regional  Supra Subprefeitura   

           DISTRITO         TIPO_REGIONALIZAÇÃO VALOR_DETALHAMENTO_AÇÃO  
11  Supra-Distrital  Despesa Não-Regionalizável                84181.62  

[1 rows x 32 columns]

In [115]:
cols_orcamento_r = ['CÓDIGO_SUBFUNÇÃO', 'DESCRIÇÃO_SUBFUNÇÃO',
                    'CÓDIGO_FONTE', 'REGIÃO',
                    'SUBPREFEITURA', 'TIPO_REGIONALIZAÇÃO']

cols_orcamento_r_vl = ['VALOR_DETALHAMENTO_AÇÃO']

df_orcamento_r = df_orcamento_r[cols_orcamento_r + cols_orcamento_r_vl]
df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
11                  122  Administração Geral           00  Supra-Regional   
12                  122  Administração Geral           00  Supra-Regional   
13                  122  Administração Geral           00  Supra-Regional   
14                  122  Administração Geral           00  Supra-Regional   
15                  122  Administração Geral           00  Supra-Regional   
...                 ...                  ...          ...             ...   
493950              363  Ensino Profissional           00             NaN   
493951              363  Ensino Profissional           00          Centro   
493952              363  Ensino Profissional           00          Centro   
493953              363  Ensino Profissional           00          Centro   
493955              122  Administração Geral           00             NaN   

                     SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
11             Supra Subprefeitura  Despesa Não-Regionalizável   
12             Supra Subprefeitura  Despesa Não-Regionalizável   
13             Supra Subprefeitura  Despesa Não-Regionalizável   
14             Supra Subprefeitura  Despesa Não-Regionalizável   
15             Supra Subprefeitura  Despesa Não-Regionalizável   
...                            ...                         ...   
493950                         NaN                         NaN   
493951  Supra Subprefeitura Centro      Despesa Regionalizável   
493952  Supra Subprefeitura Centro      Despesa Regionalizável   
493953  Supra Subprefeitura Centro      Despesa Regionalizável   
493955                         NaN                         NaN   

        VALOR_DETALHAMENTO_AÇÃO  
11                     84181.62  
12                       926.39  
13                     91415.48  
14                       964.51  
15                     88176.28  
...                         ...  
493950                      NaN  
493951                 11467.36  
493952                  8665.06  
493953                   397.05  
493955                      NaN  

[140630 rows x 7 columns]

In [116]:
df_orcamento_r['TIPO_REGIONALIZAÇÃO'].value_counts()

TIPO_REGIONALIZAÇÃO
Despesa Regionalizável        88092
Despesa Não-Regionalizável    18241
Name: count, dtype: int64

In [117]:
df_orcamento_r.loc[df_orcamento_r['TIPO_REGIONALIZAÇÃO'].isna(), 'TIPO_REGIONALIZAÇÃO'] = 'Despesa Não-Regionalizável'
df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
11                  122  Administração Geral           00  Supra-Regional   
12                  122  Administração Geral           00  Supra-Regional   
13                  122  Administração Geral           00  Supra-Regional   
14                  122  Administração Geral           00  Supra-Regional   
15                  122  Administração Geral           00  Supra-Regional   
...                 ...                  ...          ...             ...   
493950              363  Ensino Profissional           00             NaN   
493951              363  Ensino Profissional           00          Centro   
493952              363  Ensino Profissional           00          Centro   
493953              363  Ensino Profissional           00          Centro   
493955              122  Administração Geral           00             NaN   

                     SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
11             Supra Subprefeitura  Despesa Não-Regionalizável   
12             Supra Subprefeitura  Despesa Não-Regionalizável   
13             Supra Subprefeitura  Despesa Não-Regionalizável   
14             Supra Subprefeitura  Despesa Não-Regionalizável   
15             Supra Subprefeitura  Despesa Não-Regionalizável   
...                            ...                         ...   
493950                         NaN  Despesa Não-Regionalizável   
493951  Supra Subprefeitura Centro      Despesa Regionalizável   
493952  Supra Subprefeitura Centro      Despesa Regionalizável   
493953  Supra Subprefeitura Centro      Despesa Regionalizável   
493955                         NaN  Despesa Não-Regionalizável   

        VALOR_DETALHAMENTO_AÇÃO  
11                     84181.62  
12                       926.39  
13                     91415.48  
14                       964.51  
15                     88176.28  
...                         ...  
493950                      NaN  
493951                 11467.36  
493952                  8665.06  
493953                   397.05  
493955                      NaN  

[140630 rows x 7 columns]

In [118]:
df_orcamento_r['TIPO_REGIONALIZAÇÃO'].value_counts()

TIPO_REGIONALIZAÇÃO
Despesa Regionalizável        88092
Despesa Não-Regionalizável    52538
Name: count, dtype: int64

In [119]:
df_orcamento_r = df_orcamento_r.groupby(cols_orcamento_r).sum().round(2).reset_index()

df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                122  Administração Geral           00          Centro   
1                122  Administração Geral           00           Oeste   
2                122  Administração Geral           00             Sul   
3                122  Administração Geral           00             Sul   
4                122  Administração Geral           00  Supra-Regional   
..               ...                  ...          ...             ...   
278              368      Educação Básica           00             Sul   
279              368      Educação Básica           00             Sul   
280              368      Educação Básica           00             Sul   
281              368      Educação Básica           00  Supra-Regional   
282              368      Educação Básica           02  Supra-Regional   

                  SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0    Supra Subprefeitura Centro      Despesa Regionalizável   
1            Subprefeitura Lapa      Despesa Regionalizável   
2        Subprefeitura Ipiranga      Despesa Regionalizável   
3    Subprefeitura Vila Mariana      Despesa Regionalizável   
4           Supra Subprefeitura  Despesa Não-Regionalizável   
..                          ...                         ...   
278   Subprefeitura Santo Amaro      Despesa Regionalizável   
279  Subprefeitura Vila Mariana      Despesa Regionalizável   
280     Supra Subprefeitura Sul      Despesa Regionalizável   
281         Supra Subprefeitura  Despesa Não-Regionalizável   
282         Supra Subprefeitura  Despesa Não-Regionalizável   

     VALOR_DETALHAMENTO_AÇÃO  
0               1.818885e+06  
1               8.227545e+05  
2               6.646144e+04  
3               2.680670e+04  
4               1.239509e+08  
..                       ...  
278             7.164826e+05  
279             2.676908e+06  
280             3.167627e+07  
281             2.151326e+08  
282             1.431150e+07  

[283 rows x 7 columns]

In [120]:
df_orcamento_r.loc[
    ~df_orcamento_r['REGIÃO'].str.contains('Supra', na=False),
    'NIVEL_REGIONALIZAÇÃO'] = 'Região'

df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                122  Administração Geral           00          Centro   
1                122  Administração Geral           00           Oeste   
2                122  Administração Geral           00             Sul   
3                122  Administração Geral           00             Sul   
4                122  Administração Geral           00  Supra-Regional   
..               ...                  ...          ...             ...   
278              368      Educação Básica           00             Sul   
279              368      Educação Básica           00             Sul   
280              368      Educação Básica           00             Sul   
281              368      Educação Básica           00  Supra-Regional   
282              368      Educação Básica           02  Supra-Regional   

                  SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0    Supra Subprefeitura Centro      Despesa Regionalizável   
1            Subprefeitura Lapa      Despesa Regionalizável   
2        Subprefeitura Ipiranga      Despesa Regionalizável   
3    Subprefeitura Vila Mariana      Despesa Regionalizável   
4           Supra Subprefeitura  Despesa Não-Regionalizável   
..                          ...                         ...   
278   Subprefeitura Santo Amaro      Despesa Regionalizável   
279  Subprefeitura Vila Mariana      Despesa Regionalizável   
280     Supra Subprefeitura Sul      Despesa Regionalizável   
281         Supra Subprefeitura  Despesa Não-Regionalizável   
282         Supra Subprefeitura  Despesa Não-Regionalizável   

     VALOR_DETALHAMENTO_AÇÃO NIVEL_REGIONALIZAÇÃO  
0               1.818885e+06               Região  
1               8.227545e+05               Região  
2               6.646144e+04               Região  
3               2.680670e+04               Região  
4               1.239509e+08                  NaN  
..                       ...                  ...  
278             7.164826e+05               Região  
279             2.676908e+06               Região  
280             3.167627e+07               Região  
281             2.151326e+08                  NaN  
282             1.431150e+07                  NaN  

[283 rows x 8 columns]

In [121]:
df_orcamento_r.loc[
    ~df_orcamento_r['SUBPREFEITURA'].str.contains('Supra', na=False),
    'NIVEL_REGIONALIZAÇÃO'] = 'Subprefeitura'

df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                122  Administração Geral           00          Centro   
1                122  Administração Geral           00           Oeste   
2                122  Administração Geral           00             Sul   
3                122  Administração Geral           00             Sul   
4                122  Administração Geral           00  Supra-Regional   
..               ...                  ...          ...             ...   
278              368      Educação Básica           00             Sul   
279              368      Educação Básica           00             Sul   
280              368      Educação Básica           00             Sul   
281              368      Educação Básica           00  Supra-Regional   
282              368      Educação Básica           02  Supra-Regional   

                  SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0    Supra Subprefeitura Centro      Despesa Regionalizável   
1            Subprefeitura Lapa      Despesa Regionalizável   
2        Subprefeitura Ipiranga      Despesa Regionalizável   
3    Subprefeitura Vila Mariana      Despesa Regionalizável   
4           Supra Subprefeitura  Despesa Não-Regionalizável   
..                          ...                         ...   
278   Subprefeitura Santo Amaro      Despesa Regionalizável   
279  Subprefeitura Vila Mariana      Despesa Regionalizável   
280     Supra Subprefeitura Sul      Despesa Regionalizável   
281         Supra Subprefeitura  Despesa Não-Regionalizável   
282         Supra Subprefeitura  Despesa Não-Regionalizável   

     VALOR_DETALHAMENTO_AÇÃO NIVEL_REGIONALIZAÇÃO  
0               1.818885e+06               Região  
1               8.227545e+05        Subprefeitura  
2               6.646144e+04        Subprefeitura  
3               2.680670e+04        Subprefeitura  
4               1.239509e+08                  NaN  
..                       ...                  ...  
278             7.164826e+05        Subprefeitura  
279             2.676908e+06        Subprefeitura  
280             3.167627e+07               Região  
281             2.151326e+08                  NaN  
282             1.431150e+07                  NaN  

[283 rows x 8 columns]

In [122]:
df_orcamento_r.loc[df_orcamento_r['NIVEL_REGIONALIZAÇÃO'].isna(), 'NIVEL_REGIONALIZAÇÃO'] = 'Não regionalizável'
df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                122  Administração Geral           00          Centro   
1                122  Administração Geral           00           Oeste   
2                122  Administração Geral           00             Sul   
3                122  Administração Geral           00             Sul   
4                122  Administração Geral           00  Supra-Regional   
..               ...                  ...          ...             ...   
278              368      Educação Básica           00             Sul   
279              368      Educação Básica           00             Sul   
280              368      Educação Básica           00             Sul   
281              368      Educação Básica           00  Supra-Regional   
282              368      Educação Básica           02  Supra-Regional   

                  SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0    Supra Subprefeitura Centro      Despesa Regionalizável   
1            Subprefeitura Lapa      Despesa Regionalizável   
2        Subprefeitura Ipiranga      Despesa Regionalizável   
3    Subprefeitura Vila Mariana      Despesa Regionalizável   
4           Supra Subprefeitura  Despesa Não-Regionalizável   
..                          ...                         ...   
278   Subprefeitura Santo Amaro      Despesa Regionalizável   
279  Subprefeitura Vila Mariana      Despesa Regionalizável   
280     Supra Subprefeitura Sul      Despesa Regionalizável   
281         Supra Subprefeitura  Despesa Não-Regionalizável   
282         Supra Subprefeitura  Despesa Não-Regionalizável   

     VALOR_DETALHAMENTO_AÇÃO NIVEL_REGIONALIZAÇÃO  
0               1.818885e+06               Região  
1               8.227545e+05        Subprefeitura  
2               6.646144e+04        Subprefeitura  
3               2.680670e+04        Subprefeitura  
4               1.239509e+08   Não regionalizável  
..                       ...                  ...  
278             7.164826e+05        Subprefeitura  
279             2.676908e+06        Subprefeitura  
280             3.167627e+07               Região  
281             2.151326e+08   Não regionalizável  
282             1.431150e+07   Não regionalizável  

[283 rows x 8 columns]

### Orçamento não regionalizado

In [123]:
df_orcamento.head(1)

DataInicial   DataFinal Cd_AnoExecucao Cd_Exercicio Cd_Dotacao_Id  \
589  01/01/2024  31/12/2024           2024         2024        174256   

    Administracao Cd_Orgao Sigla_Orgao                          Ds_Orgao  \
589        Direta       16         SME  Secretaria Municipal de Educação   

    Cd_Unidade  ... Vl_Congelado Vl_Descongelado Vl_CongeladoLiquido  \
589         10  ...          0.0             0.0                 0.0   

    Disponivel Vl_ReservadoLiquido Vl_EmpenhadoLiquido Vl_Liquidado Vl_Pago  \
589          0                 0.0                 0.0          0.0     0.0   

    Saldo_Dotacao DataExtracao  
589             0   2025-01-18  

[1 rows x 61 columns]

In [124]:
cols_orcamento = ['Cd_SubFuncao', 'Ds_SubFuncao', 'Cd_Fonte']

cols_orcamento_vl = ['Vl_Orcado_Ano', 'Vl_Orcado_Atualizado', 'Vl_Liquidado']

df_orcamento_original = df_orcamento.copy()
df_orcamento = df_orcamento[cols_orcamento + cols_orcamento_vl]
df_orcamento

Cd_SubFuncao         Ds_SubFuncao Cd_Fonte  Vl_Orcado_Ano  \
589           122  Administração Geral       00            0.0   
590           122  Administração Geral       00            0.0   
591           122  Administração Geral       00            0.0   
592           122  Administração Geral       00            0.0   
593           122  Administração Geral       00         1000.0   
...           ...                  ...      ...            ...   
8946          363  Ensino Profissional       00            0.0   
8947          363  Ensino Profissional       00        10000.0   
8948          363  Ensino Profissional       00            0.0   
8949          363  Ensino Profissional       00        30000.0   
8950          363  Ensino Profissional       00            0.0   

      Vl_Orcado_Atualizado  Vl_Liquidado  
589                   0.00          0.00  
590              100000.00     100000.00  
591               39535.03        657.91  
592                   0.00          0.00  
593                   0.00          0.00  
...                    ...           ...  
8946               1497.82       1497.82  
8947                  0.00          0.00  
8948                  0.00          0.00  
8949                  0.00          0.00  
8950            6081962.83    5763100.00  

[1317 rows x 6 columns]

In [125]:
df_orcamento = df_orcamento.groupby(cols_orcamento).sum().reset_index()
df_orcamento

Cd_SubFuncao                               Ds_SubFuncao Cd_Fonte  \
0           122                        Administração Geral       00   
1           122                        Administração Geral       08   
2           126                   Tecnologia da Informação       00   
3           126                   Tecnologia da Informação       02   
4           128               Formação de Recursos Humanos       00   
5           131                         Comunicação Social       00   
6           271                         Previdência Básica       00   
7           306                     Alimentação e Nutrição       00   
8           306                     Alimentação e Nutrição       02   
9           306                     Alimentação e Nutrição       07   
10          361                         Ensino Fundamental       00   
11          361                         Ensino Fundamental       02   
12          361                         Ensino Fundamental       04   
13          361                         Ensino Fundamental       07   
14          362                               Ensino Médio       00   
15          363                        Ensino Profissional       00   
16          363                        Ensino Profissional       02   
17          363                        Ensino Profissional       05   
18          363                        Ensino Profissional       06   
19          364                            Ensino Superior       00   
20          365                          Educação Infantil       00   
21          365                          Educação Infantil       02   
22          365                          Educação Infantil       04   
23          365                          Educação Infantil       05   
24          366               Educação de Jovens e Adultos       00   
25          367                          Educação Especial       00   
26          368                            Educação Básica       00   
27          368                            Educação Básica       01   
28          368                            Educação Básica       02   
29          368                            Educação Básica       07   
30          368                            Educação Básica       09   
31          422  Direitos Individuais, Coletivos e Difusos       00   
32          422  Direitos Individuais, Coletivos e Difusos       08   
33          451                     Infra-Estrutura Urbana       00   
34          605                              Abastecimento       00   

    Vl_Orcado_Ano  Vl_Orcado_Atualizado  Vl_Liquidado  
0    8.708766e+08          9.518170e+08  8.875335e+08  
1    1.040000e+03          1.040000e+03  0.000000e+00  
2    3.192601e+08          2.779113e+08  2.228363e+08  
3    0.000000e+00          0.000000e+00  0.000000e+00  
4    5.559475e+07          1.753887e+07  1.301020e+07  
5    6.000000e+05          0.000000e+00  0.000000e+00  
6    3.852806e+09          3.770576e+09  3.763374e+09  
7    7.815710e+08          8.811441e+08  6.920816e+08  
8    6.937772e+08          7.857470e+08  6.672718e+08  
9    1.000000e+08          0.000000e+00  0.000000e+00  
10   2.473494e+09          2.807452e+09  2.589409e+09  
11   2.335060e+05          6.639238e+07  6.615888e+07  
12   3.399010e+09          3.736527e+09  3.677769e+09  
13   2.515377e+07          0.000000e+00  0.000000e+00  
14   1.167244e+08          1.146678e+08  1.111567e+08  
15   6.873727e+07          6.833342e+07  6.370979e+07  
16   0.000000e+00          1.402686e+06  1.036800e+03  
17   9.791835e+06          2.634161e+07  6.593838e+06  
18   1.542900e+04          1.542900e+04  0.000000e+00  
19   4.425837e+06          1.733000e+03  0.000000e+00  
20   7.148908e+09          8.332612e+09  8.023122e+09  
21   1.963329e+07          7.298697e+07  5.335368e+07  
22   3.503131e+09          3.962591e+09  3.953724e+09  
23   0.000000e+00          1.197163e+07  2.444382e+06  
24   5.737779e+07          3.257152e+07  2.886

In [126]:
r_agg_cols = ['CÓDIGO_SUBFUNÇÃO', 'CÓDIGO_FONTE']

agg_cols = ['Cd_SubFuncao', 'Cd_Fonte']

df_orcamento_r_agg = (
    df_orcamento_r[r_agg_cols + ['VALOR_DETALHAMENTO_AÇÃO']]
    .groupby(r_agg_cols)
    .sum()
    .reset_index()
)

df_orcamento_r_agg.loc[:, 'VALOR_DETALHAMENTO_AÇÃO'] = (
    df_orcamento_r_agg
    .loc[:, 'VALOR_DETALHAMENTO_AÇÃO']
    .round(2)
)

df_orcamento_ajustado = df_orcamento.merge(
    df_orcamento_r_agg,
    left_on=agg_cols,
    right_on=r_agg_cols,
    how='left'
).drop(columns=r_agg_cols)

df_orcamento_ajustado

Cd_SubFuncao                               Ds_SubFuncao Cd_Fonte  \
0           122                        Administração Geral       00   
1           122                        Administração Geral       08   
2           126                   Tecnologia da Informação       00   
3           126                   Tecnologia da Informação       02   
4           128               Formação de Recursos Humanos       00   
5           131                         Comunicação Social       00   
6           271                         Previdência Básica       00   
7           306                     Alimentação e Nutrição       00   
8           306                     Alimentação e Nutrição       02   
9           306                     Alimentação e Nutrição       07   
10          361                         Ensino Fundamental       00   
11          361                         Ensino Fundamental       02   
12          361                         Ensino Fundamental       04   
13          361                         Ensino Fundamental       07   
14          362                               Ensino Médio       00   
15          363                        Ensino Profissional       00   
16          363                        Ensino Profissional       02   
17          363                        Ensino Profissional       05   
18          363                        Ensino Profissional       06   
19          364                            Ensino Superior       00   
20          365                          Educação Infantil       00   
21          365                          Educação Infantil       02   
22          365                          Educação Infantil       04   
23          365                          Educação Infantil       05   
24          366               Educação de Jovens e Adultos       00   
25          367                          Educação Especial       00   
26          368                            Educação Básica       00   
27          368                            Educação Básica       01   
28          368                            Educação Básica       02   
29          368                            Educação Básica       07   
30          368                            Educação Básica       09   
31          422  Direitos Individuais, Coletivos e Difusos       00   
32          422  Direitos Individuais, Coletivos e Difusos       08   
33          451                     Infra-Estrutura Urbana       00   
34          605                              Abastecimento       00   

    Vl_Orcado_Ano  Vl_Orcado_Atualizado  Vl_Liquidado  VALOR_DETALHAMENTO_AÇÃO  
0    8.708766e+08          9.518170e+08  8.875335e+08             1.266858e+08  
1    1.040000e+03          1.040000e+03  0.000000e+00                      NaN  
2    3.192601e+08          2.779113e+08  2.228363e+08             2.227302e+08  
3    0.000000e+00          0.000000e+00  0.000000e+00                      NaN  
4    5.559475e+07          1.753887e+07  1.301020e+07             1.299294e+07  
5    6.000000e+05          0.000000e+00  0.000000e+00                      NaN  
6    3.852806e+09          3.770576e+09  3.763374e+09             3.763374e+09  
7    7.815710e+08          8.811441e+08  6.920816e+08             6.873529e+08  
8    6.937772e+08          7.857470e+08  6.672718e+08             6.633595e+08  
9    1.000000e+08          0.000000e+00  0.000000e+00                      NaN  
10   2.473494e+09          2.807452e+09  2.589409e+09             9.786926e+08  
11   2.335060e+05          6.639238e+07  6.615888e+07             6.615888e+07  
12   3.399010e+09          3.736527e+09  3.677769e+09                      NaN  
13   2.515377e+07          0.000000e+00  0.000000e+00                      NaN  
14   1.167244e+08          1.146678e+08  1.111567e+08             1.817497e+07  
15   6.873727e+07          6.833342e+07  6.370979e+07             6.239656e+07  
16   0.000000e+00          1.402686e+06  1.036800e+03             1.0

In [127]:
df_orcamento_ajustado.loc[df_orcamento_ajustado['VALOR_DETALHAMENTO_AÇÃO'].isna(), 'VALOR_DETALHAMENTO_AÇÃO'] = 0

df_orcamento_ajustado.loc[:, 'Vl_Liquidado_N_Detalhado'] = (
    df_orcamento_ajustado.loc[:, 'Vl_Liquidado']
    - df_orcamento_ajustado.loc[:, 'VALOR_DETALHAMENTO_AÇÃO']).round(2)

df_orcamento_ajustado

Cd_SubFuncao                               Ds_SubFuncao Cd_Fonte  \
0           122                        Administração Geral       00   
1           122                        Administração Geral       08   
2           126                   Tecnologia da Informação       00   
3           126                   Tecnologia da Informação       02   
4           128               Formação de Recursos Humanos       00   
5           131                         Comunicação Social       00   
6           271                         Previdência Básica       00   
7           306                     Alimentação e Nutrição       00   
8           306                     Alimentação e Nutrição       02   
9           306                     Alimentação e Nutrição       07   
10          361                         Ensino Fundamental       00   
11          361                         Ensino Fundamental       02   
12          361                         Ensino Fundamental       04   
13          361                         Ensino Fundamental       07   
14          362                               Ensino Médio       00   
15          363                        Ensino Profissional       00   
16          363                        Ensino Profissional       02   
17          363                        Ensino Profissional       05   
18          363                        Ensino Profissional       06   
19          364                            Ensino Superior       00   
20          365                          Educação Infantil       00   
21          365                          Educação Infantil       02   
22          365                          Educação Infantil       04   
23          365                          Educação Infantil       05   
24          366               Educação de Jovens e Adultos       00   
25          367                          Educação Especial       00   
26          368                            Educação Básica       00   
27          368                            Educação Básica       01   
28          368                            Educação Básica       02   
29          368                            Educação Básica       07   
30          368                            Educação Básica       09   
31          422  Direitos Individuais, Coletivos e Difusos       00   
32          422  Direitos Individuais, Coletivos e Difusos       08   
33          451                     Infra-Estrutura Urbana       00   
34          605                              Abastecimento       00   

    Vl_Orcado_Ano  Vl_Orcado_Atualizado  Vl_Liquidado  \
0    8.708766e+08          9.518170e+08  8.875335e+08   
1    1.040000e+03          1.040000e+03  0.000000e+00   
2    3.192601e+08          2.779113e+08  2.228363e+08   
3    0.000000e+00          0.000000e+00  0.000000e+00   
4    5.559475e+07          1.753887e+07  1.301020e+07   
5    6.000000e+05          0.000000e+00  0.000000e+00   
6    3.852806e+09          3.770576e+09  3.763374e+09   
7    7.815710e+08          8.811441e+08  6.920816e+08   
8    6.937772e+08          7.857470e+08  6.672718e+08   
9    1.000000e+08          0.000000e+00  0.000000e+00   
10   2.473494e+09          2.807452e+09  2.589409e+09   
11   2.335060e+05          6.639238e+07  6.615888e+07   
12   3.399010e+09          3.736527e+09  3.677769e+09   
13   2.515377e+07          0.000000e+00  0.000000e+00   
14   1.167244e+08          1.146678e+08  1.111567e+08   
15   6.873727e+07          6.833342e+07  6.370979e+07   
16   0.000000e+00          1.402686e+06  1.036800e+03   
17   9.791835e+06          2.634161e+07  6.593838e+06   
18   1.542900e+04          1.542900e+04  0.000000e+00   
19   4.425837e+06          1.733000e+03  0.000000e+00   
20   7.148908e+09          8.332612e+09  8.023122e+09   
21   1.963329e+07          7.298697e+07  5.335368e+07   
22   3.503131e+09          3.962591e+09  3.953724e+09   
23   0.000000e+00          1.197163e+07  2.444382e+06   
24   5.737779e+07    

In [128]:
df_orcamento_ajustado[df_orcamento_ajustado['Vl_Liquidado_N_Detalhado']<0]

Empty DataFrame
Columns: [Cd_SubFuncao, Ds_SubFuncao, Cd_Fonte, Vl_Orcado_Ano, Vl_Orcado_Atualizado, Vl_Liquidado, VALOR_DETALHAMENTO_AÇÃO, Vl_Liquidado_N_Detalhado]
Index: []

In [129]:
df_orcamento_ajustado[['Vl_Liquidado', 'VALOR_DETALHAMENTO_AÇÃO']].sum()

Vl_Liquidado               2.611063e+10
VALOR_DETALHAMENTO_AÇÃO    1.406720e+10
dtype: float64

### Unindo os dados de orçamento

Agora, vamos adicionar os dados não detalhados ao dataframe que contém o orçamento detalhado.

In [130]:
orcamento_cols_map = {'Cd_SubFuncao': 'CÓDIGO_SUBFUNÇÃO',
                      'Ds_SubFuncao': 'DESCRIÇÃO_SUBFUNÇÃO',
                      'Cd_Fonte': 'CÓDIGO_FONTE',
                    #   'Ds_Fonte': 'DESCRIÇÃO_FONTE',
                      'Vl_Liquidado_N_Detalhado': 'Vl_Liquidado'}

df_orcamento_ajustado = (
    df_orcamento_ajustado
    .drop(columns=['VALOR_DETALHAMENTO_AÇÃO', 'Vl_Liquidado'])
    .rename(columns=orcamento_cols_map)
    )

df_orcamento_ajustado

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0               122                        Administração Geral           00   
1               122                        Administração Geral           08   
2               126                   Tecnologia da Informação           00   
3               126                   Tecnologia da Informação           02   
4               128               Formação de Recursos Humanos           00   
5               131                         Comunicação Social           00   
6               271                         Previdência Básica           00   
7               306                     Alimentação e Nutrição           00   
8               306                     Alimentação e Nutrição           02   
9               306                     Alimentação e Nutrição           07   
10              361                         Ensino Fundamental           00   
11              361                         Ensino Fundamental           02   
12              361                         Ensino Fundamental           04   
13              361                         Ensino Fundamental           07   
14              362                               Ensino Médio           00   
15              363                        Ensino Profissional           00   
16              363                        Ensino Profissional           02   
17              363                        Ensino Profissional           05   
18              363                        Ensino Profissional           06   
19              364                            Ensino Superior           00   
20              365                          Educação Infantil           00   
21              365                          Educação Infantil           02   
22              365                          Educação Infantil           04   
23              365                          Educação Infantil           05   
24              366               Educação de Jovens e Adultos           00   
25              367                          Educação Especial           00   
26              368                            Educação Básica           00   
27              368                            Educação Básica           01   
28              368                            Educação Básica           02   
29              368                            Educação Básica           07   
30              368                            Educação Básica           09   
31              422  Direitos Individuais, Coletivos e Difusos           00   
32              422  Direitos Individuais, Coletivos e Difusos           08   
33              451                     Infra-Estrutura Urbana           00   
34              605                              Abastecimento           00   

    Vl_Orcado_Ano  Vl_Orcado_Atualizado  Vl_Liquidado  
0    8.708766e+08          9.518170e+08  7.608477e+08  
1    1.040000e+03          1.040000e+03  0.000000e+00  
2    3.192601e+08          2.779113e+08  1.061554e+05  
3    0.000000e+00          0.000000e+00  0.000000e+00  
4    5.559475e+07          1.753887e+07  1.725730e+04  
5    6.000000e+05          0.000000e+00  0.000000e+00  
6    3.852806e+09          3.770576e+09  3.598400e+02  
7    7.815710e+08          8.811441e+08  4.728664e+06  
8    6.937772e+08          7.857470e+08  3.912249e+06  
9    1.000000e+08          0.000000e+00  0.000000e+00  
10   2.473494e+09          2.807452e+09  1.610717e+09  
11   2.335060e+05          6.639238e+07  0.000000e+00  
12   3.399010e+09          3.736527e+09  3.677769e+09  
13   2.515377e+07          0.000000e+00  0.000000e+00  
14   1.167244e+08          1.146678e+08  9.298178e+07  
15   6.873727e+07          6.833342e+07  1.313235e+06  
16   0.000000e+00          1.402686e+06  0.000000e+00  
17   9.791835e+06          2.634161e+07  3.224095e+05  
18   1.542900e+04          1.542900e+04  0.000000e+00  
19   4.425837e+06          1.733000e+0

In [131]:
df_orcamento_r = (df_orcamento_r
                  .rename(columns={'VALOR_DETALHAMENTO_AÇÃO': 'Vl_Liquidado'}))

df_orcamento_r

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                122  Administração Geral           00          Centro   
1                122  Administração Geral           00           Oeste   
2                122  Administração Geral           00             Sul   
3                122  Administração Geral           00             Sul   
4                122  Administração Geral           00  Supra-Regional   
..               ...                  ...          ...             ...   
278              368      Educação Básica           00             Sul   
279              368      Educação Básica           00             Sul   
280              368      Educação Básica           00             Sul   
281              368      Educação Básica           00  Supra-Regional   
282              368      Educação Básica           02  Supra-Regional   

                  SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  Vl_Liquidado  \
0    Supra Subprefeitura Centro      Despesa Regionalizável  1.818885e+06   
1            Subprefeitura Lapa      Despesa Regionalizável  8.227545e+05   
2        Subprefeitura Ipiranga      Despesa Regionalizável  6.646144e+04   
3    Subprefeitura Vila Mariana      Despesa Regionalizável  2.680670e+04   
4           Supra Subprefeitura  Despesa Não-Regionalizável  1.239509e+08   
..                          ...                         ...           ...   
278   Subprefeitura Santo Amaro      Despesa Regionalizável  7.164826e+05   
279  Subprefeitura Vila Mariana      Despesa Regionalizável  2.676908e+06   
280     Supra Subprefeitura Sul      Despesa Regionalizável  3.167627e+07   
281         Supra Subprefeitura  Despesa Não-Regionalizável  2.151326e+08   
282         Supra Subprefeitura  Despesa Não-Regionalizável  1.431150e+07   

    NIVEL_REGIONALIZAÇÃO  
0                 Região  
1          Subprefeitura  
2          Subprefeitura  
3          Subprefeitura  
4     Não regionalizável  
..                   ...  
278        Subprefeitura  
279        Subprefeitura  
280               Região  
281   Não regionalizável  
282   Não regionalizável  

[283 rows x 8 columns]

In [132]:
df_orcamento_final = pd.concat([df_orcamento_r, df_orcamento_ajustado])

df_orcamento_final

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0               122                        Administração Geral           00   
1               122                        Administração Geral           00   
2               122                        Administração Geral           00   
3               122                        Administração Geral           00   
4               122                        Administração Geral           00   
..              ...                                        ...          ...   
30              368                            Educação Básica           09   
31              422  Direitos Individuais, Coletivos e Difusos           00   
32              422  Direitos Individuais, Coletivos e Difusos           08   
33              451                     Infra-Estrutura Urbana           00   
34              605                              Abastecimento           00   

            REGIÃO               SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0           Centro  Supra Subprefeitura Centro      Despesa Regionalizável   
1            Oeste          Subprefeitura Lapa      Despesa Regionalizável   
2              Sul      Subprefeitura Ipiranga      Despesa Regionalizável   
3              Sul  Subprefeitura Vila Mariana      Despesa Regionalizável   
4   Supra-Regional         Supra Subprefeitura  Despesa Não-Regionalizável   
..             ...                         ...                         ...   
30             NaN                         NaN                         NaN   
31             NaN                         NaN                         NaN   
32             NaN                         NaN                         NaN   
33             NaN                         NaN                         NaN   
34             NaN                         NaN                         NaN   

    Vl_Liquidado NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  Vl_Orcado_Atualizado  
0   1.818885e+06               Região            NaN                   NaN  
1   8.227545e+05        Subprefeitura            NaN                   NaN  
2   6.646144e+04        Subprefeitura            NaN                   NaN  
3   2.680670e+04        Subprefeitura            NaN                   NaN  
4   1.239509e+08   Não regionalizável            NaN                   NaN  
..           ...                  ...            ...                   ...  
30  0.000000e+00                  NaN         2000.0                2000.0  
31  0.000000e+00                  NaN       900000.0                   0.0  
32  0.000000e+00                  NaN     23000000.0            20150000.0  
33  0.000000e+00                  NaN         1000.0                   0.0  
34  0.000000e+00                  NaN      1151753.0                   0.0  

[318 rows x 10 columns]

In [133]:
df_orcamento_final.loc[df_orcamento_final['Vl_Orcado_Ano'].isna(),
                       'Vl_Orcado_Ano'] = 0
df_orcamento_final.loc[df_orcamento_final['Vl_Orcado_Atualizado'].isna(),
                       'Vl_Orcado_Atualizado'] = 0
df_orcamento_final.loc[df_orcamento_final['NIVEL_REGIONALIZAÇÃO'].isna(),
                       'NIVEL_REGIONALIZAÇÃO'] = 'Não detalhado'

df_orcamento_final

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0               122                        Administração Geral           00   
1               122                        Administração Geral           00   
2               122                        Administração Geral           00   
3               122                        Administração Geral           00   
4               122                        Administração Geral           00   
..              ...                                        ...          ...   
30              368                            Educação Básica           09   
31              422  Direitos Individuais, Coletivos e Difusos           00   
32              422  Direitos Individuais, Coletivos e Difusos           08   
33              451                     Infra-Estrutura Urbana           00   
34              605                              Abastecimento           00   

            REGIÃO               SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0           Centro  Supra Subprefeitura Centro      Despesa Regionalizável   
1            Oeste          Subprefeitura Lapa      Despesa Regionalizável   
2              Sul      Subprefeitura Ipiranga      Despesa Regionalizável   
3              Sul  Subprefeitura Vila Mariana      Despesa Regionalizável   
4   Supra-Regional         Supra Subprefeitura  Despesa Não-Regionalizável   
..             ...                         ...                         ...   
30             NaN                         NaN                         NaN   
31             NaN                         NaN                         NaN   
32             NaN                         NaN                         NaN   
33             NaN                         NaN                         NaN   
34             NaN                         NaN                         NaN   

    Vl_Liquidado NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  Vl_Orcado_Atualizado  
0   1.818885e+06               Região            0.0                   0.0  
1   8.227545e+05        Subprefeitura            0.0                   0.0  
2   6.646144e+04        Subprefeitura            0.0                   0.0  
3   2.680670e+04        Subprefeitura            0.0                   0.0  
4   1.239509e+08   Não regionalizável            0.0                   0.0  
..           ...                  ...            ...                   ...  
30  0.000000e+00        Não detalhado         2000.0                2000.0  
31  0.000000e+00        Não detalhado       900000.0                   0.0  
32  0.000000e+00        Não detalhado     23000000.0            20150000.0  
33  0.000000e+00        Não detalhado         1000.0                   0.0  
34  0.000000e+00        Não detalhado      1151753.0                   0.0  

[318 rows x 10 columns]

### Padronizando os nomes de subprefeituras

In [134]:
subs_orcamento = (
    df_orcamento_final.loc[~df_orcamento_final['SUBPREFEITURA'].isna(), 'SUBPREFEITURA']
    .apply(unidecode)
    .unique()
    .tolist()
)

subs_orcamento.sort()

subs_orcamento

['Subprefeitura Aricanduva/Formosa/Carrao',
 'Subprefeitura Butanta',
 'Subprefeitura Campo Limpo',
 'Subprefeitura Capela do Socorro',
 'Subprefeitura Casa Verde/Cachoeirinha',
 'Subprefeitura Cidade Ademar',
 'Subprefeitura Cidade Tiradentes',
 'Subprefeitura Ermelino Matarazzo',
 'Subprefeitura Freguesia/Brasilandia',
 'Subprefeitura Ipiranga',
 'Subprefeitura Itaim Paulista',
 'Subprefeitura Itaquera',
 'Subprefeitura Jabaquara',
 'Subprefeitura Jacana/Tremembe',
 'Subprefeitura Lapa',
 "Subprefeitura M'Boi Mirim",
 'Subprefeitura Mooca',
 'Subprefeitura Parelheiros',
 'Subprefeitura Penha',
 'Subprefeitura Perus/Anhanguera',
 'Subprefeitura Pinheiros',
 'Subprefeitura Pirituba/Jaragua',
 'Subprefeitura Santana/Tucuruvi',
 'Subprefeitura Santo Amaro',
 'Subprefeitura Sao Mateus',
 'Subprefeitura Sao Miguel Paulista',
 'Subprefeitura Sapopemba',
 'Subprefeitura Se',
 'Subprefeitura Vila Maria/Vila Guilherme',
 'Subprefeitura Vila Mariana',
 'Subprefeitura de Guaianases',
 'Subprefei

In [135]:
subs_orcamento[:-6]

['Subprefeitura Aricanduva/Formosa/Carrao',
 'Subprefeitura Butanta',
 'Subprefeitura Campo Limpo',
 'Subprefeitura Capela do Socorro',
 'Subprefeitura Casa Verde/Cachoeirinha',
 'Subprefeitura Cidade Ademar',
 'Subprefeitura Cidade Tiradentes',
 'Subprefeitura Ermelino Matarazzo',
 'Subprefeitura Freguesia/Brasilandia',
 'Subprefeitura Ipiranga',
 'Subprefeitura Itaim Paulista',
 'Subprefeitura Itaquera',
 'Subprefeitura Jabaquara',
 'Subprefeitura Jacana/Tremembe',
 'Subprefeitura Lapa',
 "Subprefeitura M'Boi Mirim",
 'Subprefeitura Mooca',
 'Subprefeitura Parelheiros',
 'Subprefeitura Penha',
 'Subprefeitura Perus/Anhanguera',
 'Subprefeitura Pinheiros',
 'Subprefeitura Pirituba/Jaragua',
 'Subprefeitura Santana/Tucuruvi',
 'Subprefeitura Santo Amaro',
 'Subprefeitura Sao Mateus',
 'Subprefeitura Sao Miguel Paulista',
 'Subprefeitura Sapopemba',
 'Subprefeitura Se',
 'Subprefeitura Vila Maria/Vila Guilherme',
 'Subprefeitura Vila Mariana',
 'Subprefeitura de Guaianases',
 'Subprefei

In [136]:
len(subs_orcamento[:-6])

32

In [137]:
subs_qlik = df_subs_qlik['sub.NOME'].unique().tolist()
subs_qlik.sort()
subs_qlik

['ARICANDUVA-FORMOSA-CARRAO',
 'BUTANTA',
 'CAMPO LIMPO',
 'CAPELA DO SOCORRO',
 'CASA VERDE-CACHOEIRINHA',
 'CIDADE ADEMAR',
 'CIDADE TIRADENTES',
 'ERMELINO MATARAZZO',
 'FREGUESIA-BRASILANDIA',
 'GUAIANASES',
 'IPIRANGA',
 'ITAIM PAULISTA',
 'ITAQUERA',
 'JABAQUARA',
 'JACANA-TREMEMBE',
 'LAPA',
 'M BOI MIRIM',
 'MOOCA',
 'PARELHEIROS',
 'PENHA',
 'PERUS',
 'PINHEIROS',
 'PIRITUBA-JARAGUA',
 'SANTANA-TUCURUVI',
 'SANTO AMARO',
 'SAO MATEUS',
 'SAO MIGUEL',
 'SAPOPEMBA',
 'SE',
 'VILA MARIA-VILA GUILHERME',
 'VILA MARIANA',
 'VILA PRUDENTE']

In [138]:
subs_qlik_orcamento = subs_qlik.copy()
# Guainases e Vila Prudente aparecem em uma ordenação diferente, por isso serão
# removidas e adicionadas novamente ao final da lista
subs_qlik_orcamento.remove('GUAIANASES')
subs_qlik_orcamento.remove('VILA PRUDENTE')
subs_qlik_orcamento.append('GUAIANASES')
subs_qlik_orcamento.append('VILA PRUDENTE')

In [139]:
mapper_orcamento = {
    so: sq
    for so, sq in zip(subs_orcamento, subs_qlik_orcamento)
}

mapper_orcamento

{'Subprefeitura Aricanduva/Formosa/Carrao': 'ARICANDUVA-FORMOSA-CARRAO',
 'Subprefeitura Butanta': 'BUTANTA',
 'Subprefeitura Campo Limpo': 'CAMPO LIMPO',
 'Subprefeitura Capela do Socorro': 'CAPELA DO SOCORRO',
 'Subprefeitura Casa Verde/Cachoeirinha': 'CASA VERDE-CACHOEIRINHA',
 'Subprefeitura Cidade Ademar': 'CIDADE ADEMAR',
 'Subprefeitura Cidade Tiradentes': 'CIDADE TIRADENTES',
 'Subprefeitura Ermelino Matarazzo': 'ERMELINO MATARAZZO',
 'Subprefeitura Freguesia/Brasilandia': 'FREGUESIA-BRASILANDIA',
 'Subprefeitura Ipiranga': 'IPIRANGA',
 'Subprefeitura Itaim Paulista': 'ITAIM PAULISTA',
 'Subprefeitura Itaquera': 'ITAQUERA',
 'Subprefeitura Jabaquara': 'JABAQUARA',
 'Subprefeitura Jacana/Tremembe': 'JACANA-TREMEMBE',
 'Subprefeitura Lapa': 'LAPA',
 "Subprefeitura M'Boi Mirim": 'M BOI MIRIM',
 'Subprefeitura Mooca': 'MOOCA',
 'Subprefeitura Parelheiros': 'PARELHEIROS',
 'Subprefeitura Penha': 'PENHA',
 'Subprefeitura Perus/Anhanguera': 'PERUS',
 'Subprefeitura Pinheiros': 'PINHEI

In [140]:
df_orcamento_final.insert(
    7,
    'sub.NOME',
    df_orcamento_final.loc[:,'SUBPREFEITURA'].apply(lambda s: unidecode(s) if isinstance(s, str) else None).map(mapper_orcamento)
)

df_orcamento_final

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0               122                        Administração Geral           00   
1               122                        Administração Geral           00   
2               122                        Administração Geral           00   
3               122                        Administração Geral           00   
4               122                        Administração Geral           00   
..              ...                                        ...          ...   
30              368                            Educação Básica           09   
31              422  Direitos Individuais, Coletivos e Difusos           00   
32              422  Direitos Individuais, Coletivos e Difusos           08   
33              451                     Infra-Estrutura Urbana           00   
34              605                              Abastecimento           00   

            REGIÃO               SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  \
0           Centro  Supra Subprefeitura Centro      Despesa Regionalizável   
1            Oeste          Subprefeitura Lapa      Despesa Regionalizável   
2              Sul      Subprefeitura Ipiranga      Despesa Regionalizável   
3              Sul  Subprefeitura Vila Mariana      Despesa Regionalizável   
4   Supra-Regional         Supra Subprefeitura  Despesa Não-Regionalizável   
..             ...                         ...                         ...   
30             NaN                         NaN                         NaN   
31             NaN                         NaN                         NaN   
32             NaN                         NaN                         NaN   
33             NaN                         NaN                         NaN   
34             NaN                         NaN                         NaN   

    Vl_Liquidado      sub.NOME NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  \
0   1.818885e+06           NaN               Região            0.0   
1   8.227545e+05          LAPA        Subprefeitura            0.0   
2   6.646144e+04      IPIRANGA        Subprefeitura            0.0   
3   2.680670e+04  VILA MARIANA        Subprefeitura            0.0   
4   1.239509e+08           NaN   Não regionalizável            0.0   
..           ...           ...                  ...            ...   
30  0.000000e+00           NaN        Não detalhado         2000.0   
31  0.000000e+00           NaN        Não detalhado       900000.0   
32  0.000000e+00           NaN        Não detalhado     23000000.0   
33  0.000000e+00           NaN        Não detalhado         1000.0   
34  0.000000e+00           NaN        Não detalhado      1151753.0   

    Vl_Orcado_Atualizado  
0                    0.0  
1                    0.0  
2                    0.0  
3                    0.0  
4                    0.0  
..                   ...  
30                2000.0  
31                   0.0  
32            20150000.0  
33                   0.0  
34                   0.0  

[318 rows x 11 columns]

### Adicionando as subprefeituras faltantes

In [141]:
orcamento_subs_cols = ['CÓDIGO_SUBFUNÇÃO', 'DESCRIÇÃO_SUBFUNÇÃO',
                       'CÓDIGO_FONTE']

df_orcamento_subs = df_orcamento_final[orcamento_subs_cols].copy()
df_orcamento_subs = df_orcamento_subs.drop_duplicates().reset_index(drop=True)
df_orcamento_subs

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE
0               122                        Administração Geral           00
1               126                   Tecnologia da Informação           00
2               128               Formação de Recursos Humanos           00
3               271                         Previdência Básica           00
4               306                     Alimentação e Nutrição           00
5               306                     Alimentação e Nutrição           02
6               361                         Ensino Fundamental           00
7               361                         Ensino Fundamental           02
8               362                               Ensino Médio           00
9               363                        Ensino Profissional           00
10              363                        Ensino Profissional           02
11              363                        Ensino Profissional           05
12              365                          Educação Infantil           00
13              365                          Educação Infantil           02
14              365                          Educação Infantil           05
15              366               Educação de Jovens e Adultos           00
16              367                          Educação Especial           00
17              368                            Educação Básica           00
18              368                            Educação Básica           02
19              122                        Administração Geral           08
20              126                   Tecnologia da Informação           02
21              131                         Comunicação Social           00
22              306                     Alimentação e Nutrição           07
23              361                         Ensino Fundamental           04
24              361                         Ensino Fundamental           07
25              363                        Ensino Profissional           06
26              364                            Ensino Superior           00
27              365                          Educação Infantil           04
28              368                            Educação Básica           01
29              368                            Educação Básica           07
30              368                            Educação Básica           09
31              422  Direitos Individuais, Coletivos e Difusos           00
32              422  Direitos Individuais, Coletivos e Difusos           08
33              451                     Infra-Estrutura Urbana           00
34              605                              Abastecimento           00

In [142]:
df_orcamento_subs['TIPO_REGIONALIZAÇÃO'] = 'Despesa Regionalizável'
df_orcamento_subs['NIVEL_REGIONALIZAÇÃO'] = 'Subprefeitura'

df_orcamento_subs

CÓDIGO_SUBFUNÇÃO                        DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0               122                        Administração Geral           00   
1               126                   Tecnologia da Informação           00   
2               128               Formação de Recursos Humanos           00   
3               271                         Previdência Básica           00   
4               306                     Alimentação e Nutrição           00   
5               306                     Alimentação e Nutrição           02   
6               361                         Ensino Fundamental           00   
7               361                         Ensino Fundamental           02   
8               362                               Ensino Médio           00   
9               363                        Ensino Profissional           00   
10              363                        Ensino Profissional           02   
11              363                        Ensino Profissional           05   
12              365                          Educação Infantil           00   
13              365                          Educação Infantil           02   
14              365                          Educação Infantil           05   
15              366               Educação de Jovens e Adultos           00   
16              367                          Educação Especial           00   
17              368                            Educação Básica           00   
18              368                            Educação Básica           02   
19              122                        Administração Geral           08   
20              126                   Tecnologia da Informação           02   
21              131                         Comunicação Social           00   
22              306                     Alimentação e Nutrição           07   
23              361                         Ensino Fundamental           04   
24              361                         Ensino Fundamental           07   
25              363                        Ensino Profissional           06   
26              364                            Ensino Superior           00   
27              365                          Educação Infantil           04   
28              368                            Educação Básica           01   
29              368                            Educação Básica           07   
30              368                            Educação Básica           09   
31              422  Direitos Individuais, Coletivos e Difusos           00   
32              422  Direitos Individuais, Coletivos e Difusos           08   
33              451                     Infra-Estrutura Urbana           00   
34              605                              Abastecimento           00   

       TIPO_REGIONALIZAÇÃO NIVEL_REGIONALIZAÇÃO  
0   Despesa Regionalizável        Subprefeitura  
1   Despesa Regionalizável        Subprefeitura  
2   Despesa Regionalizável        Subprefeitura  
3   Despesa Regionalizável        Subprefeitura  
4   Despesa Regionalizável        Subprefeitura  
5   Despesa Regionalizável        Subprefeitura  
6   Despesa Regionalizável        Subprefeitura  
7   Despesa Regionalizável        Subprefeitura  
8   Despesa Regionalizável        Subprefeitura  
9   Despesa Regionalizável        Subprefeitura  
10  Despesa Regionalizável        Subprefeitura  
11  Despesa Regionalizável        Subprefeitura  
12  Despesa Regionalizável        Subprefeitura  
13  Despesa Regionalizável        Subprefeitura  
14  Despesa Regionalizável        Subprefeitura  
15  Despesa Regionalizável        Subprefeitura  
16  Despesa Regionalizável        Subprefeitura  
17  Despesa Regionalizável        Subprefeitura  
18  Despesa Regionalizável        Subprefeitura  
19  Despesa Regionalizável        Subprefeitura  
20  Despesa Regionalizável        Subprefeitura  
21  Despesa Regionalizável        Subprefeitura  
22  Desp

In [143]:
df_orcamento_subs = (
    df_orcamento_subs
    .merge(pd.DataFrame(columns=['sub.NOME'], data=subs_qlik),
           how='cross')
)

df_orcamento_subs

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE  \
0                 122  Administração Geral           00   
1                 122  Administração Geral           00   
2                 122  Administração Geral           00   
3                 122  Administração Geral           00   
4                 122  Administração Geral           00   
...               ...                  ...          ...   
1115              605        Abastecimento           00   
1116              605        Abastecimento           00   
1117              605        Abastecimento           00   
1118              605        Abastecimento           00   
1119              605        Abastecimento           00   

         TIPO_REGIONALIZAÇÃO NIVEL_REGIONALIZAÇÃO                   sub.NOME  
0     Despesa Regionalizável        Subprefeitura  ARICANDUVA-FORMOSA-CARRAO  
1     Despesa Regionalizável        Subprefeitura                    BUTANTA  
2     Despesa Regionalizável        Subprefeitura                CAMPO LIMPO  
3     Despesa Regionalizável        Subprefeitura          CAPELA DO SOCORRO  
4     Despesa Regionalizável        Subprefeitura    CASA VERDE-CACHOEIRINHA  
...                      ...                  ...                        ...  
1115  Despesa Regionalizável        Subprefeitura                  SAPOPEMBA  
1116  Despesa Regionalizável        Subprefeitura                         SE  
1117  Despesa Regionalizável        Subprefeitura  VILA MARIA-VILA GUILHERME  
1118  Despesa Regionalizável        Subprefeitura               VILA MARIANA  
1119  Despesa Regionalizável        Subprefeitura              VILA PRUDENTE  

[1120 rows x 6 columns]

In [144]:
df_orcamento_completo = (
    df_orcamento_final
    .merge(df_orcamento_subs,
           how='outer',
           on=df_orcamento_subs.columns.tolist())
)

df_orcamento_completo

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                 122  Administração Geral           00  Supra-Regional   
1                 122  Administração Geral           00          Centro   
2                 122  Administração Geral           00             NaN   
3                 122  Administração Geral           00             NaN   
4                 122  Administração Geral           00             NaN   
...               ...                  ...          ...             ...   
1212              605        Abastecimento           00             NaN   
1213              605        Abastecimento           00             NaN   
1214              605        Abastecimento           00             NaN   
1215              605        Abastecimento           00             NaN   
1216              605        Abastecimento           00             NaN   

                   SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  Vl_Liquidado  \
0            Supra Subprefeitura  Despesa Não-Regionalizável  1.239509e+08   
1     Supra Subprefeitura Centro      Despesa Regionalizável  1.818885e+06   
2                            NaN      Despesa Regionalizável           NaN   
3                            NaN      Despesa Regionalizável           NaN   
4                            NaN      Despesa Regionalizável           NaN   
...                          ...                         ...           ...   
1212                         NaN      Despesa Regionalizável           NaN   
1213                         NaN      Despesa Regionalizável           NaN   
1214                         NaN      Despesa Regionalizável           NaN   
1215                         NaN      Despesa Regionalizável           NaN   
1216                         NaN                         NaN  0.000000e+00   

                       sub.NOME NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  \
0                           NaN   Não regionalizável            0.0   
1                           NaN               Região            0.0   
2     ARICANDUVA-FORMOSA-CARRAO        Subprefeitura            NaN   
3                       BUTANTA        Subprefeitura            NaN   
4                   CAMPO LIMPO        Subprefeitura            NaN   
...                         ...                  ...            ...   
1212                         SE        Subprefeitura            NaN   
1213  VILA MARIA-VILA GUILHERME        Subprefeitura            NaN   
1214               VILA MARIANA        Subprefeitura            NaN   
1215              VILA PRUDENTE        Subprefeitura            NaN   
1216                        NaN        Não detalhado      1151753.0   

      Vl_Orcado_Atualizado  
0                      0.0  
1                      0.0  
2                      NaN  
3                      NaN  
4                      NaN  
...                    ...  
1212                   NaN  
1213                   NaN  
1214                   NaN  
1215                   NaN  
1216                   0.0  

[1217 rows x 11 columns]

In [145]:
df_orcamento_completo.loc[df_orcamento_completo['Vl_Liquidado'].isna(), 'Vl_Liquidado'] = 0
df_orcamento_completo.loc[df_orcamento_completo['Vl_Orcado_Ano'].isna(), 'Vl_Orcado_Ano'] = 0
df_orcamento_completo.loc[df_orcamento_completo['Vl_Orcado_Atualizado'].isna(), 'Vl_Orcado_Atualizado'] = 0

df_orcamento_completo

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                 122  Administração Geral           00  Supra-Regional   
1                 122  Administração Geral           00          Centro   
2                 122  Administração Geral           00             NaN   
3                 122  Administração Geral           00             NaN   
4                 122  Administração Geral           00             NaN   
...               ...                  ...          ...             ...   
1212              605        Abastecimento           00             NaN   
1213              605        Abastecimento           00             NaN   
1214              605        Abastecimento           00             NaN   
1215              605        Abastecimento           00             NaN   
1216              605        Abastecimento           00             NaN   

                   SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  Vl_Liquidado  \
0            Supra Subprefeitura  Despesa Não-Regionalizável  1.239509e+08   
1     Supra Subprefeitura Centro      Despesa Regionalizável  1.818885e+06   
2                            NaN      Despesa Regionalizável  0.000000e+00   
3                            NaN      Despesa Regionalizável  0.000000e+00   
4                            NaN      Despesa Regionalizável  0.000000e+00   
...                          ...                         ...           ...   
1212                         NaN      Despesa Regionalizável  0.000000e+00   
1213                         NaN      Despesa Regionalizável  0.000000e+00   
1214                         NaN      Despesa Regionalizável  0.000000e+00   
1215                         NaN      Despesa Regionalizável  0.000000e+00   
1216                         NaN                         NaN  0.000000e+00   

                       sub.NOME NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  \
0                           NaN   Não regionalizável            0.0   
1                           NaN               Região            0.0   
2     ARICANDUVA-FORMOSA-CARRAO        Subprefeitura            0.0   
3                       BUTANTA        Subprefeitura            0.0   
4                   CAMPO LIMPO        Subprefeitura            0.0   
...                         ...                  ...            ...   
1212                         SE        Subprefeitura            0.0   
1213  VILA MARIA-VILA GUILHERME        Subprefeitura            0.0   
1214               VILA MARIANA        Subprefeitura            0.0   
1215              VILA PRUDENTE        Subprefeitura            0.0   
1216                        NaN        Não detalhado      1151753.0   

      Vl_Orcado_Atualizado  
0                      0.0  
1                      0.0  
2                      0.0  
3                      0.0  
4                      0.0  
...                    ...  
1212                   0.0  
1213                   0.0  
1214                   0.0  
1215                   0.0  
1216                   0.0  

[1217 rows x 11 columns]

### Adicionando descrição das vinculações

In [146]:
df_orcamento_completo = (
    df_orcamento_completo
    .merge(df_orcamento_original[['Cd_Fonte', 'Ds_Fonte']].drop_duplicates(),
            how='left',
            left_on='CÓDIGO_FONTE',
            right_on='Cd_Fonte')
    .drop(columns='Cd_Fonte')
)

df_orcamento_completo

CÓDIGO_SUBFUNÇÃO  DESCRIÇÃO_SUBFUNÇÃO CÓDIGO_FONTE          REGIÃO  \
0                 122  Administração Geral           00  Supra-Regional   
1                 122  Administração Geral           00          Centro   
2                 122  Administração Geral           00             NaN   
3                 122  Administração Geral           00             NaN   
4                 122  Administração Geral           00             NaN   
...               ...                  ...          ...             ...   
1212              605        Abastecimento           00             NaN   
1213              605        Abastecimento           00             NaN   
1214              605        Abastecimento           00             NaN   
1215              605        Abastecimento           00             NaN   
1216              605        Abastecimento           00             NaN   

                   SUBPREFEITURA         TIPO_REGIONALIZAÇÃO  Vl_Liquidado  \
0            Supra Subprefeitura  Despesa Não-Regionalizável  1.239509e+08   
1     Supra Subprefeitura Centro      Despesa Regionalizável  1.818885e+06   
2                            NaN      Despesa Regionalizável  0.000000e+00   
3                            NaN      Despesa Regionalizável  0.000000e+00   
4                            NaN      Despesa Regionalizável  0.000000e+00   
...                          ...                         ...           ...   
1212                         NaN      Despesa Regionalizável  0.000000e+00   
1213                         NaN      Despesa Regionalizável  0.000000e+00   
1214                         NaN      Despesa Regionalizável  0.000000e+00   
1215                         NaN      Despesa Regionalizável  0.000000e+00   
1216                         NaN                         NaN  0.000000e+00   

                       sub.NOME NIVEL_REGIONALIZAÇÃO  Vl_Orcado_Ano  \
0                           NaN   Não regionalizável            0.0   
1                           NaN               Região            0.0   
2     ARICANDUVA-FORMOSA-CARRAO        Subprefeitura            0.0   
3                       BUTANTA        Subprefeitura            0.0   
4                   CAMPO LIMPO        Subprefeitura            0.0   
...                         ...                  ...            ...   
1212                         SE        Subprefeitura            0.0   
1213  VILA MARIA-VILA GUILHERME        Subprefeitura            0.0   
1214               VILA MARIANA        Subprefeitura            0.0   
1215              VILA PRUDENTE        Subprefeitura            0.0   
1216                        NaN        Não detalhado      1151753.0   

      Vl_Orcado_Atualizado           Ds_Fonte  
0                      0.0  Tesouro Municipal  
1                      0.0  Tesouro Municipal  
2                      0.0  Tesouro Municipal  
3                      0.0  Tesouro Municipal  
4                      0.0  Tesouro Municipal  
...                    ...                ...  
1212                   0.0  Tesouro Municipal  
1213                   0.0  Tesouro Municipal  
1214                   0.0  Tesouro Municipal  
1215                   0.0  Tesouro Municipal  
1216                   0.0  Tesouro Municipal  

[1217 rows x 12 columns]

# Armazenamento dos dados

Finalmente, salvamos os arquivos como csv para utilizarmos no Qlik Sense.

In [147]:
base_path = os.path.join('data_output', 'educacao')

if not os.path.exists(base_path):
    os.makedirs(base_path)

for name, df in [('demanda e matriculas', mat_24),
                 ('servidores-perfil', perf_24),
                 ('escolas-municipais', escolas_24),
                 ('perfil-dos-educandos', alunos_24),
                 ('educandos-estrangeiros', alunos_est_2024),
                 ('beneficiarios-pbf', alunos_bf_2024),
                 ('nivel-padronizado', nivel_padronizado),
                 ('orcamento', df_orcamento_completo)]:
    
    filepath = os.path.join(base_path, f'{name}.csv')

    df.to_csv(filepath,
              index=False,
              sep=';',
              decimal=',',
              encoding='utf-8')